357 check error

In [1]:
%reset

Once deleted, variables cannot be recovered. Proceed (y/[n])? y


https://stackabuse.com/python-for-nlp-getting-started-with-the-stanfordcorenlp-library/ <br>
https://github.com/Lynten/stanford-corenlp

https://towardsdatascience.com/a-practitioners-guide-to-natural-language-processing-part-i-processing-understanding-text-9f4abfd13e72

In [2]:
# %reset -f

In [1]:
from stanfordcorenlp import StanfordCoreNLP
import logging
import json
import pandas as pd
# from nltk.parse.stanford import StanfordDependencyParser
import os
import numpy as np
from graphviz import Source


### 1. StanfordNLP Parser connecting to server

In [2]:
class StanfordNLP:
    def __init__(self, host='http://localhost', port=9000):
        self.nlp = StanfordCoreNLP(host, port=port,
                                   timeout=30000)  # , quiet=False, logging_level=logging.DEBUG)
        self.props = {
            'annotators': 'tokenize,ssplit,pos,lemma,ner,parse,depparse,dcoref,relation',
            'pipelineLanguage': 'en',
            'outputFormat': 'json'
        }

    def word_tokenize(self, sentence):
        return self.nlp.word_tokenize(sentence)

    def pos(self, sentence):
        return self.nlp.pos_tag(sentence)

    def ner(self, sentence):
        return self.nlp.ner(sentence)

    def parse(self, sentence):
        return self.nlp.parse(sentence)

    def dependency_parse(self, sentence):
        return self.nlp.dependency_parse(sentence)

    def annotate(self, sentence):
        return json.loads(self.nlp.annotate(sentence, properties=self.props))

    @staticmethod
    def tokens_to_dict(_tokens):
        tokens = defaultdict(dict)
        for token in _tokens:
            tokens[int(token['index'])] = {
                'word': token['word'],
                'lemma': token['lemma'],
                'pos': token['pos'],
                'ner': token['ner']
            }
        return tokens

In [3]:
#allow full data view
pd.set_option('display.max_colwidth', -1)

### 2. Retrieving data from CSV

In [4]:
df = pd.read_csv('newsdataset1.csv')
df['event_summary']=df.event_summary.astype(str)


In [5]:
# df=df.rename(columns={"event_summary": "summary"})

In [6]:
df

Unnamed: 0  index        date                     category  \
0      0           0      2016-01-01  Armed conflicts and attacks   
1      1           2      2016-01-01  Disasters and Incidents       
2      2           3      2016-01-01  International Relations       
3      3           4      2016-01-01  Crime and Law                 
4      4           7      2016-01-02  Armed conflicts and attacks   
...   ..          ..             ...                          ...   
10419  10419       14422  2019-04-29  Politics and Elections        
10420  10420       14423  2019-04-29  Politics and Elections        
10421  10421       14424  2019-04-30  Arts and culture              
10422  10422       14427  2019-04-30  Business and Economy          
10423  10423       14430  2019-04-30  Politics and Elections        

                             event_title  \
0      IsraeliE28093Palestinian conflict   
1      FALSE                               
2      FALSE                               
3      FALSE                               
4      Mexican Drug War                    
...                 ...                    
10419  FALSE                               
10420  FALSE                               
10421  2019 Japanese imperial transition   
10422  FALSE                               
10423  2019 Venezuela uprising             

                                                                                                                                                                                                              event_summary  \
0      A shooting takes place at a pub in Tel Aviv                                                                                                                                                                            
1      About one thousand houses in Manila's Tondo district in the Philippines are set ablaze following New Year's Eve firecracker festivities that left one dead and 380 others injured. AP via CTV News                     
2      The EU-Ukraine Free Trade deal officially comes into force                                                                                                                                                             
3      The two-child policy takes effect in China                                                                                                                                                                             
4      /wiki/List_of_politicians_killed_in_the_Mexican_Drug_War                                                                                                                                                               
...                                                         ...                                                                                                                                                               
10419  Indonesian President Joko Widodo has decided to relocate the nation's capital from Jakarta                                                                                                                             
10420  U.S. Deputy Attorney General Rod Rosenstein  announces he will resign                                                                                                                                                  
10421  Emperor Akihito abdicates the Chrysanthemum Throne in favor of his elder son                                                                                                                                           
10422  U.S. Attorney General William Barr has decided to recuse himself from deliberations about whether the Antitrust Division of the U.S. Justice Department ought to challenge the planned merger of T-Mobile and Sprint   
10423  /wiki/2019_Venezuelan_presidential_crisis                                                                                                                                                    

In [7]:
# df['event_summary'] = df['summary'].astype(str) + df['entities']+df['person']

In [8]:
df.count()

Unnamed: 0       10424
index            10424
date             10424
category         10424
event_title      10424
event_summary    10424
entities         10175
person           10006
external_link    9882 
dtype: int64

### 3. Cleaning Data

In [9]:
df.replace('', np.nan, inplace=True)
df.fillna("Nan")

Unnamed: 0  index        date                     category  \
0      0           0      2016-01-01  Armed conflicts and attacks   
1      1           2      2016-01-01  Disasters and Incidents       
2      2           3      2016-01-01  International Relations       
3      3           4      2016-01-01  Crime and Law                 
4      4           7      2016-01-02  Armed conflicts and attacks   
...   ..          ..             ...                          ...   
10419  10419       14422  2019-04-29  Politics and Elections        
10420  10420       14423  2019-04-29  Politics and Elections        
10421  10421       14424  2019-04-30  Arts and culture              
10422  10422       14427  2019-04-30  Business and Economy          
10423  10423       14430  2019-04-30  Politics and Elections        

                             event_title  \
0      IsraeliE28093Palestinian conflict   
1      FALSE                               
2      FALSE                               
3      FALSE                               
4      Mexican Drug War                    
...                 ...                    
10419  FALSE                               
10420  FALSE                               
10421  2019 Japanese imperial transition   
10422  FALSE                               
10423  2019 Venezuela uprising             

                                                                                                                                                                                                              event_summary  \
0      A shooting takes place at a pub in Tel Aviv                                                                                                                                                                            
1      About one thousand houses in Manila's Tondo district in the Philippines are set ablaze following New Year's Eve firecracker festivities that left one dead and 380 others injured. AP via CTV News                     
2      The EU-Ukraine Free Trade deal officially comes into force                                                                                                                                                             
3      The two-child policy takes effect in China                                                                                                                                                                             
4      /wiki/List_of_politicians_killed_in_the_Mexican_Drug_War                                                                                                                                                               
...                                                         ...                                                                                                                                                               
10419  Indonesian President Joko Widodo has decided to relocate the nation's capital from Jakarta                                                                                                                             
10420  U.S. Deputy Attorney General Rod Rosenstein  announces he will resign                                                                                                                                                  
10421  Emperor Akihito abdicates the Chrysanthemum Throne in favor of his elder son                                                                                                                                           
10422  U.S. Attorney General William Barr has decided to recuse himself from deliberations about whether the Antitrust Division of the U.S. Justice Department ought to challenge the planned merger of T-Mobile and Sprint   
10423  /wiki/2019_Venezuelan_presidential_crisis                                                                                                                                                    

In [10]:
df.count()

Unnamed: 0       10424
index            10424
date             10424
category         10424
event_title      10424
event_summary    10424
entities         10175
person           10006
external_link    9882 
dtype: int64

In [11]:
for row in df.loc[df.event_title.isnull(), 'event_title'].index:
    df.at[row, 'event_title'] = "Nan"

In [12]:
df.loc[202,'event_summary']="Vietnam reelects conservative Nguyen Phu Trong as General Secretary of the Communist Party of Vietnam Deputy Prime Minister Nguyen Xuan Phuc"

In [13]:
df.event_title.isnull()

0        False
1        False
2        False
3        False
4        False
         ...  
10419    False
10420    False
10421    False
10422    False
10423    False
Name: event_title, Length: 10424, dtype: bool

In [14]:
df.event_title.value_counts()

FALSE                                          3551
Syrian Civil War                               255 
War in Afghanistan 2001E28093present           168 
European migrant crisis                        84  
Iraqi Civil War 2014E280932017                 82  
                                               ..  
Northern Triangle of Central America           1   
Crime in the United Arab Emirates#Terrorism    1   
2017 Bishop International Airport incident     1   
2016 Irkutsk mass methanol poisoning           1   
Cryptocurrency#Legality                        1   
Name: event_title, Length: 2910, dtype: int64

In [15]:
# import re
# for i in range(0,2000):
#     out=df.loc[i,'event_summary']
# #     my_string=event_df.loc[i,"event_summary"]
# #     splitdata=data.split()

#     word ='Bloomberg News'
#     if word in out:
#         print(out)
# #        



       

    
# # (re_word, my_string)

In [16]:
df['event_summary']=df['event_summary'].str.replace('(','').astype(str)
df['event_summary']=df['event_summary'].str.replace(')','').astype(str)
df['event_summary']=df['event_summary'].str.replace('[','').astype(str)
df['event_summary']=df['event_summary'].str.replace(']','').astype(str)
df['event_summary']=df['event_summary'].str.replace('\"','').astype(str)
df['event_summary']=df['event_summary'].str.replace('\'','').astype(str)
df['event_summary']=df['event_summary'].str.replace('’','').astype(str)
# df['event_summary']=df['event_summary'].str.replace('.','').astype(str)
df['event_summary']=df['event_summary'].str.replace('-','').astype(str)
df['event_summary']=df['event_summary'].str.replace('%',' percent').astype(str)
df['event_summary']=df['event_summary'].str.replace(',','').astype(str)
df['event_summary']=df['event_summary'].str.replace('$','dollar ').astype(str)
df['event_summary']=df['event_summary'].str.replace('€','euro ').astype(str)
df['event_summary']=df['event_summary'].str.replace('£','Pound ').astype(str)
df['event_summary']=df['event_summary'].str.replace('  ',' ').astype(str)
df['event_summary']=df['event_summary'].str.replace('ı','i').astype(str)
df['event_summary']=df['event_summary'].str.replace('Ş','S').astype(str)
df['event_summary']=df['event_summary'].str.replace('ğ','g').astype(str)
df['event_summary']=df['event_summary'].str.replace('ž','z').astype(str)
df['event_summary']=df['event_summary'].str.replace('ć','c').astype(str)
df['event_summary']=df['event_summary'].str.replace('ị','i').astype(str)
df['event_summary']=df['event_summary'].str.replace('ầ','a').astype(str)
df['event_summary']=df['event_summary'].str.replace('Đ','D').astype(str)
df['event_summary']=df['event_summary'].str.replace('ł','l').astype(str)
df['event_summary']=df['event_summary'].str.replace(':',' :').astype(str)



df['event_summary']=df['event_summary'].str.replace('Ōshima','Oshima').astype(str)

# df['event_summary']=df['event_summary'].str.replace('At least','Atleast').astype(str)


df=df[~df.event_summary.str.contains("/wiki", na=False)]
# df=df[~mdf.event_summary.str.contains("According to", na=False)]
indexes=df[df['event_summary'].map(len)  < 35].index
df=df.drop(indexes)
index2=df[df['event_summary']=='nan'].index
df=df.drop(index2)


In [17]:
df.count()

Unnamed: 0       9895
index            9895
date             9895
category         9895
event_title      9895
event_summary    9895
entities         9646
person           9500
external_link    9396
dtype: int64

In [18]:
# Important to reset index otherwise you can get loc problem later
# df=df.reset_index()

In [19]:
df=df.reset_index()

In [20]:
for i in range(0,1000):
#         data=df.loc[i,"event_summary"]
#         print(df.loc[i,"event_summary"])
#         print('\n')
        print(i)
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('A.','A ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('B.','B ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('C.','C ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('D.','D ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('E.','E ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('F.','F ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('G.','G ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('H.','H ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('I.','I ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('J.','J ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('K.','K ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('L.','L ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('M.','M ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('N.','N ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('O.','O ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('P.','P ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('Q.','Q ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('R.','R ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('S.','S')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('T.','T ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('U.','U')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('V.','V ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('W.','W ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('X.','X ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('Y.','Y ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('Z.','Z ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('Inc.','Inc ')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ö','o')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('í','i')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ð','d')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('á','a')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ā','oa')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ō','o')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ó','o')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('é','e')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('í','i')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ç','c')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ï','i')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('É','E')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('á','a')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ã','a')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('Ó','O')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ñ','n')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ễ','e')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ú','u')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ọ','o')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ü','u')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ș','s')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ă','a')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ğ','g')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ệ','e')
        df.loc[i,"event_summary"]=df.loc[i,"event_summary"].replace('ạ','a')
        
        

        
#         print(df.loc[i,"event_summary"])

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [21]:
# import re
# for i in range(0,1000):
#     out=df.loc[i,'event_summary']
# #     my_string=event_df.loc[i,"event_summary"]
# #     splitdata=data.split()

#     word ='ğ'
#     if word in out:
#         print(i)
# #        



       

    
# # (re_word, my_string)

In [22]:

# mdf=df['event_summary']
# mdf=mdf[1000:2000]

In [23]:
# mdf.count()

In [24]:
# indexes=mdf[mdf['event_summary'].map(len)  < 35].index
# mdf=mdf.drop(indexes)

In [25]:
# mdf=mdf.reset_index()

In [26]:
# mdf.count()

In [27]:
df.loc[9274,'event_summary']

'Covington Catholic High School faces backlash after a video of students were seen mocking a Native American elder at the Indigenous Peoples March in Washington DC. USA Today Cincinnati Enquirer WDRB'

In [28]:
for i in range(0,9500):
    data=df.loc[i,"event_summary"]
    split_data=data.rsplit('.',1)
    print(i)
    print(split_data)
    print(split_data[0])
#     print('\n')
    df.loc[i,"event_summary"]=split_data[0]
    

0
['A shooting takes place at a pub in Tel Aviv']
A shooting takes place at a pub in Tel Aviv
1
['About one thousand houses in Manilas Tondo district in the Philippines are set ablaze following New Years Eve firecracker festivities that left one dead and 380 others injured', ' AP via CTV News']
About one thousand houses in Manilas Tondo district in the Philippines are set ablaze following New Years Eve firecracker festivities that left one dead and 380 others injured
2
['The EUUkraine Free Trade deal officially comes into force']
The EUUkraine Free Trade deal officially comes into force
3
['The twochild policy takes effect in China']
The twochild policy takes effect in China
4
['The Islamic State of Iraq and the Levant claims responsibility for a suicide bomb attack on a Iraqi Army base Camp Speicher']
The Islamic State of Iraq and the Levant claims responsibility for a suicide bomb attack on a Iraqi Army base Camp Speicher
5
['Fiji warns residents to prepare for the impact of severe t

144
['Buzzfeed and the BBC report there is evidence of alleged widespread matchfixing by 16 players who have ranked in the top 50 of world tennis involving Northern Italian']
Buzzfeed and the BBC report there is evidence of alleged widespread matchfixing by 16 players who have ranked in the top 50 of world tennis involving Northern Italian
145
['Ukraine says that a cyberattack on Boryspil International Airport near Kiev came from Russian computers', ' Sky News']
Ukraine says that a cyberattack on Boryspil International Airport near Kiev came from Russian computers
146
['A Saudiled coalition airstrike on a police building in Yemens capital']
A Saudiled coalition airstrike on a police building in Yemens capital
147
['A rocket fired from ISILcontrolled territory in Syrias Aleppo Governorate']
A rocket fired from ISILcontrolled territory in Syrias Aleppo Governorate
148
['At least five French Foreign Legion soldiers are killed and six injured in an avalanche while on a training exercise in

248
['A huge fire at a factory in Moscows eastern Sokolniki District']
A huge fire at a factory in Moscows eastern Sokolniki District
249
['Two Turkish Army soldiers are killed in a Kurdistan Workers Party ambush in the southeast Diyarbakir Province', ' Anadolu Post']
Two Turkish Army soldiers are killed in a Kurdistan Workers Party ambush in the southeast Diyarbakir Province
250
['A Taliban suicide bomb attack outside a police office in central Kabul kills at least 9 people', ' AFP via Times of India Sky News AFP via Straits Times']
A Taliban suicide bomb attack outside a police office in central Kabul kills at least 9 people
251
['A snow storm in the United States is affecting multiple regions in Colorado']
A snow storm in the United States is affecting multiple regions in Colorado
252
['The World Health Organization declares the spread of the Zika virus a global public health emergency requiring an urgent']
The World Health Organization declares the spread of the Zika virus a global

394
['Three South Korean army soldiers die after a Bell UH1 Iroquois helicopter crashes in the city of Chuncheon']
Three South Korean army soldiers die after a Bell UH1 Iroquois helicopter crashes in the city of Chuncheon
395
['Ukraine bans Russian cargo trucks from transiting its territory after Russias Ministry of Transport barred Ukrainian cargo trucks because armed groups had been blocking some Russian trucks from entering Ukraine', ' Reuters']
Ukraine bans Russian cargo trucks from transiting its territory after Russias Ministry of Transport barred Ukrainian cargo trucks because armed groups had been blocking some Russian trucks from entering Ukraine
396
['Bosnia and Herzegovina formally applies to join the European Union', ' BBC']
Bosnia and Herzegovina formally applies to join the European Union
397
['United States President Barack Obama hosts a twoday summit in Rancho Mirage']
United States President Barack Obama hosts a twoday summit in Rancho Mirage
398
['Former Prime Ministe

The United States Air Force unveils the Northrop Grumman B21 longrange strategic bomber at the Air Force Associations annual Air Warfare Symposium in Orlando
520
['Officials of FIFA meet in Zurich for the 2016 FIFA Extraordinary Congress to select a new President of FIFA to replace Sepp Blatter. Gianni Infantino is elected with a majority of votes in the second round of voting', ' BBC Los Angeles Times']
Officials of FIFA meet in Zurich for the 2016 FIFA Extraordinary Congress to select a new President of FIFA to replace Sepp Blatter. Gianni Infantino is elected with a majority of votes in the second round of voting
521
['A suicide bomber kills at least 26 and injures nearly 50 in Afghanistans eastern Kunar Province near the border with Pakistan', ' AAP via News Limited NY Times']
A suicide bomber kills at least 26 and injures nearly 50 in Afghanistans eastern Kunar Province near the border with Pakistan
522
['Voters in South Carolina go to the polls for the Democratic Party primary. H

...

8897
['Denmark suspends future weapons export licenses to Saudi Arabia in response to the killing of Jamal Khashoggi and the Saudi Arabianled intervention in Yemen', ' Reuters']
Denmark suspends future weapons export licenses to Saudi Arabia in response to the killing of Jamal Khashoggi and the Saudi Arabianled intervention in Yemen
8898
['President of the European Council Donald Tusk says there is agreement in principle on a political deal that can be endorsed at an EU summit', ' RTÉ']
President of the European Council Donald Tusk says there is agreement in principle on a political deal that can be endorsed at an EU summit
8899
['The United States urges their allies not to use Huawei network equipment']
The United States urges their allies not to use Huawei network equipment
8900
['Chinese state media report that five people are killed and 18 others are injured after a car plowed into children outside a primary school in Huludao']
Chinese state media report that five people are killed

9062
['President of Ukraine Petro Poroshenko declares the establishment of the Orthodox Church of Ukraine']
President of Ukraine Petro Poroshenko declares the establishment of the Orthodox Church of Ukraine
9063
['U.S. President Donald Trump tweets that Secretary of the Interior Ryan Zinke will quit his post at the end of the year', ' Reuters']
U.S. President Donald Trump tweets that Secretary of the Interior Ryan Zinke will quit his post at the end of the year
9064
['A Polish national who was wounded during a terrorist attack in Strasbourg']
A Polish national who was wounded during a terrorist attack in Strasbourg
9065
['A gas blast in a restaurant in Sapporo']
A gas blast in a restaurant in Sapporo
9066
['Ranil Wickremesinghe is sworn in as Prime Minister of Sri Lanka', ' Reuters']
Ranil Wickremesinghe is sworn in as Prime Minister of Sri Lanka
9067
['Six U.S', ' air strikes over the weekend kill at least 62 AlShabaab militants in Somalia']
Six U.S
9068
['Two Scandinavian women on a 

9198
['The Congolese election commission delays announcing the results of the recent election']
The Congolese election commission delays announcing the results of the recent election
9199
['The chancellor of the Ukrainian Orthodox Church Moscow Patriarchate describes the granting of autocephaly on January 5 to the Orthodox Church of Ukraine as a secular event', ' Kyiv Post']
The chancellor of the Ukrainian Orthodox Church Moscow Patriarchate describes the granting of autocephaly on January 5 to the Orthodox Church of Ukraine as a secular event
9200
['At least 30 people are killed after a gold mine collapses in northeastern Afghanistan', ' BBC']
At least 30 people are killed after a gold mine collapses in northeastern Afghanistan
9201
['The death toll from a storm that devastated the Philippines shortly after Christmas rises to 126', ' News24']
The death toll from a storm that devastated the Philippines shortly after Christmas rises to 126
9202
['Yang diPertuan Agong King of Malaysia Mu

9347
['Several cities in the Midwestern United States and Eastern Canada reach record low temperatures for the third consecutive day as a polar vortex continues to affect the region', ' The New York Times']
Several cities in the Midwestern United States and Eastern Canada reach record low temperatures for the third consecutive day as a polar vortex continues to affect the region
9348
['The European Parliament votes to recognize Juan Guaidó as interim President of Venezuela', ' The Independent']
The European Parliament votes to recognize Juan Guaidó as interim President of Venezuela
9349
['Abdullah of Pahang is elected the 16th Yang diPertuan Agong of Malaysia', ' Asia News']
Abdullah of Pahang is elected the 16th Yang diPertuan Agong of Malaysia
9350
['Two people were shot and injured in two individual attacks in Londonderry', 'BBC']
Two people were shot and injured in two individual attacks in Londonderry
9351
['The Associated Press and Snopes say they are no longer providing factchec

The United Nations Security Council Sanctions Committee permits those North Koreans on its global travel ban list to travel to Hanoi
9474
['One surviving female specimen of the Fernandina Galápagos tortoise species']
One surviving female specimen of the Fernandina Galápagos tortoise species
9475
['The United States allies France and the United Kingdom say they wont keep their troops in Syria after the United States pulls out', ' The Washington Post']
The United States allies France and the United Kingdom say they wont keep their troops in Syria after the United States pulls out
9476
['The Tobrukbased Libyan National Army says it has taken control of the El Feel oilfield in Libyas southern Murzuq District', ' Reuters']
The Tobrukbased Libyan National Army says it has taken control of the El Feel oilfield in Libyas southern Murzuq District
9477
['Russian President Vladimir Putin states that Russia is militarily ready for a Cuban Missilestyle crisis if the United States wants one']
Russia

In [29]:
df.loc[15,"event_summary"]='At least six people are killed and dozens injured from a 6.7 magnitude earthquake that struck 20 miles from the city of Imphal'
df.loc[36,'event_summary']='A 5.1 magnitude earthquake near Sungjibaegam'
df.loc[45,'event_summary']='Iran bans imports of all products made in Saudi Arabia and reiterates that the ban on Iranians traveling to the Saudi holy city of Mecca remains in place'
df.loc[184,'event_summary']='A magnitude 7.1 earthquake strikes southwestern Alaska'
df.loc[307,'event_summary']='A Scud missile fired from Yemen is intercepted over Saudi Arabia. The missiles target is believed to have been the King Khalid Air Base'
df.loc[385,'event_summary']='Crews rescue 48 people from two Cannon Mountain tram cars stuck this afternoon about 40 feet off the ground in New Hampshire subzero temperatures in the White Mountains'
df.loc[409,'event_summary']='Canadian multinational aerospace and transportation company Bombardier Inc is to cut 7'
df.loc[410,'event_summary']='Hungarian Prime Minister Viktor Orbán meets with Russian President Vladimir Putin in Moscow. Orbán used the meeting to call for Russias relations with the EU to return to normal'
df.loc[411,'event_summary']=' A report by the Taiwanese Defense Ministry states that China has placed surfacetoair missiles on the disputed Woody Island. Taiwanese Presidentelect Tsai Ingwen called on all parties to exercise selfcontrol based on the principle of peaceful resolution of disputes in the South China Sea'
df.loc[447,'event_summary']='Seven people are killed and another injured in multiple shooting incidents in Kalamazoo County in the American state of Michigan. A 45yearold man was later arrested in the city of Kalamazoo RT'
df.loc[477,'event_summary']='A 4.8 magnitude earthquake strikes near Wasco'
df.loc[578,'event_summary']='A bomb explodes under a vehicle in Belfast injuring a prison officer. Dissident republicans have claimed responsibility'
df.loc[581,'event_summary']='Electricity is gradually being restored across Syria from a nationwide blackout that began early Thursday afternoon. Syrias Electricity Ministry says the electrical grid is expected to return to normal capacity by midnight.  There is no immediate word on the cause'
df.loc[586,'event_summary']='A Turkish court places the influential Zaman newspaper under state control. Zaman is closely linked to the Gülen movement of influential USbased cleric Fethullah Gülen'
df.loc[666,'event_summary']='Jaysh alNasr rebels say they have shot down a fighter jet over the Hama Governorate in western Syria. The Syrian Observatory for Human Rights confirmed the shoot down'
df.loc[702,'event_summary']='The field of 64 teams for the NCAA Tournament is announced. Unbeaten Connecticut is the top overall seed'
df.loc[719,'event_summary']='Cuban officials announce they have detected the first case of the Zika virus transmitted inside the country'
df.loc[768,'event_summary']='New Zealand Prime Minister John Key settles a defamation case with freelance cameraman Bradley Ambrose'
df.loc[774,'event_summary']='Finland and Russia agree to impose temporary restrictions at two Arctic border crossing points on the Finnish Russian border following an increased flow of asylum seekers from Russia to Finland. Under a deal clinched by Russian President Vladimir Putin and Finnish President Sauli Niinisto in Moscow'
df.loc[837,'event_summary']='In a move designed to head off a 4 to 4 decision'
df.loc[876,'event_summary']='Health authorities in Fiji are urging people to observe strict personal hygiene as the country goes through a massive outbreak of conjunctivitis. In the past 14 days alone the number of cases of the virus in one district of Suva have jumped from 700 to 5000 cases'
df.loc[910,'event_summary']='The 2016 United States womens college basketball national championship will be decided when two former Big East Conference foes meet at Bankers Life Fieldhouse in Indianapolis at 8:30 pm'
df.loc[917,'event_summary']='Mexico City authorities declare a pollution alert after smog rose to 1.5 times acceptable limits the day before implementation of the Citys new'
df.loc[921,'event_summary']='Icelandic Prime Minister Sigmundur David Gunnlaugsson refuses to resign after leaked Panama Papers tax documents showed he and his wife used an offshore firm to allegedly hide milliondollar investments. I have not considered quitting because of this matter nor am I going to quit because of this matter'
df.loc[929,'event_summary']='France places Panama back on its list of countries that do not cooperate in catching tax evaders. France has decided to put Panama back on the list of uncooperative countries'
df.loc[945,'event_summary']='Bloomberg News reports Verizon Communications plans a bid for Yahoo Inc Web business'
df.loc[962,'event_summary']='Russia postpones a transfer of missile engines to China. There is concern the technology could be passed on to a third country'

In [30]:
df.loc[1000,'event_summary']='Goldman Sachs agrees to pay dollar 5.06 billion to settle allegations that it sold packages of shoddy mortgages prior to the global financial crisis. The US Justice Department settlement includes a dollar 2.385 billion civil penalty'
df.loc[1001,'event_summary']='A severe heat wave grips Malaysia as much of Southeast Asia struggles with unusually hot and dry weather created by the El Nino season. Temperatures in Malaysia soared above 37°C'
df.loc[1025,'event_summary']='The government of Malawi declares a state of emergency across the country over worsening food shortages caused by a severe drought that is affecting much of Southern Africa with about 2.8 million Malawians'
df.loc[1034,'event_summary']='The World AntiDoping Agency advises that WADAaccredited laboratories are currently conducting studies on meldonium excretion rates since existing data is lacking. Meldonium became a banned substance on January 1'
df.loc[1038,'event_summary']='A magnitude 6.4 earthquake strikes near Kumamoto'
df.loc[1059,'event_summary']='Leaders of the Czech Republic choose Czechia as the oneword alternative name of their country to make it easier for companies'
df.loc[1069,'event_summary']='A magnitude 7.8 earthquake strikes off the coast of Ecuador'
df.loc[1070,'event_summary']='Pope Francis arrives on the Greek island of Lesbos. Francis is expected to visit the Moria detention facility'
df.loc[1071,'event_summary']='EU Foreign policy chief Federica Mogherini holds the highestlevel talks between the EU and Iran in decades to mark a new phase in relations between the two. Both sides are keen to focus on trade'
df.loc[1235,'event_summary']='Archaeologists in Taiwan discover 48 sets of remains unearthed in graves in Taichung. The most striking discovery among them is the 4'
df.loc[1307,'event_summary']='Adelaide United win their first ALeague championship beating the Western Sydney Wanderers 3–1 in the Grand Final at the Adelaide Oval'
df.loc[1681,'event_summary']='The United States Geological Survey also reports that a magnitude 6.2 earthquake struck off the coast of Malaita island'
df.loc[1682,'event_summary']='Israel temporarily bans all Palestinians from entering its territory until Sunday following the June 2016 Tel Aviv shooting'
df.loc[2014,'event_summary']='Indonesian police kill two militants in a clash in a remote jungle area on Sulawesi island'
df.loc[2078,'event_summary']='The International Olympic Committee states it considers all Russian athletes tainted by the countrys staterun doping scheme but individual athletes can compete in 2016 Games if they are able to convince individual sports federations of their innocence. A daunting task for these organizations to handle hundreds of appeals just 12 days before the start of the Rio Games on 5 August'
df.loc[2081,'event_summary']='Verizon Communications buys Yahoo for dollar 4.83 billion in cash'
df.loc[2122,'event_summary']='Around 1.8 million people are affected'
df.loc[2154,'event_summary']='Typhoon Nida makes landfall near Hong Kong with Category 1 hurricane strength'
df.loc[2202,'event_summary']='Remnants of Hurricane Earl helped form Tropical Storm Javier which is southeast of the Mexican resort of Cabo San Lucas on the Baja California Peninsula. A hurricane warning is issued for the southern portion of the peninsula. Rainfall from the storm is expected to impact the American Southwest'
df.loc[2204,'event_summary']='A report showing a negative evaluation of the British Governments Troubled Families programme is leaked to the BBC'
df.loc[2229,'event_summary']='The 2016 Perseid meteor shower peaks tonight'
df.loc[2263,'event_summary']='Barnes & Noble fires CEO Ronald Boire after less than a year in the job. Executive Chairman and company founder Leonard Riggio'
df.loc[2276,'event_summary']='Eddie Bauer reports that malware was used to access payment data for cards used at their stores'
df.loc[2280,'event_summary']='The Obama Administration says it wants to phase out the use of privately owned federal prisons. The move would affect private prisons which house 22'
df.loc[2304,'event_summary']='Philippine officials believe they may have recovered biggest natural giant clam pearl in the world weighing 34kg. Officials are awaiting confirmation from gemologists that the find is indeed the worlds largest pearl'
df.loc[2316,'event_summary']='A 6.8 magnitude earthquake hits central Myanmar'
df.loc[2391,'event_summary']='A SpaceX Falcon 9 rocket explodes during a routine firing test at Cape Canaveral Air Force Station in Florida'
df.loc[2392,'event_summary']='A 7.1 magnitude earthquake occurs off the north east coast of North Island'
df.loc[2453,'event_summary']='Liberty Media confirms it is buying Formula One for US dollar 4.4 billion'
df.loc[2551,'event_summary']='Texas authorities agree to pay dollar 1.9 million to the family of Sandra Bland'
df.loc[2686,'event_summary']='Bass Pro Shops acquires Cabelas for dollar 5.5 billion'
df.loc[2771,'event_summary']='The death toll in North Carolina rises to 22 as flood waters continue to rise. Governor Pat McCrory says places that had a foot of water in the morning'
df.loc[2879,'event_summary']='US District Judge Charles R  Breyer in San Francisco approves German automaker Volkswagen dollar 14.7 billion settlement with federal and California regulators and the owners of the 475'
df.loc[2888,'event_summary']='United States Republican Party vice presidential candidate Mike Pences campaign plane skids off the runway at LaGuardia Airport with no injuries reported'
df.loc[2889,'event_summary']='India and Pakistan each expel a diplomat from the other country as tensions grow over Kashmir'
df.loc[2893,'event_summary']='An American Airlines Boeing 767 catches fire after an aborted takeoff at Chicagos OHare International Airport. Seven passengers and one flight attendant were injured'
df.loc[2908,'event_summary']='Canadian Prime Minister Justin Trudeau and EU officials sign the Comprehensive Economic and Trade Agreement CETA'
df.loc[3153,'event_summary']='Three of Brazils leading football clubs'
df.loc[3237,'event_summary']='Union leader Chuck Jones criticizes Donald Trumps announcement of kept jobs saying that the numbers mentioned are lower. Jones says that 550 workers would actually lose their livelihoods'
df.loc[3563,'event_summary']='Four earthquakes of magnitude 5.1 or higher strike near Amatrice'
df.loc[3726,'event_summary']='South Koreas Agricultural Ministry confirms a case of footandmouth disease at a dairy farm in Boeun County. This is the first instance of this disease in the country since March 29'
df.loc[3783,'event_summary']='Thousands of people are urged to evacuate in and around the vicinity of Yuba City due to the impending failure of an emergency spillway at Oroville Dam in Northern California'
df.loc[3985,'event_summary']='Two UN officials with MONUSCO an American and a Sweden are among six people kidnapped near the village of Ngombe in the Democratic Republic of the Congos KasaiCentral province. Congolese officials have not identified the kidnappers nor has any group claimed responsibility'
df.loc[4049,'event_summary']='NASA astronaut Shane Kimbrough and ESA astronaut Thomas Pesquet take a spacewalk outside of the International Space Station to prepare the vessel for new arrivals'
df.loc[4425,'event_summary']='President of France Emmanuel Macron nominates the full Edouard Philippe government. JeanYves Le Drian becomes foreign minister'
df.loc[4471,'event_summary']='Scientists discover 7.2 million year old prehuman remains in the Balkans area near Bulgaria and Greece'
df.loc[4742,'event_summary']='The United States plans to sell Taiwan dollar 1.42 billion in arms'
df.loc[4755,'event_summary']='A temperature of 53.7°C 128.7°F is recorded during the 2017 heat wave in Ahvaz'
df.loc[4804,'event_summary']='At least two are killed and power supply is interrupted in Eastern Visayas and Bohol when a 6.5 magnitude earthquake hits the province of Leyte in the Philippines InterAksyon'
df.loc[5019,'event_summary']='A magnitude 7.0 earthquake strikes Sichuan in southwest China'
df.loc[5056,'event_summary']='LIGO and Virgo observatories detect the gravitational wave signal from two merging black holes'
df.loc[5092,'event_summary']='Australian Senator Nick Xenophon is discovered to hold dual citizenship with Britain'
df.loc[5216,'event_summary']='A magnitude 8.1 earthquake is recorded 96 kilometers 60 miles south of Pijijiapan'
df.loc[5297,'event_summary']='A magnitude 7.1 earthquake strikes Mexico'
df.loc[5475,'event_summary']='Spanish Prime Minister Mariano Rajoy warns Catalonian President Carles Puigdemont that the regions autonomy will be suspended if he fails to drop the Catalonian governments bid for secession by 10:00 AM CEST 08:00 AM GMT'
df.loc[5509,'event_summary']='Prime Minister Mark Rutte presents his third cabinet. It took a record 225 days of negotiations to form the government composed of VVD'
df.loc[5530,'event_summary']='Paul Manafort and Rick Gates surrender to the FBI after both are indicted on multiple charges stemming from the investigation into the Donald Trump presidential campaigns possible associations with the Russian government. The two men—who respectively served as manager and deputy manager of the campaign from March to August 2016 are being charged on twelve counts'
df.loc[5706,'event_summary']='General Secretary of the Communist Party of China Xi Jinping concludes a twoday highlevel dialogue with party leaders from 120 countries. The program he announces includes the full funding by the Communist Party of China of 15'
df.loc[5715,'event_summary']='The prosecutor in a Brussels court repeats the demand to extradite Carles Puigdemont and four other former Catalan officials to Spain. The defense says that the adduced facts are not punishable under Belgian law. The judge delays the decision until December 14'
df.loc[5727,'event_summary']='US Representative John Conyers DMich steps down amid allegations of sexual harassment'
df.loc[5729,'event_summary']='The New York Metropolitan Museum of Art is brought to reply to an online petition signed by thousands of people. The museum refuses to stop displaying a Balthus painting'
df.loc[5733,'event_summary']='US President Donald Trump recognizes Jerusalem as the capital of Israel and says the US starts the process of moving its embassy from Tel Aviv to Jerusalem. The United States Department of State issues an internal travel warning to Israel'
df.loc[5734,'event_summary']='Investigators discover brain abnormalities in the victims. They are now carefully not using the term sonic to describe the attacks and there is growing skepticism it was caused by a sonic device'
df.loc[5757,'event_summary']='Trump signs a continuing resolution to prevent a government shutdown for another two weeks. Congress has until December 22 to hash out differences over funding DACA'
df.loc[5790,'event_summary']='Militant Palestinians fire rockets towards Israel from the Gaza Strip. The Israel Defense Forces say that the Iron Dome system intercepted two missiles'
df.loc[5791,'event_summary']='Dublin City Councillors vote 59–2 to revoke the Freedom of the City of Dublin given to Myanmars Aung San Suu Kyi for her apparent failure to protect the Rohingya minority from violence. Singer Bob Geldof returned his Freedom one month ago'
df.loc[5796,'event_summary']='Minnesota Governor Mark Dayton announces the appointment of Lt Gov Tina Smith to replace resigning Senate Al Franken in the United States Senate'
df.loc[5800,'event_summary']='The Walt Disney Company announces its intent to acquire a large portion of 21st Century Fox for dollar 52.4 billion'
df.loc[5808,'event_summary']='The most recent US government statistics show a marked increase in the yearly number of deaths by drug overdose. The number for end May 2017 is 66'
df.loc[5839,'event_summary']='US radio preacher Brother Stair host of The Overcomer Ministry is arrested on seven charges of sexual assault and one county of burglary. Walterboro Live The Post and Courier. The show will discontinue its radio broadcasts on January 1'
df.loc[6012,'event_summary']='Twitter posts disseminate claims that actor Kirk Douglas aged 101 had been accused in the past of having sexually assaulted actress Natalie Wood when she was 16 years old'
df.loc[6022,'event_summary']='Mexicans react with incredulity after President of Mexico Enrique Pena Nieto appointed Alberto Bazbaz to the position of head of the CISEN intelligence service. Bazbaz is known for having overseen a 9day search for a missing girl'
df.loc[6063,'event_summary']='The United States will withhold dollar 65 million for Palestinian aid paid via the United Nations Relief and Welfare Agency stating that UNRWA needs to make unspecified reforms. The US says it will provide dollar 60 million'
df.loc[6064,'event_summary']='The New York Times reports that Special Counsel Robert Mueller subpoenaed Steve Bannon last week to testify before a grand jury. The House Intelligence Committee issues a second subpoena'
df.loc[6071,'event_summary']='The Parliament of Catalonia opens the new legislature. Roger Torrent ERC is named Speaker. Three parliamentarians in jail vote through proxies'
df.loc[6072,'event_summary']='The Emirates airline announces an order for up to 36 Airbus A380s. Emirates is already the aircrafts largest operator'
df.loc[6103,'event_summary']='Montana Governor Steve Bullock signs an executive order that bars  any Internet service provider with state contracts from blocking or charging more for faster delivery of websites to any customer in the state. Montana is the first state to respond this way to the FCCs December 14'
df.loc[6220,'event_summary']='Nancy Pelosi breaks the record for the longest speech in the United States House of Representatives. The 77 year old Democrat spoke for eight hours nonstop'
df.loc[6221,'event_summary']='Without peerreview publication researchers at Londons Natural History Museum state that the DNA extracted from Cheddar Man reveals that early inhabitants of Great Britain had blue eyes and dark skin. The name Cheddar Man was given to a fossil of a human man that lived thousands of years ago'
df.loc[6227,'event_summary']='US President Donald Trump meets with Guatemalan President Jimmy Morales. Trump thanks Morales for having supported the decision of the United States to recognize Jerusalem as Israels capital. They discuss various issues about the crisis in Venezuela'
df.loc[6255,'event_summary']='Emergency teams comb snowy fields outside Moscow Monday for debris from a crashed Russian airliner and the remains of the 71 people who died. Transport Minister Maksim Sokolov says that emergency teams have already found the planes flight data recorder'
df.loc[6322,'event_summary']='US President Donald Trump meets in the White House State Dining Room with parents and friends of young people killed in school shootings to discuss what needs to be done. Suggestions for the president included a number of items to make schools safer'
df.loc[6571,'event_summary']='Malta imposes a freeze on Pilatus Bank. The banks Iranian chairman Ali Sadr Hashemi Nejad was arrested and charged in the United States earlier this week'
df.loc[7127,'event_summary']='The US Senate votes 50–49 to confirm Jim Bridenstine as administrator of NASA '
df.loc[7140,'event_summary']='The United States Federal Aviation Administration issues an emergency Airworthiness Directive for CFM567B jet engines. The EAD expands on previous orders requiring ultrasonic testing to search for metal fatigue in fan blades. It mandates testing on engines that have reached 30'
df.loc[7146,'event_summary']='The Basque separatist terrorist group ETA apologises to every victim of its actions. The ETA killed more than 800 people in its 40 year history'
df.loc[7403,'event_summary']='French economy minister Bruno Le Maire says Air France may collapse over ongoing strike action and the state will not bail the firm out despite owning 14.3 percent of parent Air France KLM'
df.loc[7427,'event_summary']='Scientists discover that WASP96b has an atmosphere that is free of clouds'
df.loc[7720,'event_summary']='The Senate of France approves a bill to reform the SNCF railway company. The French state writes off €35 billion of SNCFs €47 billion debt'
df.loc[7741,'event_summary']='A magnitude 5.5 earthquake strikes Osaka'
df.loc[8055,'event_summary']='A magnitude 6.4 earthquake hits Lombok'
df.loc[8253,'event_summary']='A 5.8 magnitude earthquake hits close to yesterdays 7.3 earthquake'
df.loc[8267,'event_summary']='A 1962 Ferrari 250 GTO is sold for dollar 48.4 million at an auction in California'
df.loc[8274,'event_summary']='A magnitude 6.0 earthquake strikes the western Iranian province of Kermanshah'
df.loc[8277,'event_summary']='Irans finance minister Masoud Karbasian is sacked after an impeachment attempt by parliament. This is the second impeachment this month'
df.loc[8280,'event_summary']='Violent protests break out across Germany after a stabbing attack the day before. Several instances of racial violence are reported'
df.loc[8316,'event_summary']='The European Union announces an aid package of €35 million dollar 40.6 million for Venezuelans'
df.loc[8539,'event_summary']='A USMC F35 jet crashes in coastal South Carolina making this the first crash of the US militarys newest and most expensively developed aircraft'
df.loc[8615,'event_summary']='Three people were killed and houses were damaged after a magnitude 6.3 earthquake struck off East Java'
df.loc[8954,'event_summary']='A magnitude 7.0 earthquake hits Alaska'
df.loc[8977,'event_summary']='Frank Scott Jr is elected Mayor of Little Rock'
df.loc[9093,'event_summary']='Soyuz MS09 lands safely on the steppe in Kazakhstan'
df.loc[9110,'event_summary']='The Dow Jones Industrial Average drops 2.9 percent'
df.loc[9148,'event_summary']='Three people are injured after being stabbed in an attack at Manchester Victoria station. The attacker shouted Allah during the attack. The attack is being treated as a terrorrelated incident'
df.loc[9206,'event_summary']='The government of Gabon quashes a coup detat by soldiers. The attempt took place while the countrys president'
df.loc[9274,'event_summary']='Covington Catholic High School faces backlash after a video of students were seen mocking a Native American elder at the Indigenous Peoples March in Washington'
df.loc[9417,'event_summary']='The mission of NASAs Opportunity rover on Mars comes to an end. The rover stopped communicating in June 2018 after a Martian dust storm'
df.loc[9453,'event_summary']='Denny Hamlin wins the 2019 Daytona 500. It is his second win in the event'
df.loc[9048,'event_summary']='Virgin Galactics SpaceShipTwo successfully completes its fourth powered test flight with VSS Unity and reaches space at an altitude of 82.7km 51.4mi but does not breach the 100km 62mi Karman Line'
df.loc[8412,'event_summary']='The French railway company SNCF announces prototypes for driverless passenger and freight trains by 2023'
df.loc[9151,'event_summary']='Russias FSB state security agency says it has arrested a US citizen caught spying in Moscow'
df.loc[1162,'event_summary']='Scientists discover the quantum tunneling of water molecules'
df.loc[7277,'event_summary']='Scientific studies have offered evidence that a geothermal plant may have caused the earthquake in South Korea'
df.loc[5356,'event_summary']='Aquatic species from Japan hitched a ride on debris from the 2011 Tohoku earthquake and tsunami and were able to reach the West Coast of the United States alive.'
df.loc[5267,'event_summary']='Scientists hope to revive the extinct Floreana island tortoise using a geneticallyinformed captive breeding program with the tortoises closest ancestors'

In [31]:
df=df.drop(df.index[6419])

In [32]:
df=df.drop(df.index[8485])
df=df.drop(df.index[8519])
df=df.drop(df.index[8978])
df=df.drop(df.index[8982])
df=df.drop(df.index[9499])
df=df.drop(df.index[1299])
df=df.drop(df.index[3840])
df=df.drop(df.index[4449])

In [33]:
mdf=df[['date','category','event_title','event_summary']]


In [34]:
mdf

date                     category  \
0     2016-01-01  Armed conflicts and attacks   
1     2016-01-01  Disasters and Incidents       
2     2016-01-01  International Relations       
3     2016-01-01  Crime and Law                 
4     2016-01-03  Armed conflicts and attacks   
...          ...                          ...   
9890  2019-04-29  Disasters and Incidents       
9891  2019-04-29  Politics and Elections        
9892  2019-04-29  Politics and Elections        
9893  2019-04-30  Arts and culture              
9894  2019-04-30  Business and Economy          

                            event_title  \
0     IsraeliE28093Palestinian conflict   
1     FALSE                               
2     FALSE                               
3     FALSE                               
4     Iraqi Civil War 2014E280932017      
...                              ...      
9890  FALSE                               
9891  FALSE                               
9892  FALSE                               
9893  2019 Japanese imperial transition   
9894  FALSE                               

                                                                                                                                                                                                            event_summary  
0     A shooting takes place at a pub in Tel Aviv                                                                                                                                                                          
1     About one thousand houses in Manilas Tondo district in the Philippines are set ablaze following New Years Eve firecracker festivities that left one dead and 380 others injured                                      
2     The EUUkraine Free Trade deal officially comes into force                                                                                                                                                            
3     The twochild policy takes effect in China                                                                                                                                                                            
4     The Islamic State of Iraq and the Levant claims responsibility for a suicide bomb attack on a Iraqi Army base Camp Speicher                                                                                          
...                                                                                                                           ...                                                                                          
9890  A minibus carrying Turkish Süper Lig Alanyaspor football players crashes near Alanya                                                                                                                                 
9891  Indonesian President Joko Widodo has decided to relocate the nations capital from Jakarta                                                                                                                            
9892  U.S. Deputy Attorney General Rod Rosenstein announces he will resign                                                                                                                                                 
9893  Emperor Akihito abdicates the Chrysanthemum Throne in favor of his elder son                                                                                                                                         
9894  U.S. Attorney General William Barr has decided to recuse himself from deliberations about whether the Antitrust Division of the U.S. Justice Department ought to challenge the planned merger of TMobile and Sprint  

[9886 rows x 4 columns]

In [35]:
mdf=mdf[~mdf.event_summary.str.contains("According to", na=False)]

In [36]:
mdf=mdf.reset_index()

In [37]:
# import re
# for i in range(0,9500):
#     my_string=df.loc[i,"event_summary"]
# #     splitdata=data.split()

#     word ='Phys'
#     if word in my_string:
#         print(i)
#         print (my_string) 
# #     matches = my_string.find(word)
    
    
# # (re_word, my_string)

In [38]:
# for i in range(0,9500):
#     text=df.loc[i,"event_summary"]
#     head, sep, tai= text.partition('via')
#     print(i)
#     print(head)
#     df.loc[i,"event_summary"]=head
#     print(".................................................................\n")
#     print(tai)

In [39]:
# import string
# dascii = set(string.printable)   

# def remove_non_ascii(s):
#     return filter(lambda x: x in ascii, s)
# for i in range(0,500):
#     w=df.loc[i,'event_summary']
#     remove_non_ascii(w)


In [40]:
sNLP = StanfordNLP()

In [41]:
from nltk.tree import Tree


In [42]:
from nltk.parse.corenlp import CoreNLPParser
from nltk.parse.stanford import StanfordDependencyParser


In [43]:
mdf.count()

index            9845
date             9845
category         9845
event_title      9845
event_summary    9845
dtype: int64

### 4. Calling CoreNLP Functions

In [44]:
if __name__ == '__main__':
    sNLP = StanfordNLP()
    for i in range(0,9500):
        print(i)
        text = mdf['event_summary'][i]
#         mdf.loc[i,'Parse Tree']= sNLP.parse(text)
#         print(mdf.loc[i,'Parse Tree'])
        
        print('\n\n .......................................................................... \n\n')
            

0


 .......................................................................... 


1


 .......................................................................... 


2


 .......................................................................... 


3


 .......................................................................... 


4


 .......................................................................... 


5


 .......................................................................... 


6


 .......................................................................... 


7


 .......................................................................... 


8


 .......................................................................... 


9


 .......................................................................... 


10


 .......................................................................... 


11


 .......................................................................... 


12


961


 .......................................................................... 


962


 .......................................................................... 


963


 .......................................................................... 


964


 .......................................................................... 


965


 .......................................................................... 


966


 .......................................................................... 


967


 .......................................................................... 


968


 .......................................................................... 


969


 .......................................................................... 


970


 .......................................................................... 


971


 .......................................................................... 


972


 .........................................................

1936


 .......................................................................... 


1937


 .......................................................................... 


1938


 .......................................................................... 


1939


 .......................................................................... 


1940


 .......................................................................... 


1941


 .......................................................................... 


1942


 .......................................................................... 


1943


 .......................................................................... 


1944


 .......................................................................... 


1945


 .......................................................................... 


1946


 .......................................................................... 


1947


 ..............................................


2900


 .......................................................................... 


2901


 .......................................................................... 


2902


 .......................................................................... 


2903


 .......................................................................... 


2904


 .......................................................................... 


2905


 .......................................................................... 


2906


 .......................................................................... 


2907


 .......................................................................... 


2908


 .......................................................................... 


2909


 .......................................................................... 


2910


 .......................................................................... 


2911


 .............................................



 .......................................................................... 


3685


 .......................................................................... 


3686


 .......................................................................... 


3687


 .......................................................................... 


3688


 .......................................................................... 


3689


 .......................................................................... 


3690


 .......................................................................... 


3691


 .......................................................................... 


3692


 .......................................................................... 


3693


 .......................................................................... 


3694


 .......................................................................... 


3695


 ...................................................

...

5615


 .......................................................................... 


5616


 .......................................................................... 


5617


 .......................................................................... 


5618


 .......................................................................... 


5619


 .......................................................................... 


5620


 .......................................................................... 


5621


 .......................................................................... 


5622


 .......................................................................... 


5623


 .......................................................................... 


5624


 .......................................................................... 


5625


 .......................................................................... 


5626


 ..............................................

6658


 .......................................................................... 


6659


 .......................................................................... 


6660


 .......................................................................... 


6661


 .......................................................................... 


6662


 .......................................................................... 


6663


 .......................................................................... 


6664


 .......................................................................... 


6665


 .......................................................................... 


6666


 .......................................................................... 


6667


 .......................................................................... 


6668


 .......................................................................... 


6669


 ..............................................


7349


 .......................................................................... 


7350


 .......................................................................... 


7351


 .......................................................................... 


7352


 .......................................................................... 


7353


 .......................................................................... 


7354


 .......................................................................... 


7355


 .......................................................................... 


7356


 .......................................................................... 


7357


 .......................................................................... 


7358


 .......................................................................... 


7359


 .......................................................................... 


7360


 .............................................

7942


 .......................................................................... 


7943


 .......................................................................... 


7944


 .......................................................................... 


7945


 .......................................................................... 


7946


 .......................................................................... 


7947


 .......................................................................... 


7948


 .......................................................................... 


7949


 .......................................................................... 


7950


 .......................................................................... 


7951


 .......................................................................... 


7952


 .......................................................................... 


7953


 ..............................................


8726


 .......................................................................... 


8727


 .......................................................................... 


8728


 .......................................................................... 


8729


 .......................................................................... 


8730


 .......................................................................... 


8731


 .......................................................................... 


8732


 .......................................................................... 


8733


 .......................................................................... 


8734


 .......................................................................... 


8735


 .......................................................................... 


8736


 .......................................................................... 


8737


 .............................................

## NOW  WE NEED TO CREATE THREE DATAFRAMES: EVENT DF, EVENT ARGUMENT DF, EVENT ANNOTATION DF

### 5. Creating EVENT Dataframe

In [45]:
event_df=mdf

In [46]:
event_df

index        date                     category  \
0     0      2016-01-01  Armed conflicts and attacks   
1     1      2016-01-01  Disasters and Incidents       
2     2      2016-01-01  International Relations       
3     3      2016-01-01  Crime and Law                 
4     4      2016-01-03  Armed conflicts and attacks   
...  ..             ...                          ...   
9840  9890   2019-04-29  Disasters and Incidents       
9841  9891   2019-04-29  Politics and Elections        
9842  9892   2019-04-29  Politics and Elections        
9843  9893   2019-04-30  Arts and culture              
9844  9894   2019-04-30  Business and Economy          

                            event_title  \
0     IsraeliE28093Palestinian conflict   
1     FALSE                               
2     FALSE                               
3     FALSE                               
4     Iraqi Civil War 2014E280932017      
...                              ...      
9840  FALSE                               
9841  FALSE                               
9842  FALSE                               
9843  2019 Japanese imperial transition   
9844  FALSE                               

                                                                                                                                                                                                            event_summary  
0     A shooting takes place at a pub in Tel Aviv                                                                                                                                                                          
1     About one thousand houses in Manilas Tondo district in the Philippines are set ablaze following New Years Eve firecracker festivities that left one dead and 380 others injured                                      
2     The EUUkraine Free Trade deal officially comes into force                                                                                                                                                            
3     The twochild policy takes effect in China                                                                                                                                                                            
4     The Islamic State of Iraq and the Levant claims responsibility for a suicide bomb attack on a Iraqi Army base Camp Speicher                                                                                          
...                                                                                                                           ...                                                                                          
9840  A minibus carrying Turkish Süper Lig Alanyaspor football players crashes near Alanya                                                                                                                                 
9841  Indonesian President Joko Widodo has decided to relocate the nations capital from Jakarta                                                                                                                            
9842  U.S. Deputy Attorney General Rod Rosenstein announces he will resign                                                                                                                                                 
9843  Emperor Akihito abdicates the Chrysanthemum Throne in favor of his elder son                                                                                                                                         
9844  U.S. Attorney General William Barr has decided to recuse himself from deliberations about whether the Antitrust Division of the U.S. Justice Department ought to challenge the planned merger of TMobile and Sprint  

[9845 rows x 5 columns]

In [47]:
event_df.loc[:,'event_id'] = np.arange(len(event_df))

In [48]:
event_df=event_df[['event_id','date','category','event_title','event_summary']]

In [49]:
# event_df.loc[:,'event_id']=event_df.loc[:,'event_id']

In [50]:
# event_df=event_df[['event_id','event_summary']]

In [51]:
event_df

event_id        date                     category  \
0     0         2016-01-01  Armed conflicts and attacks   
1     1         2016-01-01  Disasters and Incidents       
2     2         2016-01-01  International Relations       
3     3         2016-01-01  Crime and Law                 
4     4         2016-01-03  Armed conflicts and attacks   
...  ..                ...                          ...   
9840  9840      2019-04-29  Disasters and Incidents       
9841  9841      2019-04-29  Politics and Elections        
9842  9842      2019-04-29  Politics and Elections        
9843  9843      2019-04-30  Arts and culture              
9844  9844      2019-04-30  Business and Economy          

                            event_title  \
0     IsraeliE28093Palestinian conflict   
1     FALSE                               
2     FALSE                               
3     FALSE                               
4     Iraqi Civil War 2014E280932017      
...                              ...      
9840  FALSE                               
9841  FALSE                               
9842  FALSE                               
9843  2019 Japanese imperial transition   
9844  FALSE                               

                                                                                                                                                                                                            event_summary  
0     A shooting takes place at a pub in Tel Aviv                                                                                                                                                                          
1     About one thousand houses in Manilas Tondo district in the Philippines are set ablaze following New Years Eve firecracker festivities that left one dead and 380 others injured                                      
2     The EUUkraine Free Trade deal officially comes into force                                                                                                                                                            
3     The twochild policy takes effect in China                                                                                                                                                                            
4     The Islamic State of Iraq and the Levant claims responsibility for a suicide bomb attack on a Iraqi Army base Camp Speicher                                                                                          
...                                                                                                                           ...                                                                                          
9840  A minibus carrying Turkish Süper Lig Alanyaspor football players crashes near Alanya                                                                                                                                 
9841  Indonesian President Joko Widodo has decided to relocate the nations capital from Jakarta                                                                                                                            
9842  U.S. Deputy Attorney General Rod Rosenstein announces he will resign                                                                                                                                                 
9843  Emperor Akihito abdicates the Chrysanthemum Throne in favor of his elder son                                                                                                                                         
9844  U.S. Attorney General William Barr has decided to recuse himself from deliberations about whether the Antitrust Division of the U.S. Justice Department ought to challenge the planned merger of TMobile and Sprint  

[9845 rows x 5 columns]

In [52]:
event_df.loc[398,'event_summary']='Former Prime Minister of Israel Ehud Olmert starts a 19 month prison sentence for bribery and obstructing justice In the last decade'

C:\Users\gulja\AppData\Roaming\Python\Python37\site-packages\pandas\core\indexing.py:494: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


In [53]:
event_df.loc[380,'event_summary']='The US Geological Survey reports a magnitude 5.8 earthquake strikes Christchurch in New Zealand. The St. John ambulance service says that several people suffered minor injuries from falls as they ran from the quake but there were no serious damage'

### 6.1 Creating relation phrase DataFrame

In [54]:
# Relationphrase_df = pd.DataFrame()

In [55]:
# Relationphrase_df['id']='NA'
# Relationphrase_df['event_id']='NA'
# Relationphrase_df['Relation_Phrase']='NA'
# Relationphrase_df['annotator_id']='NA'

In [56]:
# for i in range(0,100):
#     Relationphrase_df.loc[i,'event_id']=event_df.loc[i,'event_id']

In [57]:
# Relationphrase_df['id'] = np.arange(len(Relationphrase_df))

In [58]:
# Relationphrase_df

### 6.2 Creating EVENT Argument dataframe

In [59]:
import sys
import re

In [60]:
event_df.loc[86,'event_summary']='South Korean soldiers fire warning shots at a suspected North Korean drone near the Korean Demilitarized Zone DMZ. The unidentified flying object was spotted around 29 miles north of Seoul'

In [61]:
for i in range(0,9500):
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('-','to')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' A ',' A.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' B ',' B.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' C ',' C.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' D ',' D.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' E ',' E.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' F ',' F.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' G ',' G.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' H ',' H.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' I ',' I.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' J ',' J.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' K ',' K.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' L ',' L.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' M ',' M.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' N ',' N.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' O ',' O.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' P ',' P.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' Q ',' Q.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' R ',' R.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' S ',' S.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' T ',' T.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' U ',' U.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' V ',' V.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' W ',' W.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' X ',' X.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' Y ',' Y.')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' Z ',' Z.')





In [62]:


# event_df['event_summary']=event_df['event_summary'].str.replace('&','a').astype(str)
event_df.loc[1662,'event_summary']='United Nations Secretary General Ban Kimoon temporarily removes the Saudi Arabian led intervention in Yemen from a UN  blacklist for violating childrens rights because its supporters threatened to stop funding many UN  programs'
event_df.loc[2164,'event_summary']='A Swedish court orders the owner of the luxury cruise ship Ocean Gala that was due to house 1'
event_df.loc[2165,'event_summary']='British activists with the Black Lives Matter movement from America block the road to Heathrow Airport and to streets in Manchester'
event_df.loc[86,'event_summary']='South Korean soldiers fire warning shots at a suspected North Korean drone near the Korean Demilitarized Zone DMZ. The unidentified flying object was spotted around 29 miles north of Seoul'
event_df.loc[356,'event_summary']='A Libyan Air Force MiG23 is shot down over Benghazi as it conducted airstrikes on Shura Council of Benghazi Revolutionaries positions in the coastal city'
event_df.loc[315,'event_summary']='Daniel Bryan announces that he will retire from WWE'
event_df.loc[22,'event_summary']='Trump nominates Katie Walsh former Republican National Committee RNC chief of staff as Deputy White House Chief'

In [63]:

for i in range(0,9500):
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('Reuters','')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('ISIL','')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('year',' year')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('month',' month')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('ń','n')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('“','')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('–',' to ')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('\xa0',' ')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(';','')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('UN ','UN')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('  ',' ')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('News.com',' ')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('United Nations','UN')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('United States','US')



In [64]:
event_df.loc[446,'event_summary']='Seven people are killed and another injured in multiple shooting incidents in Kalamazoo County in the American state of Michigan. A 45 year old man was later arrested in the city of Kalamazoo RT'
event_df.loc[293,'event_summary']='Tunisia completes the construction of a 200 km 125 mile barrier along its border with Libya'
# event_df.loc[446,'event_summary']='Seven people are killed and another injured in multiple shooting incidents in Kalamazoo County in the American state of Michigan. A.45 yearold man was later arrested in the city of Kalamazoo RT'
event_df.loc[559,'event_summary']='Mining company Samarco agrees to pay dollar 4.4 billion reais Pound 804m in compensation to victims of the Bento Rodrigues dam disaster in Brazil'
event_df.loc[606,'event_summary']='Indonesian President Joko Jokowi Widodo calls on Muslim leaders at the Organisation of Islamic Cooperation OIC summit meeting in Jakarta to unite and be part of the solution on Palestine'
event_df.loc[870,'event_summary']='Astronomers study reveals the surface of exoplanet 55 Cancri e has a 2500 degree centigrade liquid face'
event_df.loc[999,'event_summary']='A severe heat wave grips Malaysia as much of Southeast Asia struggles with unusually hot and dry weather created by the El Nino season. Temperatures in Malaysia soared above 37 degree centigrade'
event_df.loc[1109,'event_summary']='A magnitude 6.1 aftershock has struck off the coast of Ecuador at 3:33 a.m'
event_df.loc[1506,'event_summary']='Googles offices in central Paris are raided by French finance officials as part of a tax fraud investigation . Google is accused of owing euro 1.6 billion dollar 1.8 billion Pound 1.3 billion in unpaid taxes'
event_df.loc[1662,'event_summary']='United Nations Secretary General Ban Kimoon temporarily removes the Saudi Arabian led intervention in Yemen from a UN blacklist for violating childrens rights because its supporters threatened to stop funding many UN programs'
event_df.loc[1807,'event_summary']='A roller coaster derails and crashes at MD theme park in Motherwell'
event_df.loc[2083,'event_summary']='Serie A defending champions Juventus break the Italian transfer record fee after completing the signing of Argentinian forward Gonzalo Higuain from Napoli for euro 90M Pound 75.3M on a five year deal'
event_df.loc[2102,'event_summary']='Scientists have discovered that the region directly above the Great Red Spot on the planet Jupiter is about 700 degree fahrenheit warmer than the surrounding upper atmosphere'
event_df.loc[2289,'event_summary']='Philippine officials believe they may have recovered biggest natural giant clam pearl in the world weighing 34 kg . Officials are awaiting confirmation from gemologists that the find is indeed the worlds largest pearl'
event_df.loc[2529,'event_summary']='Iranian powerlifter Siamand Rahman cleared the bar at 310 kg in the mens over 107 kg'
event_df.loc[3520,'event_summary']='German police detain two suspects with over 150 kg of pyrotechnic explosives and an IED inscribed with a swastika and SS runes'
event_df.loc[3656,'event_summary']='Philippine President Rodrigo Duterte suspends the war on drugs so resources can focus on ridding corrupt officers from the Philippine National Police. The cause celèbre is the kidnapping and strangulation of South Korean businessman Jee Ickjoo last October'
event_df.loc[4600,'event_summary']='The US Federal Reserve raises the federal funds rate by a quarter percentage point to a level between the 1.0 to 1'
event_df.loc[4697,'event_summary']='The European Commission imposes a record euro 2.42 billion antitrust fine on internet giant Google for allegedly manipulating its search engine results'
event_df.loc[4723,'event_summary']='A temperature of 53.7 degree centigrade is recorded during the 2017 heat wave in Ahvaz'
event_df.loc[4820,'event_summary']='Scientists at the Chinese Academy of Sciences successfully teleport a photon from a ground station in Tibet to a satellite orbiting Earth at distance of 500 km away. It is the first time an object has been teleported from the planet into space'
event_df.loc[5276,'event_summary']='Google strikes a dollar 1.1 billion Pound 822m deal with Taiwans HTC to expand its smartphone business'
event_df.loc[5348,'event_summary']='Thirty thousand North Korean rocket propelled grenades are seized off the coast of Egypt by American forces after being purchased by Egyptian business executives for dollar 23 million EPound 406 million'
event_df.loc[5642,'event_summary']='A Soyuz 2.1 bs Fregat upper stage malfunctions during MeteorM No.21s launch from the Vostochny Cosmodrome'
event_df.loc[6058,'event_summary']='Turkish President Erdogan announces that Turkish Army ground troops have entered the district of Afrin in Syria . Turkish Prime Minister Binali Yıldırım says the goal is to establish a 30 km safe zone'
event_df.loc[6391,'event_summary']='Former United States Department of Justice attorney Jeffrey Wertkin is sentenced to 2 and half years in prison for what prosecutors called the DoJs most serious example of public corruption'
event_df.loc[7241,'event_summary']='Astronomers from the Outer Solar System Origins Survey OSSOS announce the discovery of 80 kilometre 50 mi asteroid 2015 KE172'
event_df.loc[7660,'event_summary']='A US federal judge approves AT&T dollar 85 billion merger with Time Warner'
event_df.loc[7680,'event_summary']='The Senate of France approves a bill to reform the SNCF railway company. The French state writes off euro 35 billion of SNCFs euro 47 billion debt'
event_df.loc[7803,'event_summary']='BAE Systems is awarded a Pound 19.6 billion contract to build nine nextgeneration Hunterclass frigates for the Royal Australian Navy with construction expected to begin in 2020'
event_df.loc[8274,'event_summary']='The European Union announces an aid package of euro 35 million dollar 40.6 million for Venezuelans'
event_df.loc[8351,'event_summary']='The Green Bay Packers won a game down 17 or more in the fourth quarter for the first time in their history with a 2423 win over the Chicago Bears after Aaron Rodgers returned from an injury that caused him to temporarily leave the game. This win was the fourthlargest comeback in their team history'
event_df.loc[8588,'event_summary']='The death toll in the US from Hurricane Michael rises to 17 in Florida'
event_df.loc[8815,'event_summary']='US President Donald Trump visits victims of the Camp Fire and Woolsey Fire as the death toll rises to 79 as 76 in the Camp Fire and three in the Woolsey Fire'
event_df.loc[9001,'event_summary']='Virgin Galactics SpaceShipTwo successfully completes its fourth powered test flight with VSS Unity and reaches space at an altitude of 82.7 km 51.4 mi but does not breach the 100 km 62 mi Karman Line'
event_df.loc[9294,'event_summary']='Several hundred flights are cancelled in Chicago amidst an extreme cold wave bringing temperatures of minus 22 fahrenheit to the region'

In [65]:
event_df.loc[2083,'event_summary']='Serie A defending champions Juventus break the Italian transfer record fee after completing the signing of Argentinian forward Gonzalo Higuain from Napoli for euro 90 million on a five year deal'
event_df.loc[357,'event_summary']='Atleast five policemen are killed in an attack on a police station in Aden'
event_df.loc[459,'event_summary']='Ashraf Rifi resigns as Minister for Justice for Lebanon in protest at Hezbollah domination of government which he claims is harming relations with Arab nations'

In [66]:
event_df.loc[511,'event_summary']='Zika infection during pregnancy can cause a serious birth defect'

In [67]:
event_df.loc[6350,'event_summary']='Gazan officials say Israeli soldiers killed a Palestinian farmer on his own land in Gaza Strip. An Israeli military spokesperson said that he got too close to the border fence'

In [68]:

# ann = StanfordNLP()
# ann.props = {
#             'annotators': 'ssplit',
#             'pipelineLanguage': 'en',
#             'outputFormat': 'json'
#         }

# # You can access annotations using ann.
# text = 'The Washington Capitals will play the Vegas Golden Knights in the Stanley Cup Finals after a game 7 victory. It is the first Stanley Cup Finals appearance for the Capitals since 1998'
# sentences = ann.annotate(text)
# # print (text)
# for sentence in sentences['sentences']:
# #     print (sentence)
#     sent_str = ''.join([key_word['before'] + key_word['word'] for key_word in sentence['tokens']]).strip()
#     print (sent_str)
# # print (sentences['sentences'][0])
# # if '. ' in text:
# #     text = text.split('. ')
# # else:
# #     text = [text]
    
    
# # for sentence in text:
#     parsestr = sNLP.parse(sent_str)
#     print (parsestr)

# #     id1 = event_df.loc[j,'event_id']
# # print(id1)
# #     print("\n")
# # print(text+"\n")
# # parsestr=sNLP.parse(text)
# # print(parsestr)

In [69]:
event_df.loc[514,'event_summary']='Constitutional Court of Turkey ruling that their rights had been violated'
event_df.loc[901,'event_summary']='Czech Minister of the Interior Milan Chovanec says that authorities in Prague will send a group of twentyfive IraqiChristians back to Iraq after they tried to move to Germany rather than staying in the Czech Republic. The refugees were on their way to Germany via bus before being stopped at the border. Czech authorities agreed to a request by the German police to take the people back. Chovanec said the twentyfive Iraqis abused Czech generosity and should go back to Iraq within seven days'
event_df.loc[988,'event_summary']='The Foreign Minister of Iran Mohammad Javad Zarif says that the countrys missile program would not be up for discussion. This comes as United States Secretary of State John Kerry said last Thursday that the US and its allies would only address Irans concerns in the region if it makes it clear to all involved that it was prepared to cease provocative ballistic missile launches and tests'
event_df.loc[992,'event_summary']='British Prime Minister David Cameron releases his tax records in an effort to remove discussion about his personal wealth from current political discourse. His initial reluctance to admit he had benefited from his late fathers offshore Panama Papers holdings still seems to be affecting the upcoming European Union referendum'
event_df.loc[1307,'event_summary']='United States Chief of Naval Operations Admiral John M. Richardson says Russian jets in Baltics buzzing a US military ship and planes are escalating tension between two nations. Richardson added he doesnt think Russians are trying to provoke an incident but these actions increase chance of a tactical miscalculation'
event_df.loc[1872,'event_summary']='The new Belarusian ruble replaces the old ruble during redenomination'
event_df.loc[1894,'event_summary']='Nigel Farage resigns as leader of UK Independence Party UKIP but says he and other MEPs of party would continue to carry out their term in European Parliament'
event_df.loc[1961,'event_summary']='Citibank notifies the government of Venezuela it will close the accounts of the Venezuelan Central Bank and the Bank in 30 days after conducting a periodic risk management review'
event_df.loc[2287,'event_summary']='US service member becomes first US military combat casualty in Afghanistan since January 2016 when he is killed by an improvised explosive device IED while on patrol near city of Lashkar Gah in Afghanistans southern Helmand Province. Another American service member and six Afghan soldiers were also injured in blast'
event_df.loc[2978,'event_summary']='Philippine president Rodrigo Duterte threatens to suspend the countrys habeas corpus if forced to by what he says worsening lawlessness in country'
event_df.loc[3661,"event_summary"]='Germany agrees to ban the fullface veil burqa and niqoab in public spaces'
event_df.loc[3788,"event_summary"]='The US Justice Department tells the ninth circuit court of Appeals that it wont be seeking further action by the court since this executive order will soon be replaced by a different one'
event_df.loc[3008,"event_summary"]='Japanese Prime Minister Shinzo Abe becomes the first foreign head of government to meet Donald Trump since his election as President on November 8'

# event_df.loc[183,'eventsummary2']="<span id=1026 style='background-color:#ADADEB; display:inline-block; overflow: h

In [70]:
event_df.loc[4256,"event_summary"]='Muhammad V. is formally installed as the 15th King of Malaysia'
event_df.loc[4013,"event_summary"]='Russian Special Envoy to Afghanistan Zamir Kabulov denies allegations by NATO Commander. Curtis Scaparrotti that Russia was perhaps supplying the Taliban'

In [71]:
event_df.loc[4146,"event_summary"]='Government aligned militias kill 16 people during a raid in Wau'
event_df.loc[4084,"event_summary"]='Authorities cannot contact the South Korean cargo freighter stellar daisy. It is believed that the ship sunk off the coast of Uruguay'

In [72]:
event_df.loc[4120,"event_summary"]='United States House Permanent Select Committee on Intelligence Chairman. Devin Nunes recuses himself from the committees probe into Russian interference in the 2016 presidential election. Mike Conaway will take the lead in this investigation'

In [73]:
event_df.loc[4232,"event_summary"]='Two people are killed in an attack in a Federal Security Service office in the Russian city of Khabarovsk. The US Israeli SITE Intelligence Group says Amaq News Agency claims the attack for Islamic State of Iraq and the Levant. The Russian Federal Security Service says the native 18 year old perpetrator was a known member of a neonazi group'

In [74]:
event_df.loc[4354,"event_summary"]='The New Orleans City Council removes the statue of Confederate President Jefferson Davis. This action is the second of four planned removals of Confederate monuments in the city'

In [75]:
event_df.loc[4011,"event_summary"]='Russian Special Envoy to Afghanistan Zamir Kabulov denies allegations by NATO Commander. Curtis Scaparrotti that Russia was perhaps supplying the Taliban'

In [76]:
event_df.loc[4817,"event_summary"]='Scientists at the Chinese Academy of Sciences successfully teleport a photon from a ground station in Tibet to a satellite orbiting Earth at distance of 500 km away. It is the first time an object has been teleported from the planet into space'

In [77]:
event_df.loc[4082,"event_summary"]="'Authorities cannot contact the South Korean cargo freighter stellar daisy. It is believed that the ship sunk off the coast of Uruguay'"

In [78]:
event_df.loc[4118,"event_summary"]='United States House Permanent Select Committee on Intelligence Chairman. Devin Nunes recuses himself from the committees probe into Russian interference in the 2016 presidential election. Mike Conaway will take the lead in this investigation'

In [79]:
event_df.loc[4144,"event_summary"]='Government aligned militias kill 16 people during a raid in Wau'

In [80]:

event_df.loc[4230,"event_summary"]='Two people are killed in an attack in a Federal Security Service office in the Russian city of Khabarovsk. The USIsraeli SITE Intelligence Group says Amaq News Agency claims the attack for Islamic State of Iraq and the Levant. The Russian Federal Security Service says the native 18 yearold perpetrator was a known member of a neonazi group'

In [81]:
event_df.loc[4597,"event_summary"]='The US Federal Reserve raises the federal funds rate by a quarter percentage point to a level between the 1 to 2'

In [82]:
event_df.loc[4427,"event_summary"]='Campaigning in the United Kingdom general election is suspended after the bombing at the Manchester Arena. Singer and actress Ariana Grande suspends her Dangerous Woman Tour'

In [83]:
event_df.loc[4477,"event_summary"]='A Summit Air Let L410 crashes after hitting a tree while landing at Lukla Airport in Nepal following a cargo flight'

In [84]:
event_df.loc[4556,'event_summary']='AlShabaab militants storm a military base in Puntland. The subsequent battle with the Somali military leaves at least 70 people dead'

In [85]:
event_df.loc[4574,'event_summary']='The National Diet of Japan passes legislation allowing Emperor Akihito to abdicate'

In [86]:

event_df.loc[4622,'event_summary']='Wildfires in central Portugal kill at least 24 people and several firefighters are among 20 injured'

In [87]:
event_df.loc[579,'event_summary']='Syrian rebels have seized control of the alTanf borderline crossing on the Iraq to Syria from militants. The rebel fighters who took the crossing reportedly entered Syria through Jordan'

In [88]:
event_df.loc[4626,'event_summary']='A coordinated suicide bombing attack on a police station in the town of Gardez in Paktia Province results in dozens of people killed and injured'

In [89]:
event_df.loc[4636,'event_summary']='At least one person has been killed and ten injured after a van runs over pedestrians outside the Finsbury Park Mosque. Police are investigating the act as a terrorist incident'

In [90]:
event_df.loc[1634,'event_summary']='Florida Governor Rick Scott declares a state of emergency as Tropical Storm Colins rain and gusty winds pelt the states west coast'

In [91]:
event_df.loc[332,'event_summary']='Turkish President Recep Tayyip Erdoğan blasts the United States over its support for Syrian Kurdish groups which Turkey considers to be terrorists'

In [92]:
event_df.loc[1312,'event_summary']='President of Venezuela Nicolas Maduro orders clocks in the country to move forward by a half hour in order to save electricity as Venezuela faces an increasing electricity shortage'

In [93]:
event_df.loc[1345,'event_summary']='Turkish Prime Minister Ahmet Davutoğlu announces his resignation effective twentytwo May amid conflict with President Recep Tayyip Erdoğan over Turkeys increasingly authoritarian rule. Davutoğlu said he would step down following an extraordinary meeting of AKP party leaders scheduled for May22'

In [94]:
event_df.loc[5349,'event_summary']='Thai Prime Minister Prayut Chanocha meets with US President Donald Trump in the Oval Office. Trump says he wants to lower US trade deficit with Thailand'

In [95]:
event_df.loc[5441,'event_summary']='Spanish Prime Minister Mariano Rajoy warns Catalonian President Carles Puigdemont that the regions autonomy will be suspended if he fails to drop Catalonian governments bid for secession by 10 AM'

In [96]:
event_df.loc[5573,'event_summary']='A Korean Peoples Army soldier defects to South Korea via the Korean Demilitarized. He was shot and injured by fellow North Korean soldiers as he crossed to South Korean side at Panmunjom'

In [97]:
event_df.loc[5672,'event_summary']='General Secretary of the Communist Party of China Xi Jinping concludes a twoday highlevel dialogue with party leaders from 120 countries. The program he announces includes full funding by Communist Party of China of 15'

In [98]:
event_df.loc[5797,'event_summary']='Francois Gabart from France sets a new solo around the world sailing record after he circumnavigates the globe in 42 days and 16 hours in his trimaran Macif. This is six days faster than previous record held by fellow Frenchman Thomas Coville'

In [99]:
event_df.loc[5797,'event_summary']='Francois Gabart from France sets a new solo around the world sailing record after he circumnavigates globe in 42 days and 16 hours in his trimaran Macif. This is six days faster than previous record held by fellow Frenchman Thomas Coville'

In [100]:
event_df.loc[5870,'event_summary']='Nine people are killed in two coordinated attacks targeting Coptic Christians in Egypt. Two of victims are killed by a gunman in a Copticowned appliance store in Helwan area of Cairo. The gunman then moves to a church where he kills a further six civilians and a policeman before being arrested'

In [101]:
event_df.loc[6027,'event_summary']='The United States will withhold dollar 65 million for Palestinian aid paid via the UN Relief and Welfare Agency stating that UNRWA needs to make unspecified reforms. The US says it will provide dollar 60 million'

In [102]:
event_df.loc[6033,'event_summary']='The South Korean Ministry of Unification announces that both North Korea and South Korea'

In [103]:
event_df.loc[6088,'event_summary']='President Jimmy Morales is questioned about high costs he spends to buy food and other luxury items'

In [104]:
event_df.loc[6100,'event_summary']='Financial analysts interpret remarks by US Secretary of the Treasury Steven Mnuchin as an indication. That US may change strong dollar policy that it has held since 1990s.'

In [105]:
event_df.loc[6246,'event_summary']='The UK government and the US White House accuse the Russian military of being responsible for the launch of the NotPetya malware in June 2017. The white house calls it the most destructive and costly cyberattack in history and says Russia will be met with unspecified international consequences'

In [106]:
event_df.loc[6424,'event_summary']='Anonymous Japanese government sources say that Japan is considering a summit meeting between Prime Minister Shinzo Abe and North Korean leader Kim JongUn'

In [108]:
for i in range(0,9500):
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace(' the ',' ')
    event_df.loc[i,'event_summary']=event_df.loc[i,'event_summary'].replace('  ',' ')

In [109]:
event_df.loc[6585,'event_summary']='Witnesses and Russias Investigative Committee say Winter Cherry complexs exits were blocked and no alarms during disaster'

In [110]:
event_df.loc[7131,'event_summary']='The New Orleans Pelicans became sixth seed or lower to sweep its firstround series since NBA switched from its bestoffive format in 2003 after their 131 to 123 game 4 win over Portland Trail Blazers. Anthony Davis scored 47 points and Jrue Holiday 41 points during win'

In [111]:
event_df.loc[7268,'event_summary']='The US led coalition in Iraq declares an end to major combat operations against in country. And it closes Coalition Forces Land Component Command headquarters'

In [112]:
event_df.loc[8464,'event_summary']='Russian officials state that country will send S300 airdefense missile system to Syria within two weeks. Russia also stated it will commence jamming radar and satellite signals of planes that attack Syrian territory from Mediterranean'

In [113]:
event_df.loc[8506,'event_summary']='The government of Pakistan is rethinking its dependence on China for loans it needs to complete their Peshawar to Karachi rail project. This is part of a broader pushback on ambitions of Chinas Belt and Road Initiative throughout region'

In [114]:
event_df.loc[9133,'event_summary']='The Department of Homeland Security requests more American troops be deployed to Mexico US border in order to add 160 miles of concertina wire alongside existing line fencing'

In [115]:
event_df.loc[9473,'event_summary']='Pakistan reports that Indian military aircraft violated their airspace near Muzaffarabad and were intercepted by Pakistan Air Force PAF military aircrafts '

In [116]:
event_df.loc[618,'event_summary']='International Womens Day is celebrated. Step It Up for Gender Equality'

In [117]:
event_df.loc[1348,'event_summary']='Head of Australias Department of Immigration Mike Pezzullo denies that detention centre for asylum seekers on Manus Island must be closed. He said there was no crisis that required any closure of despite Papua New Guineas Supreme Court ruling it to be unconstitutional and ordering release of detainees'

In [118]:
event_df.loc[1020,'event_summary']='The Ukrainian Army says eight of its soldiers were wounded in fighting against Russianbacked separatists in east of country during previous 24 hours. A military spokesman said there had been 29 shelling incidents around Mariupol'
event_df.loc[1063,'event_summary']='A second earthquake hits sourn Japan with a magnitude of 7.1 killing at least 32 people with death toll from both earthquakes rising to 42 . The new quake traps even more people. In Kumamoto a landslide occurs as well as a bridge collapse'
event_df.loc[1070,'event_summary']='The US announces that it will transfer nine Yemeni detainees from Guantanamo Bay detention camp to Saudi Arabia'
event_df.loc[1101,'event_summary']='Government of Australian external territory of Norfolk Island announces this is going to take its governance issue to United Nations. Former and final Chief Minister of island Lisle Snell said he seeks to have Norfolk Island added on UNs list of nonself-governing-territories and be given rights that are accorded under terms and conditions of being on list'
event_df.loc[1109,'event_summary']='A magnitude 6.1 aftershock has struck off coast of Ecuador at 3:33 AM '
event_df.loc[1124,'event_summary']='The United States Supreme Court rules that almost dollar 2 billion in frozen iranian assets must be turned over to American families of people killed in attacks blamed on Iran'
event_df.loc[1126,'event_summary']='Amnesty International says Nigerian Army killed 350 members of Islamic Movement and secretly buried in mass graves in city of Zaria in Kaduna State'
event_df.loc[1134,'event_summary']='The government of El Salvador unveils and deploys a new heavily armed special forces unit to fight criminal gangs in rural areas of country. Officials say this will target gang leaders who left cities because of a government crackdown'
event_df.loc[1143,'event_summary']='The US confesses it has killed 20 civilians and wounded 11 others in airstrikes in Syria and Iraq between September 10'
event_df.loc[1152,'event_summary']='A record 175 states sign UN climate agreement in New York on opening day. The agreement will enter into force once 55 countries representing at least 55 percent of global emissions formally join it'
event_df.loc[1164,'event_summary']='Government forces along with Popular Resistance militia kill dozens of AlQaeda in Arabian Peninsula fighters in clashes in sourn Yemen'
event_df.loc[1190,'event_summary']='Protests continue in Moldova as thousands of antigovernment protesters demonstrate in capital Chisinau despite concessions given to protesters last month'
event_df.loc[1212,'event_summary']='Mitsubishi Motors admits that this has used fuel economy measuring methods that have not complied with Japanese government regulations for 25 years'
event_df.loc[1220,'event_summary']='Eight soldiers and three civilians are killed at military barracks in Cape Verde. The government says this suspects missing disgruntled soldier is responsible for incident'
event_df.loc[1231,'event_summary']='Archaeologists in Taiwan discover fourtyeight sets of remains uneard in graves in Taichung. The most striking discovery among is 4'
event_df.loc[1234,'event_summary']='Prime Minister of Papua New Guinea Peter ONeill states that Manus Island Regional Processing Centre will be closed following ruling of Supreme Court and that he will ask Australian Government to make alternative arrangements for asylum seekers detained RE'
event_df.loc[1272,'event_summary']='A court in South Africa rules that decision in 2009 to drop over 750 corruption charges against President Jacob Zuma was irrational'
event_df.loc[1308,'event_summary']='Police in Indonesian provinces of Papua and West Papua arrest scores of protesters as planned demonstrations to mark anniversary of incorporation of region '
event_df.loc[1348,'event_summary']='Head of Australias Department of Immigration Mike Pezzullo denies that detention centre for asylum seekers on Manus Island must be closed. They said there was no crisis that required any closure of despite Papua New Guineas Supreme Court ruling this to be unconstitutional and ordering release of detainees'
event_df.loc[1390,'event_summary']='A criminal investigation is launched by New Hampshire attorney general against law enforcement officials after news footage showed Massachusetts/New Hampshire police appear to beat man who was surrendering at bistate car chase'
event_df.loc[1394,'event_summary']='An Australian security contractor is killed outside Australian embassy in Baghdad'
event_df.loc[1456,'event_summary']='Mexican government approves extradition of drug boss Joaquin Guzman to US following assurances that he will not face death penalty'
event_df.loc[1476,'event_summary']='China threatens to cut off regular communication with Taiwan unless they acknowledge one China principle'
event_df.loc[1506,'event_summary']='Googles offices in central Paris are raided by French finance officials as part of a tax fraud investigation . It is accused of owing euro 1.6 billion in unpaid taxes'
event_df.loc[1580,'event_summary']='A committee of US House of Representatives is looking into way Federal Reserve Bank of New York investigated ft of assets this was holding for central bank of Bangladesh'
event_df.loc[1602,'event_summary']='A second victim of UCLA shooter is found in Minnesota shooter is identified as a former PhD candidate in mechanical engineering that claimed his first victim had cleverly stolen his code'
event_df.loc[1632,'event_summary']='Three bodies have been discovered in flood waters : two in state of New South Wales and one in Australian Capital Territory. Two people are missing in Tasmania'
event_df.loc[1651,'event_summary']='The International Union of Pure and Applied Chemistry proposes final names for four new chemical elements : nihonium atomic number 113'
event_df.loc[1696,'event_summary']='A 22 yearold Dutch woman held in Qatar for nearly three months after telling police she had been raped is released following court ruling of a one year suspended prison sentence'
event_df.loc[1707,'event_summary']='An Egyptian Misdemeanor Court acquits 52 people charged with taking part in antigovernment demonstrations in April. Thousands rallied on April 25 to protest transfer of Red Sea islands Tiran and Sanafir to Saudi Arabia. Police arrested nearly 300 demonstrators government reports indicate each have been released from prison'
event_df.loc[1712,'event_summary']='Turkey fails to meet criteria set forth by European Union in order to obtain visafree travel to its member states. The EU promised to grant Turkey visafree travel only if this met specific conditions on border security and human rights'
event_df.loc[1719,'event_summary']='The Canadian House of Commons approves a bill to make lyrics in countrys national anm gender neutral'
event_df.loc[1725,'event_summary']='China cancels request to a Taiwanese childrens choir after it performed islands national anm at last months inauguration of President Tsai Ingwen Puzangalan'
event_df.loc[1732,'event_summary']='A Kenyan lower court judge upholds use of anal examinations to attempt to determine a suspects sexual orientation'
event_df.loc[1777,'event_summary']='Pope Franciss visit to Armenia this weekend may stress relations with Turkey. He is seeking to avoid reigniting diplomatic dispute that arose last year while he described 1915 mass killings of Armenians as a genocide'
event_df.loc[1788,'event_summary']='Foreign Minister Jose Garcia Margallo says Spain will seek to jointly govern Gibraltar with Britain'
event_df.loc[1797,'event_summary']='The Kanawha County sheriffs office reports death toll is now 26 three more victims were found overnight. It is thirddeadliest flood in West Virginia history'
event_df.loc[1831,'event_summary']='One of flight recorders of Egypt Air Flight 804 has been fully repaired in Paris after being found in Mediterranean Sea'
event_df.loc[1834,'event_summary']='EUs first debate on UKs vote to leave is marked by bitter exchanges as prominent proBrexit figure Nigel Farage is booed and heckled by members of European Parliament '
# event_df.loc[1883,'event_summary']='The European Union warns Switzerland that it will lose access to single market if they will impose restrictions on free movement of EU citizens'
event_df.loc[1901,'event_summary']='Hungarian Prime Minister Viktor Orban announces that country will hold a referendum on October 2 where voters will get to choose whether or not to accept EU imposed quotas on distribution of migrants'
event_df.loc[1935,'event_summary']='Protests in Harare and elsewhere in country continue despite police intimidation and please by President Robert Mugabe'
event_df.loc[1961,'event_summary']='Citibank notifies the government of Venezuela they will close the accounts of the Central Bank in 30 days after conducting a periodic risk management review'

In [119]:
event_df.loc[1982,'event_summary']='Prime Minister of Turkey Binali Yildirim calls for calm over what he states was an illegal attempt by sections of Turkish military to claim power'

In [120]:
event_df.loc[1998,'event_summary']='Four people have been injured after a man with an axe attacks people on board a train near Wurzburg in Germany'

In [121]:
event_df.loc[1883,'event_summary']='The European Union warns Switzerland that lead to lose access to single market if they will impose restrictions on free movement of EU citizens'

In [122]:
event_df.loc[1933,'event_summary']='The death of an elderly Utah woman with a Zika virus infection in late June is first reported Zikarelated death in continental US . The woman had traveled to an area where Zika is spreading. The exact cause of death has not been determined lady had an underlying medical condition'

In [123]:
# event_df.loc[332,'event_summary']=event_df.loc[332,'event_summary'].replace('ğ''g')

In [124]:
event_df.loc[332,'event_summary']= 'Turkish President Recep Tayyip Erdogan blasts United States over its support for Syrian Kurdish groups which Turkey considers to be terrorists'

In [125]:
event_df.loc[1892,'event_summary']='Turkish Foreign Minister Mevlut Cavusoglu says Turkeys cooperation with Russia in combating Islamic State in Syria does not include Russias use of its Incirlik Air Base'

In [126]:
event_df.loc[1345,'event_summary']='Turkish Prime Minister Ahmet Davutoglu announces his resignation effective twentytwo May amid conflict with President Recep Tayyip Erdogan over Turkeys increasingly authoritarian rule. Davutoglu said he would step down following an extraordinary meeting of AKP party leaders scheduled for May22'

In [127]:
event_df.loc[1994,'event_summary']='Vietnamese police bus away about two dozen would be protestors who gared at Hoan Kiem Lake in central Hanoi to rally in support of Permanent Court of Arbitrations South China Sea decision'

In [128]:
event_df.loc[2007,'event_summary']='2016 Nampala attack : At least 12 soldiers are killed and 27 others injured after unidentified militants briefly overrun a government base in central Mali'
event_df.loc[2063,'event_summary']='The International Olympic Committee states they considers all Russian athletes tainted by countrys staterun doping scheme but individual athletes can compete in 2016 Games'
event_df.loc[2075,'event_summary']='The Palestinian National Authority says this has been planning to sue United Kingdom over 1917 Balfour Declaration'
event_df.loc[2080,'event_summary']='Hillary Clinton is nominated as Democratic Party candidate for this years presidential election'
event_df.loc[2081,'event_summary']='Solar Impulse 2 becomes first solarpowered aircraft to travel around world without fuel after returns to Abu Dhabi'
event_df.loc[2099,'event_summary']='US President Barack Obamas advocates for Hillary Clinton stating there has never been anyone more qualified than Hillary to serve as president'
event_df.loc[2116,'event_summary']='The US military says this will shortly return 4'
event_df.loc[2148,'event_summary']='The US Supreme Court grants a Virginia school emergency request to stop implementation of federal government policy that calls for student use of bathroom consistent with their gender identity in order to allow board to appeal Fourth Circuit Court ruling that upheld this policy'
event_df.loc[2201,'event_summary']='Russias Federal SECURITY Service FSB says it has thwarted two armed Ukrainian incursions into Crimea with at least two killed'
event_df.loc[2287,'event_summary']='US service member becomes first US military combat casualty in Afghanistan since January 2016 while he is killed by an improvised explosive device IED while on patrol near city of Lashkar Gah in Afghanistans sourn Helmand Province. Another American service member and six Afghan soldiers were also injured in blast'
event_df.loc[2298,'event_summary']='The Turkish Armed Forces and USbacked Syrian rebels launch an initially successful campaign to capture town of Jarabulus from The Turkish Land Forces are also shelling YPG positions to prevent them from capturing areas that will retreat from'
event_df.loc[2307,'event_summary']='The search continues for survivors in central Italy with death toll now 241 . An aftershock of 4.7 MMS hits furr east in province near Norcia'
event_df.loc[2326,'event_summary']='The FARC orders all its fighters to observe a ceasefire from midnight local time Monday 1 am'
event_df.loc[2338,'event_summary']='The death toll of a suicide bombing in sourn Yemeni city of Aden rises to at least 71 . Islamic State in Iraq and Levant claims responsibility'
event_df.loc[2355,'event_summary']='Two North Korean officials are reportedly publicly executed by Kim Jongun after they allegedly disobeyed orders : former agriculture minister Hwang Min for unsuitable policies and Ri Yong Jin'
event_df.loc[2384,'event_summary']='President of Colombia Juan Manuel Santos announces that he will sign peace deal with Revolutionary Armed Forces of Colombia or FARC on September 26'
event_df.loc[2115,'event_summary']='The US Geological Survey USGS reports 7.7 magnitude earthquake has struck off Norrn Mariana Islands in Pacific Ocean. The Pacific Tsunami Warning Center says there is no tsunami threat because shock was very deep'


In [129]:

event_df.loc[2407,'event_summary']='The cases of people infected with Zika virus in Singapore jumps to 240 plus'
event_df.loc[2437,'event_summary']='Air China receives criticism in United Kingdom after they release an advertisement warning passengers from visiting areas of London populated by blacks'
event_df.loc[2537,'event_summary']='US House Intelligence Committee releases a summary of its two year investigation into former NSA contractor Edward Snowden which downplays his alleged status as a whistleblower while acknowledging tremendous damage to national security as a result of classified documents he stole'
event_df.loc[2545,'event_summary']='Abu Sayyaf frees a Norwegian hostage for a ransom of 30 million pounds'
event_df.loc[2555,'event_summary']='The 68th Primetime Emmy is held at Microsoft Theater in Los Angeles with Game of Thrones winning Emmy Award for Outstanding Drama Series'
event_df.loc[2575,'event_summary']='The Obama administration claims that Russia was responsible for bombing of a UN aid convoy near Aleppo on September 19 . Russia denies its involvement'
event_df.loc[2639,'event_summary']='The Royal Bank of Scotland announces that it will pay USdollar 1.1 billion to resolve some of its mortgage claims in United States'
event_df.loc[2654,'event_summary']='The Alabama Court of Judiciary finds Alabama Supreme Court Chief Justice Roy Moore guilty of six charges of violation of canon of judicial ethics and suspends him for remainder of his term which is slated to end in 2019 . The judge told or judges to ignore Supreme Court of US ruling on gay marriage Obergefell v. Hodges'
event_df.loc[2659,'event_summary']='Volkswagen agrees to pay its US dealers up to USdollar 1.2 billion to compensate them for their losses resulting from companys emissions cheating scandal'
event_df.loc[2684,'event_summary']='Pharmaceutical company Johnson & Johnson warns that one of its WiFi enabled insulin pumps for diabetics OneTouch Ping Pump is at risk of being hacked'
event_df.loc[2722,'event_summary']='Pope Francis announces upcoming creation of 17 new Cardinals 13 of them will be under age of 80 and thus able to vote in a future papal conclave to select new Pope'
event_df.loc[2756,'event_summary']='The death toll in North Carolina rises to 22 as flood waters continue to rise'
event_df.loc[2759,'event_summary']='The King of Thailand Bhumibol Adulyadej dies at age of 88 . He was worlds longest currently serving monarch'
event_df.loc[2760,'event_summary']='Colombian President Juan Manuel Santos extends his ceasefire with FARC rebels through ending of year'

In [130]:
event_df.loc[2782,'event_summary']='Indian Prime Minister Narendra Modi and Russian President Vladimir Putin sign several agreements including a dollar 12.9 billion defense and energy deal. Russian state oil major Rosneft pays for a controlling stake in both Indias Essar Oil and port facilities that already owns'
event_df.loc[2830,'event_summary']='A magnitude 6.6 earthquake hits Tottori Prefecture in western Japan. Local media report that there are 14 injuries in Kurayoshi. Tottori is Japans least populous prefecture'
event_df.loc[2872,'event_summary']='An unknown gunman shoots a Venezuelan police officer dead. Two other officers sustain injuries during protests against Government. Approximately 120 Opposition supporters also sustain injuries during protests'
event_df.loc[2916,'event_summary']='Battle of Boz Qandahari : Two US military personnel'
event_df.loc[2920,'event_summary']='Pakistan accuses eight Indian diplomats of espionage and terrorism amid rising tensions concerning Kashmir'


In [131]:
event_df.loc[2921,'event_summary']='A man identified as Todd Kohlhepp is arrested after authorities discover a missing woman chained up in a storage container on his property. The woman had gone missing along with her boyfriend around ending of August'
event_df.loc[2927,'event_summary']='The death toll from a boat accident near Singapore reaches 54 . The victims are mostly Indonesian migrant workers'
event_df.loc[2957,'event_summary']='The US army states that it has inadvertently killed 64 civilians in air strikes on targets in Syria and Iraq over past year'
event_df.loc[2960,'event_summary']='The Supreme Court of US hears arguments on case regarding whether citizenship claim of a child is different if there is an unmarried far versus an unmarried mor who is US citizen'
event_df.loc[2969,'event_summary']='2016 Bagram Airfield bombing : An explosion at NATOs Bagram Airfield kills four Americans and injures at least 16 US service members and a Polish soldier. The Taliban claims responsibility'

In [132]:
event_df.loc[2978,'event_summary']='Philippine president Rodrigo Duterte threatens to suspend countrys habeas corpus if forced to by what he says worsening lawlessness'

In [133]:
event_df.loc[2651,'event_summary']='The Obama administration through United States Department of Justice lowers fine against Germanys Deutsche Bank to a settlement of USdollar 5.4 billion after being handed a demand for up to 14 billion earlier this month over sale of toxic mortgage bonds'

In [134]:
event_df.loc[3009,'event_summary']='The Three UK mobile phone company admits that there has been a cybersecurity breach involving details of millions of customers'
event_df.loc[3015,'event_summary']='The World Health Organization declares an end to its global health crisis over spread of Zika virus as this has been shown to be a dangerous mosquitoborne disease like malaria or yellow fever'
event_df.loc[3056,'event_summary']='The BR Development Bank announces plans to repay up to dollar 29 billion in loans to Government of Brazil in order to stem a burgeoning deficit'
event_df.loc[3064,'event_summary']='Astronomers announce discovery of a near 3000 cubic mile subterranean deposit of ice on Mars'
event_df.loc[3073,'event_summary']='A magnitude 7.0 earthquake occurs off coast of El Salvador with potential to cause a tsunami. Nicaraguan President Daniel Ortega declares a state of emergency because of shock and Hurricane Otto'
event_df.loc[3076,'event_summary']='Saudi Arabia tells its partners in Organization of Petroleum Exporting Countries that this will not attend a planned November 28 meeting in Vienna'

In [135]:
event_df.loc[3131,'event_summary']='Susan Kiefel is appointed by Australian Prime Minister Malcolm Turnbull as next Chief Justice'

In [136]:
event_df.loc[3145,'event_summary']='The Financial Industry Regulatory Authority announces this has fined Bank of America Merrill Lynch dollar 7 million for failure to supervise use of leverage in its brokerage accounts'
event_df.loc[3152,'event_summary']='The government of Nepal proposes to amend constitution to make this more inclusive'
event_df.loc[3174,'event_summary']='The bodies of 21 coal miners are retrieved from an unlicensed coal mine in Chinese city of Qitaihe in province of Heilongjiang'
event_df.loc[3186,'event_summary']='The Peoples Republic of China lodges a complaint with US after President elect of US Donald Trump speaks with Taiwan Tsai Ingwen'
event_df.loc[3207,'event_summary']='Authorities report death toll has risen to 36 . Alameda County Sheriff Gregory Ahern told Associated Press they dont believe additional bodies will be found in debris'
event_df.loc[3233,'event_summary']='Carls Jr. Hardees executive and minimum wage reform critic Andrew Puzder is selected as US Secretary of Labor'


In [137]:
event_df.loc[3286,'event_summary']='The World Meteorological Organization WMO confirms 19 meter wave 62.4 feet recorded on 4 February 2013 in Atlantic Ocean between Iceland and United Kingdom is largest ever in history'
event_df.loc[3347,'event_summary']='President elect Donald Trump names Carl Icahn as Special Advisor to him on Regulatory Reform'
event_df.loc[3357,'event_summary']='Donald Trump names his former presidential campaign manager Kellyanne Conway as his Counselor'

In [138]:
event_df.loc[3358,'event_summary']='It is discovered that Limusaurus dinosaur shed their teeth as it matured'
event_df.loc[3373,'event_summary']='Medical research reveals shrinkage in womens brains as a result of pregnancy'
event_df.loc[3397,'event_summary']='The Polish government buys internationally known Czartoryski collection of Art'
event_df.loc[3430,'event_summary']='The Islamic State in Iraq and Levant claims responsibility for attack in what that claims is a response to Turkeys actions in neighbouring Syria'
event_df.loc[3450,'event_summary']='The National Aeronautics and Space Administration NASA announces selection of two new Discovery Program space exploration missions : Lucy'
event_df.loc[3464,'event_summary']='A cold spell with temperature reaching minus 30 °C in Moscow and or parts of Eastern Europe hits Europe. Nearly 20 people die in recent days 10 in Poland'
event_df.loc[3487,'event_summary']='Iran confirms receipt of Saudi invitation to discuss bilateral talk for Hajj 2017 . The Iranian delegation is expected to travel to Saudi Arabia on 23 February this year for participation in next pilgrimage'

In [139]:
event_df.loc[3537,'event_summary']='Oman receives 10 former detainees of Guantanamo Bay detention camp following a request by US to take them'
event_df.loc[3573,'event_summary']='Japanese toilet industries agreed to standardize iconography of electric toilet seat controls in order to make them less confusing for users'
event_df.loc[3581,'event_summary']='The US Senate confirms first two members of President Donald Trumps Cabinet : retired Marine General James Mattis as Secretary of Defense'
event_df.loc[3605,'event_summary']='President Adama Barrow names Fatoumata Tambajang as Vicepresident of Gambia'
event_df.loc[3611,'event_summary']='Burkina Faso and Swaziland refuse to break relations with Taiwan and recognize Onechina policy despite being offered aid from China'
event_df.loc[3626,'event_summary']='President Adama Barrow returns to Gambia after being sworn in as president in Senegal'
event_df.loc[3641,'event_summary']='An Italian court commands former Prime Minister Silvio Berlusconi to stand trial on April 4 on charges of allegedly bribing witnesses with euro 10 million USdollar 11 million in order to silence them over accusations he paid for sex with young women'
event_df.loc[3649,'event_summary']='The Ukrainian military says seven soldiers have been killed by proRussian separatists since Sunday. The separatists report over 5 days of artillery attacks on them by Ukrainian side'
event_df.loc[3655,'event_summary']='The Parliament votes in favour of a reciprocal travel ban on United States citizens if US President Donald Trumps executive order barring citizens of Iraq and six or Muslim majority countries is not reversed'
event_df.loc[3669,'event_summary']='President Donald Trump has nominated Judge Neil Gorsuch to fill vacant seat on Supreme Court of US . Neil Gorsuch is youngest nominee to court in 25 years'
event_df.loc[3674,'event_summary']='IRANIAN Minister of Defence Hossein Dehghan confirms Iran tested a new missile'
event_df.loc[3682,'event_summary']='Former HBOS manager Lynden Scourfield  and consultants are found guilty of corruption and abuse of power in stealing Pound 245 million from bank and small businesses in a loans scam'
event_df.loc[3686,'event_summary']='The US Department of Treasury announces new sanctions against Iran in response to latters recent ballistic missile test. Thirteen people and twelve entities with bind to Iran have been affected'
event_df.loc[3692,'event_summary']='Foreign Minister Julie Bishop says Australia will honor agreement to accept refugees from Central America even though US has postponed interviews with asylum seekers in a camp at Pacific island of Nauru'
event_df.loc[3696,'event_summary']='The Department of Homeland Security says this has stopped enforcing executive order per Judge James Robarts ruling in State of Washington v. Trump. The State Department activates visas that had been previously suspended because of this order'
event_df.loc[3720,'event_summary']='Incumbent Australian Senator Cory Bernardi defects from centreright Liberal Party  to establish his own minor party'
event_df.loc[3726,'event_summary']='The US District Court for District of Columbia blocks health insurer Anm Inc s proposed dollar 54 billion merger along rival Cigna because it would have exacerbated an already highly concentrated market and likely raised prices'
event_df.loc[3729,'event_summary']='The International Committee of Red Cross announces there will be temporarily halting some of its operations in Afghanistan after gunmen killed six of its workers yesterday'
event_df.loc[3735,'event_summary']='The appeal of Trump administration is denied as 9th US Circuit Court of Appeals said there would not block a lowercourt ruling that brought presidents executive order to halt'
event_df.loc[3758,'event_summary']='Adele wins Record of Year and Song of Year for Hello and Album of Year for 25 . Chance Rapper wins Grammy Award for Best New Artist'
event_df.loc[3788,'event_summary']='The US Justice Department tells ninth circuit court of Appeals that there wont be seeking furr action by court since this executive order will soon be replaced by a different one'
event_df.loc[3814,'event_summary']='Demonstrations spread to second city of Belarus Gomel where 2'
event_df.loc[3835,'event_summary']='An Austrian court grants a US request to extradite Ukrainian businessman Dmytro Firtash. US officials accuse Firtash of being involved in a scandal as he allegedly paid USdollar 18'

In [140]:
event_df.loc[3890,'event_summary']='The Hershey Company announces it will cut about 15 percent of its global workforce 2'
event_df.loc[3894,'event_summary']='German police storm a refugee center in Hamburg after a knifewielding man barricades himself in a room with a pregnant woman believed to be his partner'

In [141]:
event_df.loc[3903,'event_summary']='President Omar alBashir names Vice President Bakri Hassan Saleh as Prime Minister of Sudan'
event_df.loc[3920,'event_summary']='US President Donald Trump accuses former President Barack Obama of wiretapping Trump Tower month before 2016 presidential election but offers no evidence to support his claim. A spokesman for President Obama rejects these claims'
event_df.loc[3983,'event_summary']='Thousands of Iraqis flee western Mosul as battle between iraqi and allied forces and militants escalates in densely populated Old City'


In [142]:
event_df.loc[3991,'event_summary']='The US House Permanent Select Committee on Intelligence holds a hearing about Russian interference in 2016 election and confirms that there is an ongoing investigation into ties between Trumps team and RUSSIA '

In [143]:
event_df.loc[3233,'event_summary']='Carls Hardees executive and minimum wage reform critic Andrew Puzder is selected as US Secretary of Labor'

In [144]:
event_df.loc[4011,'event_summary']='Russian Special Envoy to Afghanistan Zamir Kabulov denies allegations by NATO Commander'
event_df.loc[4013,'event_summary']='Russian Special Envoy to Afghanistan Zamir Kabulov denies allegations by NATO Commander'
event_df.loc[4016,'event_summary']='Proactiva notes finding of five corpses Libyan coast these were floating near two capsized boats which could each hold more than 100 people'
event_df.loc[4017,'event_summary']='French National Front presidential candidate Marine Le Pen meets with Russian president Vladimir Putin and afterwards urges that European Union sanctions on RUSSIA be lifted'
event_df.loc[4022,'event_summary']='The replacement plan for Patient Protection and Affordable Care Act aka Obamacare is withdrawn after Republican leaders fail to gain enough support. The failure of Trump administration to repeal act means there will remain law in US'
event_df.loc[4045,'event_summary']='Authorities find remains of two missing UN investigators former Swedish politician Zaida Catalan and US national Michael Sharp in a shallow grave in province of KasaiCentral'
event_df.loc[4082,'event_summary']='Authorities cannot contact South Korean cargo freighter stellar daisy. It is believed that ship sunk off coast of Uruguay'
event_df.loc[4170,'event_summary']='The Afghan Ministry of Defense reports as many as 36 suspected militants were killed while no civilians were harmed in yesterdays bombing in Nangarhar Province using socalled mor of all bombs GBU43 . The ministry spokesman added these deaths have not been independently verified'
event_df.loc[4198,'event_summary']='Paraguayan President Horacio Cartes says he will not be  candidate in next years presidential election regardless of Congresss action on constitutional amendment that would allow second terms'
event_df.loc[4257,'event_summary']='Turkish airstrikes kill 18 Kurdish YPG fighters and media officials in norastern Syria. Also five Peshmerga fighters are killed during Turkish attack on Sinjar in Iraq. Turkey also claims to have destroyed terror hubs. Iraq denounces hit as a violation of its sovereignty'
event_df.loc[4283,'event_summary']='A South Korean adviser says it is impossible for Southkorea to purchase THAAD missile complex since control of its operation would remain with US'
event_df.loc[4382,'event_summary']='The US Supreme Court rules that North Carolina state legislative members do not have standing to request an appeal of US Court of Appeals for Fourth Circuit ruling against a law which found discriminated against black voters'
event_df.loc[4384,'event_summary']='The cybersecurity firms Kaspersky Lab and Symantec report that technical evidence connects WannaCry ransomware attack to North Korean backed Lazarus Group. Northkorea is also believed to be responsible for previous cyberattacks on SWIFT banking system and against Sony Pictures'
event_df.loc[4418,'event_summary']='A controversial piece written in The Atlantic magazine about Filipino servant caste and Filipino American family involved which triggers a debate in both Philippines and US'
event_df.loc[4419,'event_summary']='Because of a nationwide shortage of intravenous sodium bicarbonate'
event_df.loc[4422,'event_summary']='The US Supreme Court rejects two of North Carolinas congressional districts because they violated Constitution by relying too heavily on race in drawing M'
event_df.loc[4429,'event_summary']='The US Navy SEAL Team Sixs raid on an Al Qaeda in Yemen compound in Marib Governorate kills at least seven militants'
event_df.loc[4466,'event_summary']='The National Constitutional Convention of Aboriginal Australians and Torres Strait Islanders at Mutitjulu concludes with Indigenous leaders calling for a treaty'
event_df.loc[4486,'event_summary']='The Philippine military announces that there has discovered bodies of 16 people'
event_df.loc[4522,'event_summary']='The Movie Premiere of Captain Underpants : The First Epic Movie'
event_df.loc[4527,'event_summary']='SpaceX launches a Falcon 9 rocket with a shipment of food and supplies in a refurbished Dragon cargo capsule for International Space Station. The mission reuses a Dragon cargo vessel that was previously flown in a September 2014 mission'
event_df.loc[4540,'event_summary']='Bharat Space Research Organisation successfully launches communications satellite GSAT19 through its heaviest rocket Geosynchronous Satellite Launch Vehicle Mark III Times of India'
event_df.loc[4572,'event_summary']='A suicide bomber at a market in Musayyib kills 31 and wounds 35'
event_df.loc[4573,'event_summary']='United Launch Alliance says there was not given an opportunity to bid against rival SpaceX for upcoming launch of US Air Force miniature X37B space plane. The Air Force declined to comment'
event_df.loc[4587,'event_summary']='Maryland and District of Columbia attorneys general plan to sue President Trump on Monday claiming he violated emolument clauses in Constitution by accepting foreign payouts for his hotelier empire'
event_df.loc[4692,'event_summary']='The Supreme Court of United States partially reinstates President Donald Trumps travel ban and invalidates certain injunctions that were put on order by two federal appeals courts earlier. Final oral hearings concerning legality of Executive Order 13780 will be held in October 2017 at Supreme Court'
event_df.loc[4736,'event_summary']='The UK announces it is withdrawing from 1964 London Fisheries Convention'
event_df.loc[4795,'event_summary']='The summit announces there is unable to gain agreement on climate change between US and other 19 members of this international forum'
event_df.loc[4816,'event_summary']='The Trump Administration announces this years presidential state visit to United Kingdom is delayed until at least 2018 . Both White House and 10 Downing Street state two countries had been unable to agree on a 2017 date'
event_df.loc[4819,'event_summary']='Donald Trump Jr discloses emails which he and Rob Goldstone discuss garing opposition research against Hillary Clinton through  June 2016 meeting with Russian lawyer Natalia Veselnitskaya'
event_df.loc[4860,'event_summary']='DPR leader Alexander announced that selfdeclared Donetsk Peoples Republic DPR and Luhansk Peoples Republic LPR would form a new state called Malorossiya Little Russia as an official successor to what he called failed state of Ukraine'
event_df.loc[4889,'event_summary']='Poles march against a bill that critics say might decrease judicial independence in Poland. Hungary has supported bill while European Union has opposed. The protesters hope that President Andrzej Duda would intervene against proposed law'
event_df.loc[4900,'event_summary']='The parents of terminally ill Charlie Gard give up their legal challenge over treatment in US . The latest medical reports indicate that window of opportunity no longer exists'
event_df.loc[4923,'event_summary']='President Vladimir Putin appoints Vasily Nebenzya to be new Permanent Representative of Russia to UN following sudden death of Vitaly Churkin in February'
event_df.loc[4942,'event_summary']='Adrian Beltre of Texas Rangers becomes 31st player with three'
event_df.loc[4956,'event_summary']='President of US Donald Trump signs Countering Americas Adversaries Through Sanctions Act'
event_df.loc[4990,'event_summary']='Two Cuban diplomats are expelled from Embassy in Washington'
event_df.loc[4994,'event_summary']='Five transgender US military personnel sue President Donald Trump and top Pentagon officials over Presidents policy change announced late last month forbidding transgender people from serving. The suit asks court to prevent ban from going into effect'


In [145]:
event_df.loc[5003,'event_summary']='At least 56 migrants drown in Red Sea while traveling from Horn of Africa to Yemen. Human traffickers had forced 300 people aboard two boats into sea'
event_df.loc[5026,'event_summary']='International Criminal Court issues an arrest warrant against Mahmoud alWerfalli for war crime of murder following circulation of several videos in which he appears to oversee execution of over 30 prisoners'
event_df.loc[5040,'event_summary']='The South African Police Service issues a red alert at borders to prevent First Lady of Zimbabwe Grace Mugabe from leaving country. She is wanted on charges of assault with intent to cause grievous bodily harm on a 20 yearold woman in a hotel room in Johannesburg'
event_df.loc[5069,'event_summary']='The director of BBC World Service says it is prepared for Northkorean governments reaction over targeted launch of a radio service on North Korea in September'
event_df.loc[5110,'event_summary']='The SouthKorean military reports NorthKorea has fired several shortrange projectiles into sea from its eastern Kangwon province'
event_df.loc[5123,'event_summary']='India and China agree to end a two monthlong standoff with withdrawal of Indian troops. The standoff began in June after China began constructing a road in disputed territory of Doklam which is claimed by both China and Bhutan'
event_df.loc[5124,'event_summary']='President Michelle Bachelet sends a bill to Congress for legalization of samesex marriage in Chile and adoption by samesex couples'
event_df.loc[5127,'event_summary']='Mexican authorities say two suspected thieves died after a mob beat them and four others in Tlatlauquitepec'
event_df.loc[5174,'event_summary']='US Federal Reserve Vice Chair Stanley announces he will resign in midOctober'
event_df.loc[5224,'event_summary']='Bangladeshi Prime Minister Sheikh Hasina accuses Burmese government of atrocities against Rohingya people and calls for these alleged atrocities to stop'
event_df.loc[5225,'event_summary']='Apple Inc announces three new iPhone models : iPhone 8'
event_df.loc[5245,'event_summary']='An explosion on a train at Parsons Green tube station in London injures 29 . Scotland Yard is treating incident as a terrorist attack'
event_df.loc[5259,'event_summary']='A British Airways airplane is evacuated at Paris Charles de Gaulle Airport after a direct threat was made against this'
event_df.loc[5310,'event_summary']='The king of Saudi Arabia issues a decree allowing women to be issued driving licenses by June 2018 . Saudi Arabia is worlds last sovereign state that does not allow women to drive'
event_df.loc[5351,'event_summary']='Two women charged along assassination of Kim Jongnam plead not guilty in a Malaysian court because they thought it was a TV prank. Kim Jongnam was eldest son of deceased North Korean leader Kim Jongil and halfbror of current North Korean leader Kim Jongun'
event_df.loc[5394,'event_summary']='President of Catalonia Carles Puigdemont gives a speech regarding independence from Spain while he proposes to suspend effect of independence declaration in order to hold talks with Madrid'
event_df.loc[5398,'event_summary']='The Boy Scouts of America announces that girls may join as full members of Cub Scouts beginning in 2018 . Young women may join as full members of Boy Scouts and earn highest rank of Eagle Scout beginning in 2019'
event_df.loc[5496,'event_summary']='Paul Manafort and Rick Gates surrender to FBI after both are indicted on multiple charges stemming from investigation into Donald Trump presidential campaigns possible associations with Russian government'
event_df.loc[5517,'event_summary']='US President Donald Trumps main social media account is suspended for 11 minutes'
event_df.loc[5554,'event_summary']='The US Department of Justice antitrust chief has told AT&T that they must sell off eir DirecTV or Turner Broadcasting System parent of CNN in order to complete its acquisition of Time Warner'
event_df.loc[5580,'event_summary']='Thousands of Yemenis protest a blockade led by a Saudi Arabian coalition'
event_df.loc[5607,'event_summary']='Martin Truex Jr. wins seasonending 2017 Ford EcoBoost 400 and along it his first title of NASCAR Cup Series. The race also marks final Cup Series appearance for Dale Earnhardt Jr'
event_df.loc[5623,'event_summary']='Bangladeshs Foreign Minister A. H. Mahmood Ali and Myanmars State Counsellor Aung San Suu Kyi agree to return Rohingya refugees in a two month period'
event_df.loc[5628,'event_summary']='President Vladimir Putin signs into law amendments that allow foreign media outlets in Russia to be listed as foreign agents'
event_df.loc[5642,'event_summary']='A Soyuz 2.1 bs Fregat upper stage malfunctions during MeteorM No 21s launch from Vostochny Cosmodrome'
event_df.loc[5666,'event_summary']='Former president of Yemen Ali Abdullah Saleh suggests that he is open to talking to Saudiled coalition that his forces have been fighting for years'
event_df.loc[5672,'event_summary']='General Secretary of Communist Party of China Xi Jinping concludes a twoday highlevel dialogue with party leaders from 120 countries. He announces includes full funding by Communist Party of China of 15'
event_df.loc[5686,'event_summary']='Eurofighter GmbH offers Belgium a national cyber defense network suggesting telecommunications security on par with United Kingdom intelligence'
event_df.loc[5700,'event_summary']='Investigators discover brain abnormalities in victims. They are now carefully not using term sonic to describe attacks and there is growing skepticism which was caused by a sonic device'
event_df.loc[5704,'event_summary']='Police raid wrong tent of an activist camp in Kiev and fail to arrest stateless opposition leader Mikheil Saakashvili. A police source says police are preparing a special operation and will be unleashed in near future'
event_df.loc[5725,'event_summary']='Mikheil Saakashvili is arrested again by National Police of Ukraine. He was on run since December 5 . He has been leading anticorruption rallies against Petro Poroshenko'
event_df.loc[5744,'event_summary']='Corsican nationalists demand talks with French government after a convincing win in second round of elections for a reformed regional government'
event_df.loc[5795,'event_summary']='Australian Federal Police arrest naturalized North Korean Chan Han Choi for violating UN and Australian sanctions by acting as an economic agent for Northkorea'
event_df.loc[5851,'event_summary']='Tunisias Transport Ministry suspends Emirates Airlines flights'
event_df.loc[5853,'event_summary']='A suicide blast near National Directorate of Security headquarters in Kabul kills 10 . Amaq News Agency claims is responsible for attack'
event_df.loc[5908,'event_summary']='Prime Minister Hailemariam Desalegn announces that Ethiopia will drop charges against all political prisoners and close down infamous prison camp of Maekelawi'
event_df.loc[5909,'event_summary']='Two new Democratic senators Doug Jones of Alabama and Tina Smith of Minnesota are sworn in'
event_df.loc[5911,'event_summary']='Security researchers disclose two hardware vulnerabilities Spectre'
event_df.loc[5923,'event_summary']='A hot air balloon crashes due to strong winds in Egypts Luxor Governorate. A tourist from Australia is killed and 12 other tourists are injured. The Egypt Aviation Authority says there were 20 passengers on balloon'
event_df.loc[5929,'event_summary']='Sixtime US NASA astronaut John Young dies at age of 87 . He was 9th man who walked on Moon'
event_df.loc[5943,'event_summary']='The Pakatan Harapan alliance chooses 92 yearold former prime minister Mahathir Mohamad as their candidate Prime Minister in upcoming Malaysian general election. Opposition leader Anwar Ibrahim will be released from jail on June 8 . Mahathir and Anwar join forces in election'
event_df.loc[5998,'event_summary']='The USled coalition confirms reports that they will form a new 30'
event_df.loc[5196,'event_summary']='Brazilian prosecutor Rodrigo Janot files charges in Supreme Court against officials in President Michel Temers Brazilian Democratic Movement Party accusing  of forming a criminal organization'
event_df.loc[5354,'event_summary']='Scottish Government Energy Minister Paul  announces that he will seek an indefinite ban an existing moratorium has been in place since 2015 on crude oil recovery in Scotland by means of process of hydraulic fracturing'
event_df.loc[5386,'event_summary']='Iceland qualifies for 2018 FIFA World Cup after defeating Kosovo two to zero to win UEFA Group one'
event_df.loc[5802,'event_summary']='The United States vetoes a UN Security Council resolution calling for this to withdraw its declaration of a capital in Jerusalem'
event_df.loc[5870,'event_summary']='Nine people are killed in two coordinated attacks targeting Coptic Christians in Egypt. Two of victims are killed by a gunman in a Copticowned appliance store in Helwan area of Cairo. Gunman moves to a church while he kills a furr six civilians and a policeman before being arrested'
event_df.loc[5898,'event_summary']='Vice media suspends two top executives as it investigates allegations made against them '





In [146]:
event_df.loc[6017,'event_summary']='Nephew of assassinated Egyptian president Mohamed Anwar alSadat announces that He will not run in Marchs presidential election'
event_df.loc[6027,'event_summary']='The US will withhold dollar 65 million for Palestinian aid paid via UN Relief and Welfare Agency stating that UNRWA needs to make unspecified reforms'
event_df.loc[6029,'event_summary']='Temperatures reach minus 67 °C minus 89 °F in Russias Yakutia region'
event_df.loc[6033,'event_summary']='The South Korean Ministry of Unification announces that both Northkorea and Southkorea'
event_df.loc[6048,'event_summary']='Twitter announces this has notified 677'
event_df.loc[6076,'event_summary']='The US Senate reaches an agreement to reopen federal agencies through to February 8 . A.bill is working its way through legislative process. The first Senate vote was 81 to 18'
event_df.loc[6091,'event_summary']='The USled coalition against says there has killed up to 150 militants in air strikes on a headquarters in Deir ezZor Governorate'
event_df.loc[6104,'event_summary']='Two bills are unanimously approved by Florida House and Senate Committees that propose moving state permanently to Daylight Saving Time 04:00 '
event_df.loc[6154,'event_summary']='YouTube announces that YouTubers who make egregious content will be punished'
event_df.loc[6161,'event_summary']='Epcot announces that Circle of Life : An Environmental Fable would close permanently'
event_df.loc[6228,'event_summary']='Former President Alvaro Colom and his entire government cabinet were arrested for their alleged participation in a new corruption case investigated by CICIG and MP . They were sent to preventive detention at Mariscal Zavala Military Center'
event_df.loc[6246,'event_summary']='The UK government and US White House accuse Russian military of being responsible for launch of NotPetya malware in June 2017'
event_df.loc[6262,'event_summary']='An Iran Aseman Airlines ATR 72 commercial aircraft carrying 59 passengers and 6 crew members crashes near Iranian town of Semirom'
event_df.loc[6275,'event_summary']='A court in Thailand awards Japanese man paternity rights over 13 of his children from THAI surrogate mors'
event_df.loc[6294,'event_summary']='US President Donald Trump meets with Australian Prime Minister Malcolm Turnbull in White House. Trump indicated that there would be new sanctions against North Korean regime'
event_df.loc[6301,'event_summary']='Archbishop of Guatemala City Oscar Julio Vian Morales died at age 70 . Acting President Jafeth Cabrera decrees three days of national mourning'
event_df.loc[6353,'event_summary']='The Florida Senate rejects a bill to ban assault weapons and holds a moment of silence and reflection for Parkland'
event_df.loc[6358,'event_summary']='South African officials determine that countrys ongoing listeriosis outbreak which is already worlds deadliest listeriosis outbreak'
event_df.loc[6394,'event_summary']='Nearearth asteroid 2017 VR12 makes a flyby past Earth'
event_df.loc[6424,'event_summary']='Anonymous japanese government sources say that Japan is considering a summit meeting between Prime Minister Shinzo Abe and North Korean leader Kim JongUn'
event_df.loc[6485,'event_summary']='Former French President Nicolas Sarkozy is happened for up to 48 hours and questioned by police in Nanterre over allegations that he illegally accepted euro 50 million from Libyan leader Muammar Gaddafi to finance his bid in 2007 presidential election'
event_df.loc[6502,'event_summary']='Israel accepts for first time that it carried out an airstrike on a suspected nuclear reactor in Deir ezZor Governorate'
event_df.loc[6509,'event_summary']='The Independent claims Metropolitan Police misidentified material in convicted bomber Ahmad Hassans possession as not related to ISIS when in fact this was produced by group'
event_df.loc[6521,'event_summary']='Qatars Interior Ministry releases a list of individuals and entities which are linked to terrorism'
event_df.loc[6522,'event_summary']='Polands ruling Law and Justice proposes changes to planned judicial reforms in response to European Union criticisms plans threaten judicial independence'
event_df.loc[6547,'event_summary']='Former President of South Korea Lee Myungbak is detained on charges of taking bribes while he was in office'
event_df.loc[6566,'event_summary']='A friend of poisoned exiled russian spy Sergei Skripal claims Skripal had written to Vladimir Putin asking to return to Russia'
event_df.loc[6569,'event_summary']='Peruvian exPresident Pedro Pablo Kuczynskis homes are raided by police investigating Operation Car Wash'
event_df.loc[6600,'event_summary']='NATO says Afghan Air Force dropped its first laserguided bomb on a Taliban compound on March 22 . NATO have trained Afghans in use of equipment'
event_df.loc[6606,'event_summary']='Chilean search and rescue authorities declare that a crewman who fell overboard from a competitor vessel is lost at Sea'
event_df.loc[6623,'event_summary']='California Highway Patrol search and rescue operations continue off Californian coast for three children missing following a crash which killed five of their relatives'
event_df.loc[6656,'event_summary']='A pair of women accuse The Ren & Stimpy Show creator John Kricfalusi of sexually abusing them in 1990s while they were minors'
event_df.loc[6697,'event_summary']='The Malaysian Maritime Enforcement Agency claims a Vietnamese fishing vessel tried to ram one of their boats when they tried to detain  for illegally entering and fishing from malaysian waters'
event_df.loc[6723,'event_summary']='Botswanan President Ian Khama retires from office. Mokgweetsi Masisi has inaugurated as fifth President of botswana'
event_df.loc[6733,'event_summary']='Nine people have died amid violent protests involving tens of thousands of protesters from SC/ST caste groups across India'
event_df.loc[6734,'event_summary']='The Egyptian Parliament approves a draft law creating 18member Supreme Council for Combating Terrorism and Extremism'
event_df.loc[6739,'event_summary']='Israeli Defence Minister Avigdor Liberman says nation will maintain its tactics at Gazan border of shooting anybody who approaches Fence'
event_df.loc[6760,'event_summary']='The WWF describes Germanys rivers as being in a state bordering on critical after this emerges more than 90 percent do not meet European Union standards for cleanliness and ecological quality'
event_df.loc[6767,'event_summary']='A court in Kuwait sentences a Lebanese man and his Syrian wife to death in absentia for murder of their Filipino maid. The case sparked an Interpol manhunt and diplomatic tensions'
event_df.loc[6816,'event_summary']='An arrest warrant is issued for Ultimate Fighting Championship UFC lightweight champion Conor McGregor after he was involved in a melee at a press conference at Barclays Center in New York City ahead of UFC 223 . Video footage appears to show McGregor throwing a hand truck through a window of Khabib Nurmagomedov team bus'
event_df.loc[6829,'event_summary']='Former President of South Korea Park Geunhye is sentenced to 24 years in prison and an 18 billion fine for bribery'
event_df.loc[6840,'event_summary']='Israeli troops shoot dead ten Palestinians near israel to Gaza barrier'
event_df.loc[6868,'event_summary']='The Metropolitan Police in London launches a war crimes investigation into five men wanted in Rwanda for alleged massacres in 1994 . A.United Kingdom court previously refused to extradite men over concerns they may not receive a fair trial'
event_df.loc[6886,'event_summary']='Extremist Muslim preacher Kiki Muhammad Iqbal is sentenced to nine years for inciting terrorism for  sermon. He gave last year at  mosque in Bandung. The sermon is alleged to have caused two suicide bombers to launch a May 2017 attack that killed three policemen in East Jakarta'
event_df.loc[6891,'event_summary']='Yulia Skripal is released from hospital. Russia says this will view any resettlement efforts by United Kingdom as abduction'
event_df.loc[6914,'event_summary']='An Italian judge says a mafia clan has been plotting murder of Spiait journalist Paolo Borrometi. Italian prime minister Paolo Gentiloni voices his support to journalist'
event_df.loc[6933,'event_summary']='Family of a man killed in California while his Tesla Model them crashed with Autopilot engaged says they intend to sue carmaker. His wife furr says he had complained of flaws in vehicles behaviour and predicted his death in a collision with barrier his car ultimately hit'
event_df.loc[6946,'event_summary']='The Organisation for Prohibition of Chemical Weapons states this agrees with UK authorities on their analysis of identity of toxic chemical used against Skripals'
event_df.loc[6973,'event_summary']='Three Syrian nationals are arrested in Saarland suspected of terror links. Two are suspected of fighting with Islamic State in syria'
event_df.loc[6989,'event_summary']='Yemen accuses Iran of arming Houthi rebels with drones in violation of UN sanctions to allow militants to launch attacks on Saudi Arabia. Iran supports Houthis but denies arming them'



In [147]:
event_df.loc[7038,'event_summary']='SpaceXs scheduled launch of NASAs Transiting Exoplanet Survey Satellite TESS from Cape Canaveral Air Force Station is delayed until April 18 . TESS is designed to search for exoplanets using transit method and is 400 times more powerful than Kepler space observatory'
event_df.loc[7040,'event_summary']='Bombardier announces an increase in range for Global seven thousand business aircraft to 7'
event_df.loc[7056,'event_summary']='UK media regulator Ofcom launches investigations into RT over possible breaches of impartiality rules in its coverage of poisoning'
event_df.loc[7081,'event_summary']='A woman goes on trial in England accused of murdering a man who was voluntarily euthanised in Belgium after she allegedly attacked him with acid'
event_df.loc[7123,'event_summary']='The Arab Emirates says Qatari jet fighters intercepted a passenger plane heading to Bahrain and flew dangerously close to it'
event_df.loc[7125,'event_summary']='Indian lawmakers approve capital punishment for man who rape children under age of 12 . Prime Minister Narendra Modi signs measure'
event_df.loc[7131,'event_summary']='The New Orleans Pelicans became sixth seed or lower to sweep its firstround series since NBA switched from its bestoffive format in 2003 after their 131 to 123 game 4 win over Portland Trail Blazers. Anthony Davis scored 47 points and Jrue Holiday 41 points during win'
event_df.loc[7150,'event_summary']='UK Health Secretary Jeremy Hunt writes to social media firms including Google and Facebook giving them until end of month to come up with ways to counter online bullying'
event_df.loc[7156,'event_summary']='Israeli law makers Yuval Steinitz and Oren Hazan accuse Jerusalem born actress Natalie Portman of antisemitism and seek to revoke her citizenship with Hazan calling her little hyprocrite liar after she decides not to travel to israel and accept USdollar 2 million Genesis Prize'
event_df.loc[7161,'event_summary']='Southwest Airlines cancels 128 flights in addition to 40 cancelled yesterday as that inspects CFM567B engines mounted to its Boeing 737 fleet following a fatal accident'
event_df.loc[7177,'event_summary']='The Transportation Safety Board of Canada reports aircraft departed with ice on that before losing height shortly after takeoff. The December 17 crash killed one and injured fifteen'
event_df.loc[7198,'event_summary']='Israeli border police officer Ben Deri receives a 9 month sentence for fatally shooting Palestinian teen Nadeem Nawara in 2014 . Deri was convicted of causing unarmed boys death by negligence'
event_df.loc[7200,'event_summary']='Scotlands Parliament approves a bill devolving authority for social care payments'
event_df.loc[7231,'event_summary']='German Chancellor Angela Merkel and US President Donald Trump hold a joint press conference at White House. Merkel states she believes that there can be a bilateral trade deal between European Union and US'
event_df.loc[7239,'event_summary']='A photograph from Hubble Space Telescope reveals a companion star that survived explosion of a supernova in galaxy NGC 7424 . This brings strong evidence to a ory according to which Type IIb strippedenvelope supernovae are due to stellar companions capturing hydrogen from progenitor stars envelope before its explosion'
event_df.loc[7268,'event_summary']='The US led coalition in Iraq declares an end to major combat operations against in country'
event_df.loc[7279,'event_summary']='Polish Foreign Minister Jacek Czaputowicz says nation will oppose European Union budget orders set to be introduced on May 2 by European Commission. The proposals would see funding in 20212027 budget cut for countries where democratic principles and rule of law are deemed under threat'
event_df.loc[7308,'event_summary']='Louisiana Secretary of State Tom Schedler announces that He will resign in one week'
event_df.loc[7386,'event_summary']='Russian President Vladimir Putin is inaugurated at Grand Kremlin Palace in Moscow for a fourth term as President of russia following his victory in Marchs presidential election'
event_df.loc[7395,'event_summary']='Junior officer'
event_df.loc[7399,'event_summary']='Theresa May confirms her trust in Foreign Secretary Boris Johnson after called her post Brexit trade policy with European Union crazy'
event_df.loc[7411,'event_summary']='Four neoNazis are convicted of attempting to incite racial hatred at Aston University in England by carrying out a sticker recruitment campaign for National Action. A.fifth is acquitted and sentencing alongside two or convicts is set for June 1 . National Action has since been banned as a terror group'
event_df.loc[7446,'event_summary']='A pilot is injured while a cockpit window breaks and he is partially sucked out of Airbus A319 operating Sichuan Airlines Flight 8633 . The aircraft lands safely at Chengdu'
event_df.loc[7450,'event_summary']='President Vladimir Putin opens auto part of 19kilometre 12 milong roadandrail Kerch Strait Bridge connecting Crimea with Russia'
event_df.loc[7456,'event_summary']='Luxembourg Green Party politician and government secretary Camille Gira dies after he collapsed while delivering a speech to parliament'
event_df.loc[7450,'event_summary']='Russian President Vladimir Putin opens auto part of 19kilometre 12 milong roadandrail Kerch Strait Bridge connecting Crimea with russia'
event_df.loc[7457,'event_summary']='Michigan State University announces that this will settle with sexual assault victims of Larry Nassar for over dollar 500 million'
event_df.loc[7475,'event_summary']='All 34 Roman Catholic bishops in Chile offer to resign after Pope Francis accused them of destroying evidence of sexual crimes'
event_df.loc[7490,'event_summary']='The Syrian government declares Damascus as completely safe from militant groups for first time in seven years'
event_df.loc[7498,'event_summary']='The European Commission recommends to remove France from excessive deficit procedure that entered in 2009'
event_df.loc[7525,'event_summary']='Police in India state that mobs have killed three people after social media warned of roaming gangs of child kidnappers. They say that there is no evidence of such gangs'
event_df.loc[7545,'event_summary']='2014 IndyCar Series champion Will Power of Australia wins 102nd running of Indianapolis 500 . It is Danica Patricks final race before her retirement'
event_df.loc[7546,'event_summary']='Polands Minister of Defence Mariusz Blaszczak says he recently talked with US officials in Washington D.C. about permanently stationing thousands of US troops in poland as a deterrent against Russia'
event_df.loc[7556,'event_summary']='The US Government announces a 25 percent import tariff on USdollar 50 billion of Chinese goods with industrially significant technology. A full list of affected products will be published on June 15 . Investment restrictions and enhanced export controls are to be announced on June 30'
event_df.loc[7571,'event_summary']='The European Court of Human Rights rules that Romanian and Lithuanian governments each knowingly hosted CIA secret prisons around 2005 . Both countries also participated in US extraordinary rendition program : one case by each country is acknowledged'
event_df.loc[7591,'event_summary']='A 2 to 5 metre 6ft 7in to 16ft 5in wide asteroid named 2018 LA was estimated before impact to have an 82 percent chance of having impacted Earth today'
event_df.loc[7607,'event_summary']='The gunman who is suspected of having killed six people to among them'
event_df.loc[7631,'event_summary']='Canadian prime minister Justin Trudeau is accused of groping a journalist in 2000 . He denies he made negative interactions'
event_df.loc[7657,'event_summary']='Spanish Prime Minister Pedro Sanchez announces that He will allow a migrant vessel carrying 629 rescued migrants'
event_df.loc[7757,'event_summary']='The Ethiopia Federal Police Commission announces arrests of 30 people suspected of involvement in a bombing of a rally for Prime Minister Abiy Ahmed. The attack killed two and injured 156 . The US announces deployment of FBI specialists to assist probe'
event_df.loc[7760,'event_summary']='A judge in Nauru declares Civil Procedures Amendment 2018 unconstitutional. The act restricted ability of those facing prosecution to obtain legal representation. The court orders Naurus government to pay Australian lawyers acting for those who brought legal challenge'
event_df.loc[7765,'event_summary']='The Israeli Air Force strikes vehicles it claims were being used to launch incendiary balloons from Gaza over border into israel'
event_df.loc[7773,'event_summary']='An Israeli official says that nation has asked Cyprus to consider allowing israel to set up a shipping point on island for goods destined for Gaza'
event_df.loc[7774,'event_summary']='The Palestinian Authority rejects proposals from Israel and US to reduce sanctions that PA has imposed on Hamascontrolled Gaza'
event_df.loc[7801,'event_summary']='The Prosecutors Office of Peru opens a preliminary investigation to determine if there were alleged political benefits to among them humanitarian pardon granted to former President Alberto Fujimori to offered by former President Pedro Pablo Kuczynski to avoid being removed from his office during first impeachment process against him in December 2017'
event_df.loc[7842,'event_summary']='Cheshire Police in England arrest a female healthcare professional on suspicion of bloodshedding eight babies and attempting to murder six more at Countess of Chester Hospital'
event_df.loc[7917,'event_summary']='Belgium defeats England 2 to 0 to finish at third place its best ever result at a World Cup'
event_df.loc[7959,'event_summary']='The Israeli Parliament passes a Basic Law declaring that Land of israel is historical homeland of Jewish people and that right to exercise national selfdetermination in State of israel is unique to Jewish people'
event_df.loc[7963,'event_summary']='James Gunn is fired as director of Guardians of Galaxy Volume 3 after emergence of old tweets while he joked about subjects like pedophilia and rape'
event_df.loc[7986,'event_summary']='Geologists monitoring eruption of Kilauea warned this could continue to spout lava for a long time'
event_df.loc[7356,'event_summary']='Egypts Court of Cassation rejects appeals by 45 people handed long prison terms over a 2013 Port Said riot that killed 42 . The riots broke out in response to death sentences handed out over a previous riot in 2012 that killed 72 football fans'


In [148]:
event_df.loc[1,'event_summary']='About one thousand houses in Manilas Tondo district in Philippines are set ablaze following New Years Eve firecracker festivities that left two dead and 380 others injured'

In [149]:
event_df.loc[10,'event_summary']='Two Sunni mosques are bombed in central Iraq and a muezzin is killed amid fears of renewals of sectarian strife following Saudi Arabias execution of Shiite cleric Nimr alNimr'
event_df.loc[11,'event_summary']='The Islamic State of Iraq and Levant releases video showing killing of five men accused of committing espionage on militant group for United Kingdom. The British Foreign and Commonwealth Office released a statement saying that they are examining content of video'

event_df.loc[18,'event_summary']='The President of US Barack Obama announces executive orders to expand background checks for firearms'
event_df.loc[31,'event_summary']='Former Beijing Deputy Communist Party Secretary Lu Xiwen is expelled from communist party of China for interfering with market economy and law enforcement and living a luxurious lifestyle'
event_df.loc[32,'event_summary']='United Kingdoms Prime Minister David Cameron announces he will suspend collective responsibility ahead of referendum on countrys EU membership'
event_df.loc[35,'event_summary']='Starwars : The Force Awakens becomes highestgrossing film ever in US and Canada'
event_df.loc[44,'event_summary']='South Korea says it will resume crossborder propaganda broadcasts and limit entry to Kaesong Industrial Region in response to yesterdays nuclear test at Norths Punggyeri Nuclear Test Site'
event_df.loc[45,'event_summary']='Iran bans imports of all products made in Saudi Arabia and reiterates that probihit on Iranians traveling to Saudi holy city of Mecca remains in place'
event_df.loc[47,'event_summary']='Scotland Yard confirms that they are investigating a triple murder in relation to death of British actress Sian Blake and her two sons after discovery of their dead bodies on Tuesday'
event_df.loc[55,'event_summary']='Sian Blakes partner Arthur SimpsonKent is arrested in Ghana in connection with murder of blake and her two children'
event_df.loc[74,'event_summary']='Boko Haram militants shoot and kill seven people and burn down 10 houses in Madagali'
event_df.loc[83,'event_summary']='Windows 8 along with Internet Explorer versions eight'
event_df.loc[86,'event_summary']='South Korean soldiers fire warning shots at a suspected North Korean drone near Korean Demilitarized Zone. The unidentified flying object was spotted around twentynine miles north of Seoul'
event_df.loc[91,'event_summary']='Subtropical Storm Alex is located 785 miles one'
event_df.loc[92,'event_summary']='An avalanche kills three and injures one at Les Deux Alpes ski resort in Isere departement of French Alps. Officials are searching for or possible victims'
event_df.loc[93,'event_summary']='Iran claims that it has interrogated ten US Navy personnel who captured allegedly in its territorial waters'
event_df.loc[94,'event_summary']='Israel says Swedish Foreign Minister Margot Wallstrom is no longer welcome in country after she called for investigations into suspected extrajudicial executions of Palestinians by israeli army'
event_df.loc[100,'event_summary']='Archbishops of Anglican Communion meeting in England vote to sanction US branch of communion for its unilateral decision to allow samesex marriages'
event_df.loc[102,'event_summary']='A Brazilian court suspends licence for Belo Monte Dam weeks before it was due to start operating until operator Norte Energia SA and government of brazil reorganizes Fundacao Nacional do Indio'
event_df.loc[103,'event_summary']='The World Health Organisation declares an end to Ebola Virus outbreak in West Africa with Liberia last country to be declared free of virus'
event_df.loc[132,'event_summary']='Iran releases four iranianAmerican prisoners including Washington Post reporter Jason Rezaian and Christian pastor Saeed Abedini'
event_df.loc[137,'event_summary']='A suicide bomber kills at least thirteen people and injures fourteen in Afghan city of Jalalabad'
event_df.loc[142,'event_summary']='Pakistani prime minister Nawaz Sharif and army chief General Raheel Sharif will visit Riyadh on Monday and Tehran on Tuesday to launch mediation efforts between Iran and Saudi Arabia for normalization of relations and to ease tensions in region after SaudiArabia executed a prominent Shia cleric Sheikh Nimr and an attack on Saudi Embassy in tehran'
event_df.loc[150,'event_summary']='Biafran separatists claim that police killed eight protesters calling for independence'
event_df.loc[158,'event_summary']='The roof of renovated Hotel Ritz in Paris is damaged by fire just weeks before planned reopening'
event_df.loc[168,'event_summary']='Two former Presidents of Burundi call for UN Security Council to authorise use of peacekeeping troops to prevent a potential civil war'
event_df.loc[194,'event_summary']='The US Supreme Court ruled in Montgomery Louisiana 2016 that its prohibition of mandatory life sentences for juveniles convicted of murder under Miller'
event_df.loc[195,'event_summary']='A US drone strike kills at least six militants in Afghanistans Nangarhar Province'
event_df.loc[213,'event_summary']='Vietnam reelects conservative Nguyen Phu Trong as General Secretary of Communist Party'
event_df.loc[235,'event_summary']='A helicopter fighting forest fires in South Koreas North Jeolla Province crashes near Geumsansa Temple in Gimje'
event_df.loc[237,'event_summary']='Jamaican health officials confirm countrys first case of Zika virus in a four yearold child who recently returned from a trip to Texas'
event_df.loc[239,'event_summary']='A million dollars in FIFA funding is missing from accounts of National Football Federation of Guatemala'
event_df.loc[249,'event_summary']='A Taliban suicide bomb attack outside a police office in central Kabul kills at least nine people'
event_df.loc[257,'event_summary']='The Government of Honduras declares a state of emergency with three'
event_df.loc[262,'event_summary']='Japan puts its military on alert to shoot down any North Korean rocket that threatens it following an announcement by Northkorea of a planned Earth observation launch'
event_df.loc[276,'event_summary']='Clashes between local tribal forces and Sudanese fighters in Libyas souastern Cyrenaica region around town of Kufra leaves around thirty dead'
event_df.loc[299,'event_summary']='North Korea launches a long range rocket that critics claim is a test of banned technology for a long range missile that could hit US'
event_df.loc[336,'event_summary']='French Foreign Minister Laurent Fabius announces his resignation. President Francois Hollande says he will nominate fabius to lead countrys Constitutional Council'
event_df.loc[341,'event_summary']='Four policemen are killed and another seven wounded when one of their colleagues opened fire on them in Kandahar'
event_df.loc[349,'event_summary']='Charlot Salwai is elected Prime Minister of Vanuatu following January snap election'
event_df.loc[372,'event_summary']='The US Geological Survey reports a magnitude of earthquake five'
event_df.loc[377,'event_summary']='The UN reports that civilian casualties reached a record level in 2015 at least three'
event_df.loc[312,'event_summary']='New refugee camps go up near Syria to Turkey border after turkey blocks thousands of refugees from entering country'
event_df.loc[205,'event_summary']='Marshall Islands President Casten Nemra is defeated in a vote of no confidence. She had just been elected president in early January 2016. A successor is expected to be selected soon'
event_df.loc[221,'event_summary']='At least three people are killed and 7 wounded in an attack on a Shia mosque in Saudi Arabias Eastern Province'
event_df.loc[235,'event_summary']='A helicopter fighting forest fires in South Koreas North Jeolla Province crashes near Geumsansa Temple in Gimje'
event_df.loc[272,'event_summary']='Srilanka lifts unofficial ban on Tamil national anm on independence day'
event_df.loc[275,'event_summary']='Al Shabaab militants claim to have captured port of Merca Marka after African Union and Somali Armed Forces withdraw'
event_df.loc[329,'event_summary']='Adair Turner former head of UK Financial Services Authority'
event_df.loc[380,'event_summary']='The US Geological Survey reports a magnitude 5.8 earthquake strikes Christchurch in New Zealand'
event_df.loc[383,'event_summary']='The earthquake death toll rises to onehundredsixteen. Tainans disaster response office says search and rescue operations have ended. The last body was found yesterday'
event_df.loc[384,'event_summary']='Crews rescue 48 people from two Cannon Mountain tram cars stuck this afternoon about forty feet off ground in New Hampshire subzero temperatures in White Mountains'
event_df.loc[385,'event_summary']='Slovenia announces that it will be clamping down on number of migrants eho will allow to enter country'
event_df.loc[394,'event_summary']='Ukraine bans Russian cargo trucks from transiting its territory after Russias Ministry of Transport barred Ukrainian cargo trucks because armed groups had been blocking some Russian trucks from entering ukraine'
event_df.loc[405,'event_summary']='Medecins Sans Frontieres Doctors Without Borders reports three people are found alive in rubble of a hospital in northwest Syria hit by Russian airstrikes Monday'
event_df.loc[408,'event_summary']='Canadian multinational aerospace and transportation company Bombardier Inc is to cut seven'
event_df.loc[409,'event_summary']='Hungarian Prime Minister Viktor Orban meets with Russian President Vladimir Putin in Moscow. He used meeting to call for Russias relations with EU to return to normal'
event_df.loc[410,'event_summary']=' A report by Taiwanese Defense Ministry states that China has placed surfacetoair missiles on disputed Woody Island. Taiwanese Presidentelect Tsai Ingwen called on all parties to exercise selfcontrol based on principle of peaceful resolution of disputes in South China Sea'
event_df.loc[413,'event_summary']='Russias Finance Ministry sues Ukraine in Londons High Court of Justice over a dollar three billion debt'
event_df.loc[414,'event_summary']='Maldives jails opposition leader Imran Abdulla for terrorism. It is claimed that he urged overthrow of government in a speech'
event_df.loc[418,'event_summary']='UEFA charges Dmitri Tarasov and his football club Lokomotiv Moscow with improper conduct after tarasov'
event_df.loc[422,'event_summary']='South Koreas National Intelligence Service warns that North Korea is currently planning a terrorist attack on Southkorea'
event_df.loc[423,'event_summary']='President of US Barack Obama announces that he will visit Cuba next month becoming first American president to visit Cuba since 1928'
event_df.loc[432,'event_summary']='Cyclone Winston heads towards Fiji at Category five strength. It is expected to make landfall on Saturday'
event_df.loc[444,'event_summary']='Jat protesters shut down 70 percent of Delhis water supply meaning Indian city could run out of Water by end of weekend. At least nine people are killed in fighting'
event_df.loc[460,'event_summary']='Denny Hamlin wins 2016 Daytona 500 by zero'
event_df.loc[461,'event_summary']='A suicide bomber kills at least thirteen people and injures nineteen in Afghanistans Parwan province. The Taliban claims responsibility'
event_df.loc[472,'event_summary']='Emergency warnings are issued after bushfires threaten Victorian Towns of Mount Bolton and Addington northwest of Ballarat as well as town of Somerville'
event_df.loc[474,'event_summary']='At least one person has been killed and three people remain missing following partial collapse of decommissioned turbine hall at Didcot A. Power Station in Oxfordshire'
event_df.loc[480,'event_summary']='The President of US Barack Obama announces plans to close Guantanamo Bay detention camp in Cuba. He made similar statements during his first presidential campaign in 2007 and had previously stated that camp would be closed by 2010'
event_df.loc[482,'event_summary']='Senior Libyan military officials say French special forces are in Benghazi helping Libyan National Army troops fight militants'
event_df.loc[487,'event_summary']='The Oxfordshire Fire and Rescue Service state that three people missing since a decommissioned turbine hall partially collapsed at Didcot power station in oxfordshire'
event_df.loc[495,'event_summary']='Former President of FIFA Sepp Blatter and suspended president of UEFA boss Michel Platini lose their appeals against being banned from all football related activities but prohibited period is reduced from eight to six years'
event_df.loc[516,'event_summary']='Voters in Iran go to polls for a Islamic Consultative assembly and Assembly of Experts elections'
event_df.loc[519,'event_summary']='Officials of FIFA meet in Zurich for 2016 Fifa Extraordinary Congress to select a new President of FIFA to replace Sepp Blatter. Gianni Infantino is elected with a majority of votes in second round of voting'
event_df.loc[526,'event_summary']='Thirtysix people are believed to have died at a Coal Mine where a methane gas ignition triggered three explosions and collapse of mine in Vorkuta'
event_df.loc[531,'event_summary']='China says it expects to lay off one'
event_df.loc[533,'event_summary']='Macedonian police use tear gas after hundreds of migrants frustrated with long delays broke a gate on border with Greece'
event_df.loc[535,'event_summary']='Clashes break out inside Calais jungle camp in port city of Calais between migrants and riot police as officials attempted to evict hundreds of migrants from sourn section of Camp'
event_df.loc[544,'event_summary']='The UN Security Council vote on USChina draft resolution on North Korea is rescheduled to 10:00 AM. EST Wednesday. Russia requests more time to review text'
event_df.loc[558,'event_summary']='The Tunisian Army kills five suspected militants near town of Ben Gardane after they infiltrated across border from neighboring Libya'
event_df.loc[561,'event_summary']='Philippines Foreign Secretary Albert del Rosario says Chinese coast guard ships that were sighted two weeks ago near disputed Jackson Atoll in norast Dangerous Ground are no longer there today'
event_df.loc[571,'event_summary']='A Riot at a prison in Guyanas capital Georgetown leaves at least 16 people dead. The riot began when inmates angered by a search that led to confiscation of mobile phones set fires in one part of prison'
event_df.loc[572,'event_summary']='Voting begins for second stage of New Zealands flag referendum with current flag going up against design chosen on first stage of Referendum'
event_df.loc[579,'event_summary']='Syrian rebels have seized control of alTanf borderline crossing on Iraq to Syria from militants. The rebel fighters who took crossing reportedly entered syria through Jordan'
event_df.loc[582,'event_summary']='Germany wants France to shut down Fessenheim Nuclear Power Plant near its border as soon as possible following media reports April nine'
event_df.loc[585,'event_summary']='A Turkish court places influential Zaman newspaper under state control'
event_df.loc[590,'event_summary']='The Philippines impounds a North Korean cargo ship in line with new UNsanctions on Northkorea in response to Pyongyangs recent nuclear test and missile launch'
event_df.loc[598,'event_summary']='Iranian billionaire Babak zanjani is sentenced to death for corruption. Zanjani was arrested in December 2013 after accusations that he withheld billions in oil revenue channelled through his companies. He denies allegations'
event_df.loc[604,'event_summary']='Apple Inc must pay dollar 450 million July 2014 settlement in a price fixing case since US Supreme Court will not hear its appeal of June 2015 Court of Appeals ruling that this played a central role in a conspiracy with publishers to eliminate retail price competition and raise ebook prices'
event_df.loc[609,'event_summary']='Venezuelan security forces search for 30 gold miners reportedly killed last week in state of Bolivar in countrys souast. Survivor reports state miners were shot last Friday in a fight for control of a gold deposit by criminals who they hid bodies. Bolivar Governor Francisco Rangel Gomez denies any such massacre occurred'
event_df.loc[617,'event_summary']='Russia claimed Friday to have killed several top commanders of the Islamic State group in an airstrike in Syria, including the Minister of War and the socalled Emir of Deir Ezzor'
event_df.loc[619,'event_summary']='The World Health Organization cautions pregnant women against traveling to areas where there is ongoing transmission of Zika virus'
event_df.loc[623,'event_summary']='An Istanbul court places Cihan News Agency under state rule. The seizure of Fethullah Gulenlinked news agency comes just days after Turkish government seized control of opposition Zaman newspaper'
event_df.loc[634,'event_summary']='A Saudiled coalition spokesman announces they have exchanged prisoners with their Houthi opponents and welcome a pause in combat on border. Saudi Foreign Minister Adel alJubeir said lull was important to deliver aid and medical supplies to people in norrn regions of Yemen'
event_df.loc[638,'event_summary']='Googles DeepMind AlphaGo artificial intelligence program defeats South Korean grand master Lee Sedol in ancient game of go'
event_df.loc[646,'event_summary']='Three candidates are put forward to become President of Myanmar : Htin Kyaw and Sai Nyunt Lwin from National League for Democracy and Khin Aung Myint from military'
event_df.loc[651,'event_summary']='Bangladeshi bank officials say unknown hackers installed malware in banks computer systems in last months attempt to steal nearly dollar one billion from central banks account at Federal Reserve Bank of New York'
event_df.loc[659,'event_summary']='Astronaut Scott kelly announces his retirement from NASA effective April 1. Kelly holds record for American who has spent most time in space'
event_df.loc[665,'event_summary']='Jaysh alNasr rebels say they have shot down a fighter jet over Hama Governorate in western syria. The Syrian Observatory for Human Rights confirmed shoot down'
event_df.loc[680,'event_summary']='Chinas Peoples Liberation Army PLA will be deployed in Pakistan to protect china to Pakistan Economic Corridor that connects Chineseoperated Gwadar Port in Balochistan'
event_df.loc[681,'event_summary']='US officials say North Korea has apparently lost contact with one of its Submarines. The US was watching sub off North Koreas eastern coast which vanished earlier this week. Officials are unsure where missing vessel is adrift or has sunk'
event_df.loc[686,'event_summary']='Brazils biggest protests in two decades intensified on Thursday despite government concessions meant to quell the demonstrations, as three lac people took to the streets of Rio de Janeiro and hundreds of thousands more flooded other cities'
event_df.loc[702,'event_summary']='Czech Intelligence Service that said Mohammad Atta leader of the hijackers had been in Prague in first April and met with the senior Iraqi intelligence official in Prague'
event_df.loc[705,'event_summary']='Pope Francis announces that Mor Teresa will be canonized on 4th September'
event_df.loc[713,'event_summary']='Argentinas coastguard says it has sunk a Chinese fishing trawler that was operating illegally within its territorial waters. The coastguard says they rescued four of trawlers crew while others who abandoned ship were picked up by another Chinese vessel shadowing pursuit'
event_df.loc[718,'event_summary']='Cuban officials announce they have detected first case of Zika virus transmitted inside country'
event_df.loc[721,'event_summary']='The travel ban for former pakistani President Pervez Musharraf is lifted by Supreme Court of Pakistan. Musharraf is currently facing treason charges in Pakistan'
event_df.loc[722,'event_summary']='Authorities in Turkey arrest three academics on charges of terrorist propaganda after they called for an end to security operations in countrys Kurdishmajority souast'
event_df.loc[723,'event_summary']='The US military disciplines more than a dozen personnel for mistakes that led to bombing of a Medecins Sans Frontieres Doctors Without Borders hospital that killed 42 people in Afghanistan last October. No criminal charges are pending. The partially redacted investigation report is expected to be made public shortly'
event_df.loc[730,'event_summary']='The Vatican is replacing Italian Archbishop Carlo Maria Vigano'
event_df.loc[733,'event_summary']='Kurdish parties in norrn Syria declare establishment of a federal system in areas they control. Turkey and US had warned this risks furr destabilizing already warravaged country. The move was criticized by government of syria'
event_df.loc[735,'event_summary']='Judges at International Criminal Tribunal for former Yugoslavia announce that they will soon deliver their verdict against radical Serb leader Vojislav Seselj'
event_df.loc[738,'event_summary']='The South Korean Joint Chiefs of Staff and a US defense official report that North Korea fired two ballistic missiles from South Pyongan Province. One flew 800 kilometers 497 miles into Sea of Japan. The other disappeared at an altitude of about 17.5 kilometers 10.5 miles'
event_df.loc[739,'event_summary']='European Union leaders offer Turkey a detailed package of cash and incentives to agree that all migrants attempting to cross Aegean Sea by raft or boat would be sent back to turkey'
event_df.loc[748,'event_summary']=' Flydubai Boeing 737800 Flight FZ981 was a scheduled international passenger flight that crashed during an aborted landing at RostovonDon Airport Russia on 19th March 2016 resulting in the deaths of all 62 passengers and crew on board'
event_df.loc[752,'event_summary']='Russian speed skaters Pavel Kulizhnikov won the men 500 metres event at the 2015 World Single Distance Championships '
event_df.loc[765,'event_summary']='A South Korean Joint Chiefs of Staff official reports North Korea launched five shortrange missiles from eastern city of Hamhung into Sea of Japan'
event_df.loc[766,'event_summary']='At a 55 minute joint press conference, following their two-hour closed door meeting Barrack Obama and Cuban President Raul Castro agreed this new day of openness between the two countries benefits the entire hemisphere as well'
event_df.loc[773,'event_summary']='Finland and Russia agree to impose temporary restrictions at two Arctic border crossing points on Finnish russian border'
event_df.loc[778,'event_summary']='Brazil President Dilma Rousseff will not resign under any circumstances because she hadnt committed a crime'
event_df.loc[782,'event_summary']='Medecins Sans Frontieres Doctors Without Borders and UNrefugee agency'
event_df.loc[784,'event_summary']='The Supreme Court of US SCOTUS is the highest court in federal judiciary of United States.'
event_df.loc[343,'event_summary']='For months starting in late 2015 a gas leak in Los Angeles spewed methane into the air. The Southern California Gas Company has agreed to reimburse local governments and mitigate damage'
event_df.loc[667,'event_summary']='At least 298 people are killed when a magnitude 6 earthquake strikes central Italy'
event_df.loc[788,'event_summary']='Judges at International Criminal Tribunal for former Yugoslavia find former President of Republika Srpska Radovan karadzic guilty of committing genocide and crimes against humanity in Bosnia during Bosnian War and is sentenced to 40 years in prison. Karadzic is found to be criminally responsible for Srebrenica massacre'
event_df.loc[789,'event_summary']='New Zealanders vote to retain current flag over proposed design in nations flag referendum. More than two million people vote in Referendum'
event_df.loc[790,'event_summary']='Dutch iconic professional footballer and Johan Cruyff dies from lung cancer at age of 68'
event_df.loc[793,'event_summary']='The Nigerian Army claims to have rescued more than 800 hostages from Boko Haram while performing a clearance operation in nigerian Norastern part with fighting killing 22 insurgents'
event_df.loc[795,'event_summary']='The body of Ukrainian lawyer Yurij Grabovsky who defended two exRussian soldiers charged in Eastern Ukraine with terrorism and waging an aggressive war against the country. It is found on the grounds of a former farming collective in Zhashkiv'
event_df.loc[798,'event_summary']='A US federal district judge rules unconstitutional a provision in an Alabama state law that requires doctors who perform abortions to have admitting privileges at a local hospital. A Florida law enacted today contains a comparable provision to Alabamas. The US Supreme Court heard arguments a few weeks ago on constitutionality of similar abortion restrictions in Texas'
event_df.loc[810,'event_summary']='Taliban fighters fire explosives at Afghanistans Parliament while it is in session. Members said no one was wounded while a Taliban spokesperson claims it caused heavy casualities'
event_df.loc[812,'event_summary']='Belgian prosecutors release Faycal C. who was charged in connection with last weeks deadly Brussels bombings. The prosecutors office says the evidence which led to his arrest has not been backed up by the ongoing investigation'
event_df.loc[825,'event_summary']='The US Supreme Courts even split among current eight justices turns down a group of California teachers challenge to agency fees publicsector unions representing government employees charge for collective bargaining costs'
event_df.loc[828,'event_summary']='Seven people die in a plane crash on Magdalen Islands in Canadian province of Quebec. Former minister Jean Lapierre was one of them on board plane'
event_df.loc[830,'event_summary']='A UN commission rules in favour of Argentina to expand its maritime territory in South Atlantic Ocean by 35 percent to include Falkland Islands and beyond despite ARG and UK still having an unresolved dispute over islands'
event_df.loc[831,'event_summary']='The US Department and Pentagon order families of US diplomats and military personnel to leave posts in sourn Turkey due to increased threats from terrorist groups in country. This order comes two days before Turkish President Recep Tayyip Erdogans arrival in US for security meetings'
event_df.loc[832,'event_summary']='US and its European allies have notified United Nations that Irans launching of nuclear capable missiles violated UN Security Council resolution 2231 which endorsed iran deal'
event_df.loc[839,'event_summary']='The US Government Millennium Challenge Corporation MCC and the Government of Morocco marked the beginning of the Employability and Land Compact Thursday in Rabat'
event_df.loc[840,'event_summary']='Two police officers are killed and four others are wounded in western Venezuelan city of San Cristobal after they were run over by a bus driven by young men protesting a hike in public transport fares'
event_df.loc[841,'event_summary']='US Federal Communications Commissioner Michael ORielly says Internet Access Is Not a Necessity'
event_df.loc[843,'event_summary']='At least seven Central Reserve Police Force CRPF personnel are killed in an IED attack on their vehicle in Indian state of Chhattisgarhs Dantewada district'
event_df.loc[848,'event_summary']='The US Food and Drug Administration announces it has relaxed its official requirements regarding use of abortion drug Mifeprex RU486 . The current guidelines were based on 1990s medical evidence'
event_df.loc[850,'event_summary']='The Ukrainian parliament votes to ban all Russian films released after first January'
event_df.loc[852,'event_summary']='The National Border Patrol Council which organizes some 16500 border patrol agents endorses Donald Trump for President of the United States NBPC firstever endorsement in presidential election'
event_df.loc[853,'event_summary']='Government of Pakistan warns that it will push to clear Islamist protests occurring in Islamabad. Protests have broken out in capital and or cities ever since Mumtaz Qadri was executed last February for his role in killing Punjab governor Salmaan Taseer in 2011 because he opposed Pakistans blasphemy laws'
event_df.loc[854,'event_summary']='The UNbacked Libyan Presidential Council arrives in Tripoli despite warnings by hardliners opposed to any unity government that they will attempt to keep them out of city'
event_df.loc[863,'event_summary']='A US official announces that The Pentagon plans to transfer about a dozen inmates from Guantanamo Bay detention camp to at least two countries that have agreed to take them'
event_df.loc[866,'event_summary']='Vietnam elects Nguyen Thi Kim Ngan chairwoman of National Assembly'
event_df.loc[868,'event_summary']='Italys Minister of Economic Development Federica Guidi resigns amid allegations that she passed along confidential information to her boyfriend that helped his business interests'
event_df.loc[869,'event_summary']='Brazils Supreme Court voted 82 to take over corruption investigation of former President Luiz Inacio Lula da Silva'
event_df.loc[873,'event_summary']='International monitors from OSCE report that fighting has intensified in Eastern Ukraine as a second year of a shaky truce begins. The worst of controversy is located between governmentcontrolled Avdiivka and separatistcontrolled Yasynuvata'
event_df.loc[879,'event_summary']='The Syrian Observatory for Human Rights claims that AlNusra Front or insurgents have captured village of Tel elAis in a strategic position overlooking highway between Aleppo and Damascus'
event_df.loc[886,'event_summary']='The US Air Force sends 12F15C Eagles and 350 personnel to Iceland and Nerlands to deter furr Russian aggression in Europe'
event_df.loc[891,'event_summary']='Governor of US territory of Guam Eddie Calvo announces his intention to hold a plebiscite to decide future political status of island. Calvo said he hopes to start a successful education campaign on issue before filing a petition to start a referendum'
event_df.loc[895,'event_summary']='Two weeks after the deadly suicide bombings Brussels Zaventem International Airport will reopen today with three symbolic flights to Faro, Athens, and Turin. On Thursday the airport had said it was technically ready to resume partial services but the opening was held up because police unions threatened to strike unless additional security checks were introduced'
event_df.loc[900,'event_summary']='At least 18 people are injured following a collision between two trains at Plymouth railway station'
event_df.loc[901,'event_summary']='Czech Minister of Interior Milan Chovanec says that authorities in Prague will send a group of twentyfive IraqiChristians back to Iraq after they tried to move to Germany rar than staying in Czech Republic. The refugees were on their way to Germany via bus before being stopped at border. Czech authorities agreed to a request by German police to take people back. Chovanec said twentyfive Iraqis abused Czech generosity and should go back to their country within seven days'
event_df.loc[903,'event_summary']='The Parliament of South Africa announces it will debate a motion to impeach President Jacob zuma this coming Tuesday. This comes after Zuma is facing mounting pressure when Constitutional Court ruled that Zuma violated constitution by using state funds to renovate his mansion'
event_df.loc[907,'event_summary']='The Associated Press reports governmentsponsored committee of 27 companies/trade associations'
event_df.loc[908,'event_summary']='Defending champions The West Indies beat England by four wickets in final in Kolkata'
event_df.loc[912,'event_summary']='Alaska Airlines announces plans to acquire Virgin America for dollar four billion'
event_df.loc[920,'event_summary']='Icelandic Prime Minister Sigmundur David Gunnlaugsson refuses to resign after leaked Panama Papers tax documents showed he and his wife used an offshore firm to allegedly hide million dollar investments. I have not considered quitting because of this matter nor am I going to quit'
event_df.loc[921,'event_summary']='The President of Kyrgyzstan Almazbek Atambayev signs a presidential decree officially recognizing 17th March'
event_df.loc[923,'event_summary']='The Turkish army say it carried out air strikes in norrn Iraq against targets belonging to Kurdistan Workers Party'
event_df.loc[928,'event_summary']='France places Panama back on its list of countries that do not cooperate in catching tax evaders'
event_df.loc[931,'event_summary']='The Military junta of Thailand gives Royal Thai Armed Forces broad policelike powers. The military is now allowed to prevent or suppress over 27 types of offenses. The move created an outcry from human rights organizations and prompted US to express its concern over growing influence of army in country'
event_df.loc[935,'event_summary']='The International Criminal Tribunal for the former Yugoslavia in majority vote ordered an indefinite halt in the war crimes trial of Croatian Serb rebel leader Goran Hadzic who is terminally ill with brain cancer and declared"unfit to stand trial. He was charged with fourteen war crimes and crimes against humanity for his role in the 1991 to 1995 war in Croatia'
event_df.loc[936,'event_summary']='The President of Russia Vladimir Putin announces the creation of a new National Guard which he said would fight terrorism and organized crime'
event_df.loc[937,'event_summary']='The selfdeclared National Salvation government which is one of the rival governments of Libya, resigns and gives up power to the UN backed Libyan Presidential Council in Tripoli'
event_df.loc[938,'event_summary']='Beninese businessman Patrice Talon is sworn in as new President of country'
event_df.loc[941,'event_summary']='Mississippi Hospitality and Restaurant Association in response to the potential backlash from mississippi Governor Phil Bryant is signing of the known-as religious freedom bill which permits denial of services because of religious belief will distribute decals that say Everyone Welcome Here'
event_df.loc[942,'event_summary']='Australian mining and materials company Arrium goes into voluntary administration with 7000 jobs under threat including 1000 at the Whyalla Steelworks in South australia'
event_df.loc[944,'event_summary']='Another earthquake measuring at 6.7 strikes off the northwest of Vanuatu third earthquake in the same region this week. However he Pacific Tsunami Warning Center says the earthquake poses no tsunami threat'
event_df.loc[948,'event_summary']='Planned Parenthood and American Civil Liberties Union sue Indiana stating US states new abortion law is unconstitutional because that bans procedure if sought because of genetic abnormalities'
event_df.loc[949,'event_summary']='The National Assembly of Vietnam approves Nguyen Xuan Phuc as countrys new prime minister'
event_df.loc[955,'event_summary']='Both StarWood Hotels and Resorts Worldwide and Marriott International shareholders approve Marriotts acquisition of Starwood which will create the worlds largest hotelier. The deal has cleared the premerger antitrust reviews in the US and Canada approvals from the European Union and China is pending. Last week Anbang Insurance Group topped Marriotts bid then withdrew their offer three days later'
event_df.loc[957,'event_summary']='King of Saudi Arabia Salman bin Abdulaziz Al Saud announces during his trip to Cairo that a bridge crossing the Red Sea will be built linking Egypt and SA. President Abdel Fattah elSisi says the bridge will be named after the saudi monarch. A SAUDIEGYPT Causeway project has been in the works for years'
event_df.loc[959,'event_summary']='NATO announces it will hold a meeting to Russia Council at ambassadorial level at their headquarters in Brussels in next two weeks after two year break since they cut all practical cooperation with Russia in 2014'
event_df.loc[964,'event_summary']=' The French occupy movement known as Nuit debout enters its ninth day March 40th spreading across dozens of French cities and to Belgium, Germany, and Spain'
event_df.loc[969,'event_summary']='The Colorado Republican Party continues choosing its delegates to 2016 Republican National Convention in Cleveland'
event_df.loc[971,'event_summary']='Russian Sports Minister Vitaly Mutko says they will not open up a formal investigation into doping scandals that were reported by World AntiDoping Agency last November'
event_df.loc[980,'event_summary']='Registered Democratic voters in the US of Wyoming gather by county for Wyoming Democratic caucuses. Bernie Sanders is projected to win'
event_df.loc[981,'event_summary']='Thousands of people protest in Whitehall calling on British Prime Minister David Cameron to resign over his financial affairs and his handling of them in relation to revelations made by leak of Panama Papers'
event_df.loc[981,'event_summary']='Thousands of people protest in Whitehall calling on British Prime Minister David Cameron to resign over his financial affairs and his handling of them in relation to revelations made by leak of Panama Papers'
event_df.loc[988,'event_summary']='The Foreign Minister of Iran Mohammad Javad Zarif says that countrys missile program would not be up for discussion. This comes as United States Secretary John Kerry said last Thursday that US and its allies would only address Irans concerns in region if they makes it clear to all involved that was prepared to cease provocative ballistic missile launches and tests'
event_df.loc[999,'event_summary']='A severe heat wave grips Malaysia as much of Souast Asia struggles with unusually hot and dry wear created by El Nino season. Temperatures soared above 37 degree centigrade'





In [150]:
event_df.loc[999,'event_summary']

'A severe heat wave grips Malaysia as much of Souast Asia struggles with unusually hot and dry wear created by El Nino season. Temperatures soared above 37 degree centigrade'

In [151]:
event_df.loc[8068,'event_summary']='A report commissioned by UN Security Council concludes that North Korea has not stopped its nuclear program and that they attempted to sell military supplies to Libya'
event_df.loc[8093,'event_summary']='The Australian Bureau of Statistics says total population of australia has hit 25 million'
event_df.loc[8100,'event_summary']='China announces 25 percent tariffs on an additional USdollar 16 billion worth of imports from United States'
event_df.loc[8126,'event_summary']='The BNPB spokesperson Sutopo Purwo Nugroho confirmed that death toll from earthquake in Lombok rises to 436'
event_df.loc[8147,'event_summary']='Following accusations by fellow monks of sexual misconduct and embezzling funds accusations which were subsequently posted on social media Buddhist Association of China announces Shi Xuechengs resignation from office of president of that organization'
event_df.loc[8153,'event_summary']='The Cabinet of Germany approves a third gender option for official identification records'
event_df.loc[8156,'event_summary']='Prime Minister Narendra Modi says India will launch its first manned space mission by 2022'
event_df.loc[8174,'event_summary']='Belarusian president Alexander Lukashenko reshuffles his government in wake of a corruption scandal. Andrei Kobyakov is replaced by Sergei Rumas as Prime Minister of belarus'
event_df.loc[8185,'event_summary']='The Venezuelan armed forces send two attack helicopters and a brigade of 30 soldiers across colombiavenezuela border. Colombia denounces violation of sovereignty but takes no furr action against country'
event_df.loc[8189,'event_summary']='American actor Jimmy Bennett accuses Italian actress Asia Argento of having sexual relations with him while he was 17 years old and then paying him dollar 380'
event_df.loc[8195,'event_summary']='Judge in trial of two journalists jailed in Myanmar announces that he will deliver his verdict on August 27'
event_df.loc[8213,'event_summary']='President Nicolas Maduro says that wages for workers in Venezuela must be linked to petro'
event_df.loc[8254,'event_summary']='Germany hands over to Namibia human remains ninteen skulls'
event_df.loc[8270,'event_summary']='Catholic bishops in Australia reject a recommendation from Royal Commission into Institutional Responses to Child Sexual Abuse that would force priests by law to report abuse to police when they hear about that in confession'
event_df.loc[8305,'event_summary']='Tropical Storm Gordon makes landfall near Alabama to Mississippi border in US . One death is reported'
event_df.loc[8342,'event_summary']='A court in Egypt sentences 75 people to death for participating in a proMorsi sitin protest in a Cairo suburb in 2013 . The breakup of that protest at Rabaa Square by Egyptian authorities resulted in over 600 deaths'
event_df.loc[8378,'event_summary']='The European Central Bank maintains its policy to halve monetary stimulus after September and end that in December 2018'
event_df.loc[8423,'event_summary']='The death toll of Typhoon Mangkhut in Philippines rises to 81 '
event_df.loc[8428,'event_summary']='The death toll from recent spike in ethnic violence in Ethiopia rises to 58 . Thousands are still protesting against killings in capital Addis Ababa'
event_df.loc[8464,'event_summary']='Russian officials state that country will send S300 airdefense missile system to Syria within two weeks'
event_df.loc[8485,'event_summary']='NASAs Opportunity rover is spotted on satellite imagery three months after that went silent during a Martian dust storm'
event_df.loc[8495,'event_summary']='A USMC F35 jet crashes in coastal South Carolina making this first crash of United States militarys newest and most expensively developed aircraft'
event_df.loc[8500,'event_summary']='The New York Supreme Court allows a dollar 45 million loan lawsuit against Harvey Weinstein to resume after pausing that for bankruptcy proceedings for The Weinstein Company to complete'
event_df.loc[8506,'event_summary']='The government of Pakistan is rethinking its dependence on China for loans that needs to complete their Peshawar to Karachi rail project. This is part of a broader pushback on ambitions of Chinas Belt and Road Initiative throughout region'
event_df.loc[8538,'event_summary']='The Swedish Academy names two new members : Swedish supreme court justice Eric Runesson'
event_df.loc[8545,'event_summary']='A cloture vote on nomination of Judge Brett Kavanaugh passes 51 to 49 . A final confirmation vote is set to occur on Saturday'
event_df.loc[8548,'event_summary']='At least 50 people are killed and 100 others are injured after an oil tank truck collides with a vehicle on Kinshasa Matadi highway in Kisantu'
event_df.loc[8551,'event_summary']='The US Food and Drug Administration bans usage of seven artificial flavors as food additives'
event_df.loc[8558,'event_summary']='A total of 342 people have been arrested for attacking Hindispeaking migrants in Indian state of Gujarat'
event_df.loc[8559,'event_summary']='Google announces that it is shutting down its googleplus network for consumers after seven years due to very low usage and a software error'
event_df.loc[8560,'event_summary']='The death toll of a magnitude 5.9 earthquake that struck Haiti rises to 15 . At least 333 others are injured'
event_df.loc[8566,'event_summary']='Hurricane Michael strengns to a category 2 storm with 110 mph winds as It continues to ascend through Florida Panhandle'
event_df.loc[8579,'event_summary']='Heavy floods affect France and Italy : in French city of Sainte Maxime'
event_df.loc[8593,'event_summary']='Five South Korean climbers and four Nepali guides die after a snowstorm destroys their camp on a Himalayan peak'
event_df.loc[8605,'event_summary']='Fracking for shale gas begins in UK for first time since it was suspended in 2011 after being linked to a series of earthquakes. Cuadrilla Resources say they will spend at least three months fracking two horizontal wells in Lancashire'
event_df.loc[8622,'event_summary']='Afghan general and Kandahar police chief Abdul Raziq Achakzai is assassinated by one of his bodyguards during a highlevel meeting inside governors compound with US general Austin S.Miller'
event_df.loc[8634,'event_summary']='Arianespace launches European Space Agency to Japan Aerospace Exploration Agency probe BepiColombo from Guiana Space Centre as it begins a 7 year journey to Mercury. It is final mission of Horizon 2000 plus program'
event_df.loc[8653,'event_summary']='Hurricane Willa hits coast of Western Mexico. It is also expected to become a noreaster after passes through US'
event_df.loc[8688,'event_summary']='Japanese company Hitachi Chemical states that they falsified inspections for a material used in semiconductors'
event_df.loc[8739,'event_summary']='British Defence Minister Gavin Williamson announces that a joint britishomani military training base will open in Oman next year'
event_df.loc[8786,'event_summary']='UK and EU negotiators reached a draft agreement and that it will be discussed by Cabinet tomorrow'
event_df.loc[8853,'event_summary']='President of European Council Donald Tusk says there is agreement in principle on a political deal that can be endorsed at an EU summit'
event_df.loc[8856,'event_summary']='The World Meteorological Organization reports that average global carbon dioxide concentrations rose to 405.5 parts per million in 2017 . They say this level was not seen since at least three million years ago'
event_df.loc[8868,'event_summary']='The Spanish government and UK government reach an agreement on Gibraltar whereby Spain lifts its threat of boycotting Sundays summit on Brexit. Prime Minister Pedro Sanchez says there are now sufficient guarantees that any future decisions regarding Gibraltar would be made with Spain'
event_df.loc[8871,'event_summary']='Russia stops three Ukrainian Navy vessels from passing under Kerch Strait Bridge by blocking with a cargo ship'
event_df.loc[8889,'event_summary']='The National Board of Review of Motion Pictures names Green Book best film in 2018 . A Star Is Born won three awards'
event_df.loc[8914,'event_summary']='Supreme Court of Canada says that Vice Media reporter Ben Makuch must give Royal Canadian Mounted Police material he gared for stories about an accused Islamic State terrorist'
event_df.loc[8950,'event_summary']='Jamaican reggae artist Buju Banton Mark Anthony Myrie is released from a US prison and deported back to jamaica'
event_df.loc[8952,'event_summary']='Huawei CFO Meng Wanzhou attends a bail hearing in Vancouver while she awaits extradition to US . She is charged by Canadian and American prosecutors with conspiracy to defraud multiple financial institutions in order to commit evasion of US sanctions against Iran so as to conduct business with Iran'
event_df.loc[8973,'event_summary']='Russian serial killer and former policeman Mikhail Popkov is convicted of an additional 56 murders between 1992 and 2007 . All of his victims were women'
event_df.loc[8985,'event_summary']='The Afghan National Army abandons western Shib Koh District after government failed to resupply troops stationed RE'
event_df.loc[8986,'event_summary']='Two police officers are injured after a man throws a grenade at them at a shopping centre in Nazran'
event_df.loc[8988,'event_summary']='Soldiers from North Korea and South Korea peacefully cross Korean Demilitarized Zone for first time since this was created in 1953'
event_df.loc[9036,'event_summary']='Parts of Ventura Freeway in Sourn California is renamed as President Barack H. Obama Highway in honor of former President Barack Obama'
event_df.loc[9037,'event_summary']='Myanmars announces it will resume clearance operations in Rakhine State after a recent spike in attacks by unidentified assailants'
event_df.loc[9044,'event_summary']='US Secretary of Defence Jim Mattis announces his resignation at end of February 2019 . Mattis says that his views are not well aligned with those of President'
event_df.loc[9101,'event_summary']='Three people are injured after being stabbed in an attack at Manchester Victoria station'
event_df.loc[9102,'event_summary']='At least 69 people are reported dead from flooding caused by Tropical Depression Usman in Philippines'
event_df.loc[9104,'event_summary']='Russias FSB state security agency says they have arrested a US citizen caught spying in Moscow'
event_df.loc[9121,'event_summary']='Four skiers three Finnish men and a Swedish woman are killed in an avalanche near Blabaerfjellet mountain in Troms'
event_df.loc[9148,'event_summary']='The Syrian Network for Human Rights reports that at least 223 documented massacres were perpetrated in 2018 by parties to conflict in syria'
event_df.loc[9162,'event_summary']='The government of Guatemala denounces UNbacked International Commission against Impunity in Guatemala CICIG and gives 24 hours to leave country'
event_df.loc[9165,'event_summary']='The Army police of Russia says that it has started patrolling area surrounding Manbij'
event_df.loc[9216,'event_summary']='Myanmars announces that it has killed 13 Arakan Army fighters in a series of eight armed clashes in Rakhine State'
event_df.loc[9217,'event_summary']='Al Shabaab claims they killed over 57 Ethiopian troops in an ambush in Somalia'
event_df.loc[9225,'event_summary']='A state of emergency is declared in Pennsylvania and New Jersey as a large winter storm makes its way to norastern US'
event_df.loc[9248,'event_summary']='North Carolina Superior Court judge Paul Ridgeway rejects bid to certify Republican Mark Harris as winner of countrys last undecided congressional race until theres a final decision in investigation into possible illegal tactics'
event_df.loc[9388,'event_summary']='Militants attacked an army checkpoint in Sinai Peninsula killing and injuring 15 . It is believed that 11 were killed but that has not been confirmed'
event_df.loc[9430,'event_summary']='President Vladimir Putin states that Russia is militarily ready for a Cuban Missilestyle crisis if US wants one'
event_df.loc[9464,'event_summary']='The Labour Party announces it will support a second referendum on last of UK membership of European Union unless Wednesday sees Labours proposed Brexit deal supported by Parliament'
event_df.loc[9484,'event_summary']='MPs in House of Commons meet to discuss UK Prime Minister Theresa Mays latest proposed deal for states departure from European Union'
event_df.loc[9487,'event_summary']='29 people were killed in three bomb attacks and a siege that lasted into March 1'
event_df.loc[9490,'event_summary']='Attorney General of Israel Avichai Mandelblit says that after more than two years of investigations he has decided to indict Prime Minister Benjamin Netanyahu on charges of bribery'



In [152]:
event_df.loc[2905,'event_summary']='A fire at a karaoke bar in Hanois Cau Giay district kills 13 people'
event_df.loc[3269,'event_summary']='The death toll from bombings in Besiktas'
event_df.loc[3451,'event_summary']='A shootout in Izmir kills two gunmen while another one escapes'
event_df.loc[3954,'event_summary']='Dutch authorities withdrew landing permission for a plane carrying Turkish Foreign Minister Mevlut Cavusoglu'
event_df.loc[4495,'event_summary']='North Korea launches a ShortRange Ballistic missile near Wonsan towards Sea of Japan'
event_df.loc[5507,'event_summary']='The UluruKata Tjuta National Parks board votes unanimously to ban climbing on Uluru'
event_df.loc[5712,'event_summary']='Peoples Democratic Partys cochair Selahattin Demirtas remains behind bars until next hearing'
event_df.loc[5933,'event_summary']='German foreign minister Sigmar Gabriel and his Turkish colleague Mevlut Cavusoglu agree to improve relations between their countries'
event_df.loc[6015,'event_summary']='Malaysia upholds death sentences for nine Filipino Tausugs over 2013 incursion in Sabah by a faction of claimant to Sultanate of Sulu throne'
event_df.loc[6051,'event_summary']='A bus crash in Turkeys northwestern Eskisehir Province kills at least 11 people and injures 46 others'
event_df.loc[6058,'event_summary']='Turkish President Erdogan announces that Turkish Army ground troops have entered district of Afrin in Syria . Turkish Prime Minister Binali Yildirim says goal is to establish a 30 km safe zone'
event_df.loc[6128,'event_summary']='Swiss tennis player Roger Federer successfully defends his title in fivesets mens singles final against Marin Cilic'
event_df.loc[6224,'event_summary']='An overnight fire destroys parts of Haitis historic Marche en Fer Iron Market in Port Prince. It is unclear what started fire'
event_df.loc[6274,'event_summary']='Latvia will ask European Central Bank not to renew mandate of ECB Governing Council member Ilmoars Rimsevics'
event_df.loc[6629,'event_summary']='Polish environment minister Henryk Kowalczyk says Poland alone should decide fate of protected Bialowieza Forest'
event_df.loc[6775,'event_summary']='The parents of Ayse Deniz Karacagil who died in Iraq Raqqa after joining the outlawed Kurdistan Workers Party'
event_df.loc[6876,'event_summary']='A double decker tourist bus collides with lowlying tree branches in Zurrieq'
event_df.loc[7046,'event_summary']='The European Commission rules Polands logging operations in Bialowieza Forest'
event_df.loc[7071,'event_summary']='The US Geological Surveys Hawaiian Volcano Observatory states that Kilauea is showing unusually high activity and that a new vent could form'
event_df.loc[7343,'event_summary']='Hawaiian volcano Kilauea begins erupting at Leilani Estates subdivision'
event_df.loc[7353,'event_summary']='An earthquake strikes a coal mine near JastrzebieZdroj'
event_df.loc[7375,'event_summary']='About 35 structures in Leilani Estates are destroyed during Kilauea eruption in Hawaii'
event_df.loc[7465,'event_summary']='The summit at Kilauea erupts and sends a plume of ash and smoke 30'
event_df.loc[7521,'event_summary']='A magnitude 4.4 earthquake occurs at Kilauea'
event_df.loc[7529,'event_summary']='Several more properties are destroyed as Kilauea continues to erupt'
event_df.loc[7663,'event_summary']='Hawaiian Airlines warns that eruption of Kilauea may hurt bookings and trim revenues'
event_df.loc[7924,'event_summary']='23 passengers on a tour boat in Hawaii are injured after a lava bomb from Kilauea volcano punctures roof of vessel'
event_df.loc[8200,'event_summary']='Footage from US Geological Survey shows lava activity at Kilauea slowing down'
event_df.loc[8449,'event_summary']='Vietnamese President Tran Dai Quang dies at age of 61 following an extended illness. Vice President Dang Thi Ngoc Thinh succeeds as acting President'
event_df.loc[8457,'event_summary']='Hawai Volcanoes National Park reopens after 134 days of closure due to volcanic activity at Kilauea that damaged park infrastructure'
event_df.loc[8471,'event_summary']='Dunkin Donuts announces it will drop Donuts part of its name and be simply known as dunkin beginning in January 2019'
event_df.loc[8710,'event_summary']='The Turkish chief Istanbul prosecutor Irfan Fidans office states that Jamal Khashoggi was'
event_df.loc[8993,'event_summary']='A highspeed train crashes at Marsandiz railway station in Ankara'
event_df.loc[9469,'event_summary']='Japanese Prime Minister Shinzo Abe says relocation of Marine Corps Air Station Futenma'




In [153]:
event_df.loc[544,'event_summary']='The UN Security Council vote on USChina draft resolution on North Korea is rescheduled to 10:00 AM . Russia requests more time to review text'
event_df.loc[895,'event_summary']='Two weeks after the deadly suicide bombings Brussels Zaventem International Airport will reopen today with three symbolic flights to Faro and Turin. On Thursday the airport had said it was technically ready to resume partial services but the opening was held up because police unions threatened to strike unless additional security checks were introduced'
event_df.loc[6348,'event_summary']='European Union lawmakers strike a deal on opening up 3.6 and 26 GHz bandwidths by 2020 to make room fornew 5G network'
event_df.loc[9489,'event_summary']='The UN Security Council rejected rival resolutions on Venezuela byUS and Russia Thursday. Russia and China vetoed US call for new elections andunhindered distribution of humanitarian aid'


In [154]:
event_df.loc[964,'event_summary']='The French occupy movement known as Nuit debout enters its ninth day March 40th spreading across dozens of French cities and to Belgium and Germany'

In [155]:
event_df.loc[1008,'event_summary']='It has seen a draft memorandum generated by International Monetary Fund that describesdebt owed by Greece to its European partners as highly unsustainable'
event_df.loc[1011,'event_summary']='Taiwan accuses China of extrajudicial abduction after 45 Taiwanese acquitted of fraud in Kenya were forcibly deported to china'
event_df.loc[1015,'event_summary']='North Carolina Governor Pat McCrory signs Executive Order 73 that addresses some but not all troublesome provisions in House Bill two that caused businesses and traveling recording stars to stay clear of the state'
event_df.loc[1016,'event_summary']='Authorities in Panama raid law firm Mossack Fonseca source of data leaked about offshore companies'
event_df.loc[1017,'event_summary']='Hundreds of people take to the streets of Handwara and Jammu and Kashmir after Indian Army soldiers shot dead at least two people during a protest against an alleged case of sexual harassment by an army soldier against a young woman'
event_df.loc[1022,'event_summary']='A magnitude 6.4 earthquake strikes near Kumamoto Japan collapsing several buildings killing at least four people and injuring 400. However no tsunami warning was issued and local nuclear power plants reported no problems'
event_df.loc[1030,'event_summary']='Massive demonstrations in Support ofFree Papua Movement take place in various cities inIndonesian provinces of Papua and West Papua. The demonstrations voice support forLiberation Movement to become a full member ofMelanesian Spearhead Group'
event_df.loc[1032,'event_summary']='The World AntiDoping Agency advises that WADAaccredited laboratories are currently conducting studies on meldonium excretion rates since existing data is lacking. Meldonium became a banned substance on 1st January'
event_df.loc[1033,'event_summary']='Taliban militants kill eight people including a police commander in an ambush in northern Afghanistan'
event_df.loc[1040,'event_summary']='The US company Microsoft has sued United States alleging that it has been prevented from disclosing warrants to the companys customers in violation of Companys constitutional rights'
event_df.loc[1043,'event_summary']='Thousands of opposition supporters rally in Harare Zimbabwe against President Robert Mugabe and deteriorating economy. The rally was banned by police however it went ahead after a ruling by the High Court sanctioned the protest'
event_df.loc[1053,'event_summary']='Authorities in Rwanda jail former politician Leon mugesera for life. Mugesera was known for describing Tutsis as cockroaches and called for their extermination in a speech in 1992 and is said to be a precursor toRwandan genocide'
event_df.loc[1055,'event_summary']='Belgian Minister of Transportation Jacqueline Galant resigns inwake ofrecent bombings that shook Brussels last March. He resigned amid accusations her ministry ignored EU criticism of security at Belgiums airports'
event_df.loc[1063,'event_summary']='A second earthquake hits sourn Japan with a magnitude of 7.1 killing at least thirtytwo people with death toll from both earthquakes rising to fourtyttwo . The new quake traps even more people. In Kumamoto a landslide occurs as well as a bridge collapse'
event_df.loc[1064,'event_summary']='A helicopter crashes near Baltimore to Washington International Airport in Maryland'
event_df.loc[1068,'event_summary']='Pope Francis arrives on the Greek island of Lesbos. He is expected to visit the Moria detention facility while he will have lunch with some of the 3060 people and children'
event_df.loc[1077,'event_summary']='The Prime Minister of Israel Benjamin Netanyahu vows that Israel occupied Golan Heights recognized as part of Syria will forever stay in  countrys hands and called on international community to recognize their sovereignty over area'
event_df.loc[1079,'event_summary']='The President of Myanmar Htin Kyaw pardons 83 political prisoners. A total of 282 people accused of political crimes have been released or had charges dropped sincenew National League for Democracy government gained power on April 1'
event_df.loc[1085,'event_summary']='The Japanese Red Cross says that 250000 people have been asked to leave their homes due to further tremors'
event_df.loc[1087,'event_summary']='Violent storms cause floods across Uruguay with seven people killed and more than 2000 left homeless. Four of those were killed by a tornado that struck Dolores. Four million people in the Chilean capital of Santiago were left without tap water as heavy rains triggered landslides. This led to the fouling of the citys water supply'
event_df.loc[1088,'event_summary']='Heavy rain of more than 1 foot causes major flooding in Houston Texas affecting 1000 homes causing five deaths and causing power outages for over 100000 residents'
event_df.loc[1089,'event_summary']='Protests against President Gjorge Ivanov continue in Skopje capital of Macedonia after his decision to pardon politicians involved in a scandal'
event_df.loc[1092,'event_summary']='The death toll from Saturdays earthquake has risen to at least 480 with 1700 missing. Another 2,500 have been injured. President Rafael Correa states it is the worst disaster in Ecuador in seven decadesand reconstruction will have a Huge Economic Impact on country'
event_df.loc[1093,'event_summary']='Swedish deputy prime minister Asa Romson is criticized after referring to September 11 attacks in New York as mere accidents. Romson madecomments on public television while discussing resignation of housing minister Mehmet Kaplan who had compared Israels treatment of Arabs to Nazis treatment of Jews during Holocaust'
event_df.loc[1094,'event_summary']='Under pressure from Chinese delegation Belgian Deputy Prime Minister Kris Peeters ejects Taiwanese delegation from a symposium of the OECD Steel Committee'
event_df.loc[1096,'event_summary']='In response to an ongoing Supreme Court case regarding the ownership of KohiNoor diamond government of India said it should not try to reclaim it from UK'
event_df.loc[1098,'event_summary']='An American federal appeals court in Richmond Virginia rules a transgender high school student who was banned from the boys bathroom can proceed with the lawsuit against board'
event_df.loc[1100,'event_summary']='While South Korea prepares for the 2018 Winter Olympics Associated Press reports country has covered up widespread human rights violations including rapes and murders when it swept socalled vagrants off streets in years prior to 1988 Games in Seoul'
event_df.loc[1101,'event_summary']='Government of Australian external territory of Norfolk Island announces this is going to take its governance issue to United Nations. Former and final Chief Minister of island lisle Snell said he seeks to have island added on UNs list of Nonself Governing Territories and be given rights that are accorded under terms and conditions of being on list'
event_df.loc[1105,'event_summary']='Mitsubishi admits that its fuel efficiency tests broke Japanese rules for about 625000 ultrasmall vehicles sold in Japan'
event_df.loc[1115,'event_summary']='The United Kingdoms Foreign Office issues a Travel Advisory for gay people concerning travel to parts of US due to new legislation in North Carolina and Mississippi'
event_df.loc[1120,'event_summary']='The first criminal charges are laid against three people two state officials and a municipal official involved in the Flint water crisis'
event_df.loc[1121,'event_summary']='In a letter to International Consortium of Investigative Journalists US Department of Justice announces it is opening a criminal investigation into tax avoidance schemes exposed by Panama Papers with United States attorney Preet Bharara asking ICIJ for help'
event_df.loc[1124,'event_summary']='The United States Supreme Court rules that almost dollar two billion in frozen iranian assets must be turned over to American families of people killed in attacks blamed on Iran'
event_df.loc[1133,'event_summary']='United States President Barack Obama at the Gulf Cooperation Council Summit in Saudi Arabia, says the US will continue to deter and confront aggression against Gulf arab states joins others in warning the fragile cease fire in Syria is on verge of collapse pledges vigilance about Irans destabilizing activities in the Middle East wants Gulf allies to offer more democratic reforms and improve human rights '
event_df.loc[1135,'event_summary']='Six high ranking Pakistan Army officers including a lieutenant general and Major General are sacked by Chief Staff Raheel Sharif amid corruption allegations within army'
event_df.loc[1136,'event_summary']='Ukrainian President Petro Poroshenko signs legislation banning all Russian films made after January 1st 2014'
event_df.loc[1139,'event_summary']='Some Miami Marlins and Pittsburgh Pirates baseball players who are scheduled to play a twogame series the end of May in San Juan to honor Pirates Hall of Famer Roberto Clemente are concerned about being exposed to the Zika virus. About 400 cases have been confirmed in the Commonwealth'
event_df.loc[1149,'event_summary']='State oil company Petroleos Mexicanos reportsdeath toll has risen to 28 from Wednesdays explosion at Petroquimica Mexicana de Vinilos Clorados three petrochemical plant inGulf port city of Coatzacoalcos'
event_df.loc[1157,'event_summary']='Thousands of Sudanese students take tostreets around University of Kordofan in Khartoum and other parts of country to protest recent killing of scholars last Monday'
event_df.loc[1173,'event_summary']='President of Russia Vladimir Putin accusesUS of reneging on a sixteen yearold deal that called for reducing Russias andUS stockpiles of weaponsgrade plutonium. He accused Washington of trying to preserve its ability to turn some of its plutonium stockpile back into a form usable for nuclear weapons'
event_df.loc[1174,'event_summary']='Friday afternoon truce between Kurdish Asayish forces and proSyrian government forces declared following a threeday outbreak of violence that killed at least 26 people is holding'
event_df.loc[1177,'event_summary']='During a rally in support of German comedian Jan Bohmermann, outside the Turkish embassy in Berlin Bruno Kramm head of the branch of Deutsch Pirate Party is arrested for insulting a representative of a foreign state by quoting a line from comics satirical poem about turkish president Recep Tayyip Erdogan'
event_df.loc[1178,'event_summary']='Prime Minister of Pakistan Nawaz Sharif bows to opposition demands that he ask Pakistans chief justice to set up an independent commission to investigate offshore accounts linked to his family. He said he would acceptcommissions findings and even resign if called upon'
event_df.loc[1179,'event_summary']='United States Federal agents are combing three states for 32 cases of commercial grade explosives about 500 pounds of two and half to five inch aerial shells stolen from a CSX train traveling from Chicago Illinois through Ohio that arrived in Detroit Michigan'
event_df.loc[1183,'event_summary']='Solarpowered aircraft Solar Impulse 2 lands in Mountain View California after a 62 hour flight across the Pacific Ocean from Hawaii'
event_df.loc[1193,'event_summary']='The President of US Barack Obama announces that United States will send an additional 250 troops to fight in Syria'
event_df.loc[1198,'event_summary']='A Royal Norwegian Air Force F16 fighter jet taking part in a mock attack on Tarva on April 12rh mistakenly opened fire on a control tower with three officers inside who survived unharmed according to Norwegian military'
event_df.loc[1203,'event_summary']='The top US diplomat in Belarus Scott Rauland and Belarusian Foreign Minister Uladzimer makey said that their countries are ready to discuss possible return of their ambassadors. Makey told reporters in Minsk that there is readiness from both sides for a full normalization of our relations. Belarus recalled its ambassador from Washington in 2008 after United States imposed sanctions against Belarusian oil giant Belneftekhim following tensions between Minsk and West'
event_df.loc[1205,'event_summary']='Turkey says it has deported more than 3300 foreigners suspected of links to jihadi groups and barred another 41000 foreigners from entering country'
event_df.loc[1209,'event_summary']='A Syrian government airstrike near Aleppo kills at least five members ofSyrian Civil Defense rescue organisation. Dozens of people have been killed in Alepppo overpast few days from government airstrikes and opposition bombardment'
event_df.loc[1215,'event_summary']='Foreign Minister Frank Walter Steinmeier apologizes that German diplomats failed to act on abuses at Colonia Dignidad secretive german enclave in Chile whose story is told in the movie colonia. '
event_df.loc[1216,'event_summary']='The US deploys F22 Raptor fighter jets to Romanias RoAF 86th Air Base near the Black Sea in a show of strength and cooperation against Russia'
event_df.loc[1221,'event_summary']=' Voters in the US of Connecticut Delaware Maryland and Pennsylvania and Rhode Island head to the polls to vote in Democratic and Republican presidential primaries'
event_df.loc[1223,'event_summary']='Clashes break out between migrants and riot police at Moria camp onGreek island of Lesbos after a policeman reportedly hit a minor. The violence occurred as a Greek migration minister was visitingcenter. Several refugees/migrants are reported injured'
event_df.loc[1224,'event_summary']='Following heavy pressure from world powers Yemens warring factions agree on an agenda for UN backed peace negotiations to continue'
event_df.loc[1225,'event_summary']='Venezuelan President Nicolas Maduro who previously gave most of countrys 2.8 million state employees Fridays off through May announces public workers will also have Wednesdays and Thursdays off for at least two weeks as an energysaving measure. Full salaries will still be paid despite the twoday week'
event_df.loc[1230,'event_summary']='The US military warns that Kabul Attack Network comprised of fighters from various jihadist groups such as Taliban and Haqqani networks is planning attacks on people in Parwan and Khost and Kabul and Logar Provinces Afghanistan and asks for information from the Afghan public'
event_df.loc[1231,'event_summary']='Archaeologists in Taiwan discover 48 sets of remains unearthed in graves in Taichung. The most striking discovery among them is 4800 yearold skeleton of a mother looking down at a child cradled in her arms'
event_df.loc[1232,'event_summary']='The German cities of Augsburg and Cologne are testing a scheme of traffic lights embedded to reduce cell phone texting pedestrian accidents with vehicles that happen when socalled smombies step out into street against signal'
event_df.loc[1235,'event_summary']='The unrecognized House of Representatives, one of rival governments based in eastern Libya ships its first cargo of crude oil in defiance of UN backed authorities in the capital Tripoli in a move that could deepen divisions within country'
event_df.loc[1240,'event_summary']='Two days before the one year anniversary of the execution of Andrew Chan and Myuran Sukumaran ringleaders of Bali Nine member Michael Czugaj is discovered to be in possession of drugs in prison'
event_df.loc[1241,'event_summary']='Belgian prosecutors hand over Salah Abdeslam key suspect in November 2015 Paris attacks to French authorities'
event_df.loc[1247,'event_summary']='The government of North Korea announces its ruling Workers Party of Korea will hold a party congress on 6th May'
event_df.loc[1257,'event_summary']='In response to UN backed Government of National Accords plea United Nations Security Council blacklists the tanker shipping crude oil by the unrecognized rival House of Representatives government in eastern Libya'
event_df.loc[1258,'event_summary']='Filipino domestic helper Mary Jane Veloso commemoratesfirst anniversary of her being spared from death penalty in Indonesia for allegedly smuggling controlled substances. A trial to determine her innocence is ongoing'
event_df.loc[1262,'event_summary']='The Parliament of Finland holds a debate on whether or not to abandon Euro as its currency following a petition that garnered enough signatures to forceissue into parliament'
event_df.loc[1263,'event_summary']='Africas longest serving leader Teodoro Obiang President of Equatorial Guinea is declared winner of recent election with 93.7 percent of the vote. His government has been heavily criticised by human rights group'
event_df.loc[1264,'event_summary']='A magnitude 7.0 earthquake hits off coast of Vanuatu island of Malakula prompting Pacific Tsunami Warning Center to issue a tsunami warning for the coasts of New Caledonia and Papua New Guinea and Solomon Islands and Vanuatu which was later cancelled'
event_df.loc[1273,'event_summary']='The states of Oklahoma and Nebraska having recently suffered a loss in their frontal attack on Colorados state legal cannabis policy launch another litigation strategy to the same end.'
event_df.loc[1281,'event_summary']='A threestorey building collapses in Indian city of Mumbai resulting in six deaths and trapping many others'
event_df.loc[1283,'event_summary']='A mosque under refurbishment in Mogadishu Somalia collapses killing at least 15 people and injuring around 40. Hundreds more are thought to be buried under the rubble.'
event_df.loc[1287,'event_summary']='Russia says it intercepted a US Air Force plane approaching its border overBaltic Sea on Friday becauseaircraft had turned off its transponder which is needed for identification. The Pentagon saysUS RC135 was flying a routine route in international airspace when Russian SU27 fighter intercepted in an unsafe and unprofessional way'
event_df.loc[1300,'event_summary']='Adelaide United win their first ALeague championship beating Western Sydney Wanderers three to one in Grand Final at Adelaide Oval'
event_df.loc[1301,'event_summary']='Three bombings in and around Baghdad kill at least 14 including Shiite pilgrims and injure more than 30'
event_df.loc[1303,'event_summary']='Australian tech entrepreneur Craig Steven Wright claims he is Satoshi Nakamoto creator of the Bitcoin currency'
event_df.loc[1304,'event_summary']='Puerto Rico defaults on a dollar 422 million debt payment. The Governor of puerto rico Alejandro Garcia Padilla calls situation a humanitarian crisis'
event_df.loc[1307,'event_summary']='United States Chief of Naval Operations Admiral John M. richardson says Russian jets in Baltics buzzing a US military ship and planes are escalating tension between two nations. Richardson added he doesnt think Russians are trying to provoke an incident but these actions increase chance of a tactical miscalculation'
event_df.loc[1309,'event_summary']='Honduran authorities arrest four men in March 3rd home invasion killing of Goldman Environmental Prizewinning environmental activist Berta Caceres'
event_df.loc[1313,'event_summary']='Researchers report in the journal Nature the discovery of three potentially habitable Earth like exoplanets orbiting TRAPPIST1 an ultracool dwarf star 40 lightyears away in the constellation Aquarius'
event_df.loc[1317,'event_summary']='A mandatory evacuation order for more than 29000 people remains in place for the Canadian town of Fort McMurray Alberta, which is threatened by an out of control wildfire'
event_df.loc[1322,'event_summary']='The government of Hungary announces it will hold a referendum regarding future European Union quotas for resettling refugees. The vote is expected to be held either in September or October of this year where a turnout of over 50 percent will render to be valid'
event_df.loc[1330,'event_summary']='British publisher Trinity Mirror announces that its daily newspaper The New Day will close after just two months since its launch after sales fell to around 30000 copies per day. The last edition will be printed on May 6'
event_df.loc[1331,'event_summary']='Alberta Premier Rachel Notley says the wildfire has destroyed about 1000 structures in Fort McMurray which is in Canadas oil sands region'
event_df.loc[1340,'event_summary']='A Palestinian woman is killed and another person is injured in Gaza Strip by tank fire from Israel. It responded to mortar rounds and discovery of another tunnel by Hamas'
event_df.loc[1344,'event_summary']='Hackers attack millions of users of Gmail and Hotmail and Yahoo Mail forcing to make password changes'
event_df.loc[1345,'event_summary']='Turkish Prime Minister Ahmet Davutoglu announces his resignation effective twentytwo May amid conflict with President Recep Tayyip Erdogan over Turkeys increasingly authoritarian rule'
event_df.loc[1346,'event_summary']='Former Governor of Texas and Republican presidential candidate Rick Perry endorses Donald Trump for president and says he is open to being Trumps VicePresidential running mate'
event_df.loc[1352,'event_summary']='Irans elected Parliament member from Maragheh and Ajabshir district dies in a car crash in Zanjan. He was set to take office on 28 May'
event_df.loc[1360,'event_summary']='Unidentified gunmen shoot dead Khurram Zaki a Pakistani rights activist known for speaking out against the Taliban'
event_df.loc[1365,'event_summary']='At least seven people are killed and thirty injured in a bus accident in Ranchi'
event_df.loc[1369,'event_summary']='US District Judge Emmet Sullivan blocks the dollar 6.3 billion merger of major office supply companies Staples and Office Depot finding it would result in reduced competition and higher prices'
event_df.loc[1371,'event_summary']='Alberta authorities update information about fire. About 2400 homes and buildings were destroyed but firefighters saved 25000 others in city including hospital and municipal buildings and every functioning school'
event_df.loc[1377,'event_summary']='A fragment of the worlds oldest groundedge axe dated at between 45000 and 49000 years old is found in the Kimberley region of Western Australia'
event_df.loc[1379,'event_summary']='The head of Bangladesh largest Islamist party JamaateIslami Motiur Rahman Nizami is executed for his alleged role in acts of genocide and war crimes 45 years ago during the independence war against Pakistan in 1971'
event_df.loc[1380,'event_summary']='Amnesty International reports that this year at least 149 have died including children in a military detention center Giwa barracks in Maiduguri Nigeria'
event_df.loc[1382,'event_summary']='The Federal Senate of Brazil debates whether to suspend and impeach President Dilma Rousseff for allegedly breaching budget rules. The Presidents allies are not optimistic about Senate vote'
event_df.loc[1389,'event_summary']='Turkish president Recep Tayyip Erdogan threatens unilateral action against Islamic State of Iraq and Syria'
event_df.loc[1392,'event_summary']='A 120 year old woman is found living in the Astrakhan Oblast of Russia which would make her worlds oldest living person'
event_df.loc[1393,'event_summary']='Researchers from Konkoly Observatory in Budapest Hungary reveal that  2007 OR10 is the third largest dwarf planet in the solar system'
event_df.loc[1404,'event_summary']='At least 14 suicide bombers attack a complex killing themselves and at least 6 people'
event_df.loc[1417,'event_summary']='At least 15 students are killed and six are missing after heavy rains and flash flooding trigger a landslide at a popular tourist resort in Deli Serdang Regency'
event_df.loc[1418,'event_summary']='Colombian police announce the seizure of about eight tonnes of cocaine in an operation targeting the Clan Usuga gang. This would make it the biggest seizure of drugs in the history of colombia'
event_df.loc[1419,'event_summary']='A Swedish court sentences Claver Berinkindi a 61 yearold Swedish citizen originally from Rwanda to life in prison for participation in the Rwandan genocide in 1994'
event_df.loc[1423,'event_summary']='A flare up of wildfires around Fort McMurray has caused evacuation of 8000 workers'
event_df.loc[1424,'event_summary']='Amid growing concern about North Koreas ballistic missile capability Southkorea and Japan and US are to hold their first ever joint antimissile exercise next month according to southkorea Ministry of National Defense'
event_df.loc[1432,'event_summary']='A powerful 6.7 magnitude earthquake hits Ecuador near the town of Muisne one person is killed'
event_df.loc[1434,'event_summary']='China stages joint war games featuring mock beach landing helicopter assaults and tank battles along its east coast just days before the inauguration of Taiwanese president Tsai Ing Wen'
event_df.loc[1436,'event_summary']='Syrian government forces and allies including Lebanese Hezbollah fighters retake a large area southeast of Damascus including the key town of Deir alAsafir'
event_df.loc[1440,'event_summary']='Google honors Asian American civil rights activist Yuri Kochiyama who held controversial views about racial harmony terrorism and American power with a doodle'
event_df.loc[1450,'event_summary']='Temperatures soar to a record 51 centigrade in Indian state of Rajasthan. The heatwave has claimed 300 lives since April 2016'
event_df.loc[1457,'event_summary']='A US Secret Service officer shoots an armed man on a street near White House after man allegedly approached him and refused to drop his weapon. The White House is locked down'
event_df.loc[1460,'event_summary']='The Oklahoma legislature passes a bill that would make it a felony for doctors to perform abortions and revokes medical license of assisting physicians'
event_df.loc[1464,'event_summary']='At least 21 are killed and more than 500000 are displaced by cyclone Roanu in Bangladesh'
event_df.loc[1465,'event_summary']='At least thirtyseven people have been killed and twentytwo injured in a bus crash in Democratic Republic of Congo'
event_df.loc[1467,'event_summary']='Norway Foreign Minister Borge Brende says his government is doubling humanitarian aid to Afghanistan to around 200 million kroner USdollar 24 million'
event_df.loc[1474,'event_summary']='Syrian Observatory for Human Rights claims that over 60000 people have died in Syrian government jails during the five year civil war'
event_df.loc[1480,'event_summary']='Reuters reports nearly 150 people are killed and at least 200 wounded in a series of car bomb and suicide attacks in Syrian cities of Jableh and Tartus in governmentcontrolled territory that hosts Russian military bases. The Islamic State of Iraq and Levant group claims responsibility'
event_df.loc[1486,'event_summary']='An overnight fire at Pitakiatwittaya Christian elementary schools dormitory in northern Chiang Rai Province in Thailand kills 18 girls between ages of five and twelve'
event_df.loc[1491,'event_summary']=' The firstever UN humanitarian summit opens in Istanbul Turkey to address the 125 million people crisis worst since World War II'
event_df.loc[1493,'event_summary']='Judge Barry Williams finds Baltimore Maryland Police Officer Edward nero not guilty of all charges. Nero was accused of second degree intentional assault two counts of misconduct in office and reckless endangerment. Community leaders and elected officials appeal for calm.'

event_df.loc[1506,'event_summary']='Googles offices in central Paris are raided by French finance officials as part of a tax fraud investigation'
event_df.loc[1507,'event_summary']='Motorist Wahib Sadek Ahmed is arrested after he is accused of wielding a knife at a motorist. He is subdued after four taser shots. The FBI investigates after sadek claim to be affiliated with a terrorist organization'
event_df.loc[1512,'event_summary']='At least five die after their overcrowded repurposed trawler capsized in the southern Mediterranean Sea off the coast of Libya. The Italian navy rescued 562 people'
event_df.loc[1514,'event_summary']='Archaeologists announce the discovery of a 2400 yearold tomb which they believe to be that of Aristotle based on its grandiosity and its location atop a hill in Stagira the city of his birth'
event_df.loc[1515,'event_summary']='The Scripps National Spelling Bee in US finishes with a tie between Jairam Hathwar and Nihar Janga. This is third successive year event has finished in a Tie'
event_df.loc[1517,'event_summary']='At least 20 people drown in southern Mediterranean Sea when repurposed fishing boat sinks 35 nautical miles north of Zuwara'
event_df.loc[1518,'event_summary']='Researchers at the United States Department of Defense report in the journal Antimicrobial Agents and Chemotherapy discovery in the US of a strain of Ecoli that includes the new gene MCR1 which is resistant to colistin a last resort antibiotic'
event_df.loc[1520,'event_summary']='South Korea plans to import arms worth about 3.5 trillion won USdollar three billion this year to enhance its defense capabilities'
event_df.loc[1522,'event_summary']='A lawsuit brought against Google by Oracle Corporation accusing Google of using copyrighted code for Android operating system is decided in googles favor'
event_df.loc[1526,'event_summary']='The Pittsburgh Penguins defeat Tampa Bay Lightning in Game seven of Eastern Conference Final to advance to Stanley Cup Final they will face San Jose Sharks'
event_df.loc[1533,'event_summary']='The legal team of Joaquin Guzman leader of the Sinaloa Cartel has challenged the foreign ministry of Mexicos decision to extradite him to the United States'
event_df.loc[1539,'event_summary']='A Rutan VariEze experimental aircraft crashes north of Ventura California killing the two people aboard'
event_df.loc[1553,'event_summary']='Tropical Storm Bonnie makes landfall on East Coast of US affecting mainly the city of Charleston South Carolina'
event_df.loc[1554,'event_summary']='In compliance with recent UN Security Council resolutons President Yoweri Museveni of Uganda announces an end to security and military cooperation with North Korea'
event_df.loc[1555,'event_summary']='Mexican international football player Alan Pulido who plays for Olympiacos F. C. is kidnapped by masked men near his home in Ciudad Victoria Tamaulipas. He is later rescued'
event_df.loc[1564,'event_summary']='A new study by University of Colorado Boulder researchers published in the Proceedings of the National Academy of Sciences finds opioid medicines can paradoxically cause an increase in chronic pain in lab rats'
event_df.loc[1570,'event_summary']='In an interview with the German broadsheet Frankfurter Allgemeine Tibetan spiritual leader Dalai Lama says that germany has taken too many refugees only be accommodated temporarily with the goal of them returning home to rebuild their countries'
event_df.loc[1572,'event_summary']='A recent Global Slavery Index report estimates the number of people born into servitude trafficked for sex work in debt bondage or forced labour to be 45.8 million. India is reported to have the highest number at an estimated 18.4 million slaves and North Korea the highest ratio 4.4 percent of its population.'
event_df.loc[1575,'event_summary']='Association football icon Pele announces that he will sell 1500 lots of his possessions via Juliens Auctions which will include his medals and trophies and jerseys nd diplomatic gifts'
event_df.loc[1581,'event_summary']='The Public Investment Fund of Saudi Arabia invests dollar 6.5 billion in Uber . It is largest single investment company has ever received as of that date'
event_df.loc[1584,'event_summary']='Residents return to Fort McMurray for first time since 1st May'
event_df.loc[1592,'event_summary']='The worlds longest and deepest rail tunnel the 57 km  Gotthard Base Tunnel opens in Switzerland'
event_df.loc[1594,'event_summary']='In a raid by Somali forces near Kismayo at least 16 AlShabaab militants are killed including the mastermind of the Garissa University College attack'
event_df.loc[1595,'event_summary']='The US announces new rules that will go into effect on 6th July this amount to a neartotal ban on the commercial trade of African elephant ivory'
event_df.loc[1607,'event_summary']='The Supreme Court of US accepts a petition by five people from American Samoa arguing that People born in this United States territory are entitled to US citizenship under US Constitution. The State Department currently opposes this idea'
event_df.loc[1610,'event_summary']='Eleven cars from a 96 car Union Pacific oil train derail and at least one catches fire in the Columbia River Gorge near Mosier Oregon within about 20 feet of the citys sewage plant'
event_df.loc[1612,'event_summary']='A study by researchers at the University of North Carolina at Chapel Hill presented at the American Society of Clinical Oncology meeting in Chicago reports 26 percent of cancer patients cant afford to pay for their treatment and 18 percent cant afford their prescriptions'
event_df.loc[1616,'event_summary']='Syrian Government forces enter Raqqa province the joint capital of Islamic State in Iraq and the Levant'
event_df.loc[1618,'event_summary']='The flight recorder casings and potential flight recorder of Eastern Flight 980 which crashed in 1985 on Mount Illimani Bolivia are recovered by hikers from Boston'
event_df.loc[1621,'event_summary']='Turkish Air Force bombs Kurdistan Workers Party targets in northern Iraq and southeastern Turkey killing at least twentyseven militants'
event_df.loc[1627,'event_summary']='Six people are hurt as an unknown assailant fires shots at a Czech tourist bus on A7 autoroute near SaulcesurRhone in southeastern France'
event_df.loc[1628,'event_summary']='Novak djokovic tops Andy Murray to win French Open mens championship. This completes his noncalendar year Grand Slam. Djokovic is first man since 1969 Rod Laver to hold all four Grand Slam singles titles at once'
event_df.loc[1635,'event_summary']='Researchers report that testing of 5000 forgotten Cuyahoga County hio police rape kits for unsolved cases between 1993 and 2010 has led to more than 250 criminal convictions'
event_df.loc[1637,'event_summary']='Seven police officers and four civilians are killed and 36 people are wounded three critically by a car bomb explosion near the main tourism district in Istanbul Turkey'
event_df.loc[1638,'event_summary']='Kazakhstan police report death toll from Sundays attack in Aktobe is now 19 three civilians'
event_df.loc[1641,'event_summary']='A pickup truck reported to be driving erratically mowed down a group of nine bicycle riders killing five and injuring four near Kalamazoo Michigan'
event_df.loc[1642,'event_summary']='Johns Hopkins University researchers report in the journal Health Affairs that media reports about people accused of committing violent crimes having mental illnesses rarely discuss successful treatment of patients and thereby overstate the problem'
event_df.loc[1643,'event_summary']='Voters go to the polls in six states including California and New Jersey with Hillary Clinton gaining enough delegates to become the presumptive nominee of the Democratic Party. She will be the first woman nominee by a major party to run for President of the United States'
event_df.loc[1645,'event_summary']='The Taliban kills 12 members of Afghanistans security forces who were captured in recent ambushes in Ghazni Province on June 3th and 5th'
event_df.loc[1651,'event_summary']='The International Union of Pure and Applied Chemistry proposes final names for four new chemical elements : nihonium and moscovium and tennessine  and oganesson '
event_df.loc[1663,'event_summary']='New Zealand Prime Minister John Key visits Fiji first time a Kiwi leader has done so since the 2006 coup detat. Key is hoping to improve relations between the two countries though its clear their political tensions dont have easy solutions'
event_df.loc[1666,'event_summary']='US President Barack Obama endorses Hillary Clinton for President of United States'
event_df.loc[1667,'event_summary']='Researchers in Iceland report on CarbFix in the journal Science that carbon dioxide emissions can be pumped into the earth and changed chemically to stone significantly faster than expected'
event_df.loc[1671,'event_summary']='Amazon is preparing to start a standalone streaming music service in direct competition with Apple Music and Spotify'
event_df.loc[1672,'event_summary']='The United States Geological Survey reports a magnitude 5.1 earthquake strikes near Borrego Springs Southern California'
event_df.loc[1677,'event_summary']='A Maldives court convicts Ahmed Adeeb the countrys former vice president of masterminding a plot to kill President Abdulla Yameen. He is sentenced to 15 years in prison. Earlier this week Adeeb was sentenced to 10 years for firearms possession'
event_df.loc[1679,'event_summary']='Fighting breaks out between militants and Afghan police in Haska Mina District Nangarhar Province leaving six police officers and 15 militants dead'
event_df.loc[1682,'event_summary']='The 70th Tony Awards are held at Beacon Theater in New York City with The Humans winning best Play and Hamilton winning Best Musical'
event_df.loc[1686,'event_summary']='Lawyers for former President of Chad Hissene Habre who was recently found guilty of crimes against humanity and sentenced to life in prison appeal the verdict. However a tribunal spokesman said the appeal process is not expected to be done before April 2017'
event_df.loc[1688,'event_summary']='Canadian Prime Minister Justin Trudeau says his government has compelling reason to believe that Robert Hall who was held hostage in the Philippines has been killed by his captors presumably the same Abu Sayyaf militants who beheaded another canadian John Ridsdel on 25 April 2016'
event_df.loc[1689,'event_summary']='A car bomb injures at least nine people three in serious condition in the mainly Kurdish southeast region in Turkeys Tunceli Province '
event_df.loc[1693,'event_summary']='Eleven TurkishGerman members of germanys Parliament Bundestag who voted in support of declaring the Ottoman Turks slaughter of Armenians in 1915 a genocide are under police protection'
event_df.loc[1698,'event_summary']='The US Supreme Court strikes down a Puerto Rican law that would have allowed it to restructure debts of its public utilities over objections of creditors. Puerto Ricos agencies have a dollar two billion debt payment due 1st July and has already defaulted on a dollar 370 million debt payment for its Government Development Bank back on 1st May'






In [156]:
event_df.loc[1698,'event_summary']

'The US Supreme Court strikes down a Puerto Rican law that would have allowed it to restructure debts of its public utilities over objections of creditors. Puerto Ricos agencies have a dollar two billion debt payment due 1st July and has already defaulted on a dollar 370 million debt payment for its Government Development Bank back on 1st May'

In [157]:
# columns=['Arg_ID', 'event_id', 'arg_pos'.'argtext','arglevel','phraselabel','arg_indicies']
Args_df = pd.DataFrame()
Args_df['Arg_ID']='NA'
Args_df['event_id']='NA'
# Args_df['s_arg_pos']='NA'
# Args_df['e_arg_pos']='NA'
Args_df['argtext']='NA'
# Args_df['arglevel']='NA'
# Args_df['phraselabel']='NA'
# Args_df['arg_indicies']='NA'

In [158]:
ann = StanfordNLP()
ann.props = {
            'annotators': 'ssplit',
            'pipelineLanguage': 'en',
            'outputFormat': 'json'
        }

l=0

for j in range(0,100):
    fo = open('verbphrase', 'w', encoding="utf-8")
    text = event_df.loc[j,'event_summary']
    id1 = event_df.loc[j,'event_id']
    print(id1)
    print("\n")
    print(text+"\n")
    sentences = ann.annotate(text)
    for sentence in sentences['sentences']:
        sent_str = ''.join([key_word['before'] + key_word['word'] for key_word in sentence['tokens']]).strip()
#         print (sent_str)

        parsestr=sNLP.parse(sent_str)
#         print (parsestr)
        root_tree = Tree.fromstring(parsestr)
        parsed_arguments = {}
        for  i in root_tree.subtrees():
            if i.label() == 'NP':
                count = len([j for j in i.subtrees() if j.label() in ['NP','VP','PP']])
#             print ('%d\t%s' %(count, str(i.leaves())))
                if count > 1:
                   continue
 
                fo.write(str( i.leaves())+ ';')
                print(str( i.leaves()))

    fo.close()        
    with open('verbphrase', 'r',encoding="utf8") as file:
        data = file.read().replace('\n', '')

        split_data=data.split(';')
#         print (split_data[0])
#         print(len(split_data))
        
        for k in range(0,len(split_data)):
#             k=k+1
#             df['Nounphrases'+ str(k) ]="random"
#             print(l)
            Args_df.loc[l,'argtext']=split_data[k]
            Args_df.loc[l,'event_id']=event_df.loc[j,'event_id']
            Args_df.loc[l,'argtext'] = str(Args_df.loc[l,'argtext']).strip('[]')
            Args_df.loc[l,'argtext'] = str(Args_df.loc[l,'argtext']).replace(',','')
            Args_df.loc[l,'argtext'] = str(Args_df.loc[l,'argtext']).replace('\'','')
            Args_df.loc[l,'argtext'] = str(Args_df.loc[l,'argtext']).replace('\"','')
    
            l=l+1
        file.seek(0)
    fo = open('verbphrase', 'w').close()


0


A shooting takes place at a pub in Tel Aviv

['A', 'shooting']
['place']
['a', 'pub']
['Tel', 'Aviv']
1


About one thousand houses in Manilas Tondo district in Philippines are set ablaze following New Years Eve firecracker festivities that left two dead and 380 others injured

['one', 'thousand', 'houses']
['Manilas', 'Tondo', 'district']
['Philippines']
['ablaze']
['New', 'Years']
['Eve', 'firecracker', 'festivities']
['two']
['380', 'others']
2


The EUUkraine Free Trade deal officially comes into force

['The', 'EUUkraine']
['Free', 'Trade']
['force']
3


The twochild policy takes effect in China

['The', 'twochild', 'policy']
['effect']
['China']
4


The Islamic State of Iraq and Levant claims responsibility for a suicide bomb attack on a Iraqi Army base Camp Speicher

['The', 'Islamic', 'State']
['Iraq', 'and', 'Levant']
['responsibility']
['a', 'suicide', 'bomb', 'attack']
['a', 'Iraqi', 'Army', 'base']
['Camp', 'Speicher']
5


Fiji warns residents to prepare for impact of s

['The', 'Islamic', 'States', 'Libyan', 'branch']
['attacks']
['Libyas', 'oil', 'ports']
['Sidra']
['Ras', 'Lanuf']
34


Bahrain says it has dismantled a terrorist cell allegedly linked to Irans Revolutionary Guard and Lebanons Hezbollah

['Bahrain']
['it']
['a', 'terrorist', 'cell']
['Irans', 'Revolutionary', 'Guard', 'and', 'Lebanons', 'Hezbollah']
35


Starwars : The Force Awakens becomes highestgrossing film ever in US and Canada

['Starwars']
['The', 'Force', 'Awakens']
['highestgrossing', 'film']
['US', 'and', 'Canada']
36


A 5.1 magnitude earthquake near Sungjibaegam

['A', '5.1', 'magnitude', 'earthquake']
['Sungjibaegam']
37


German police temporarily seal off main entrance to chancellery building because of a suspicious package

['German', 'police']
['main', 'entrance']
['chancellery', 'building']
['a', 'suspicious', 'package']
38


Texas state trooper Brian Encinia is charged with perjury in connection with death of Sandra Bland

['Texas', 'state', 'trooper', 'Brian', 'Enci

['Thousands']
['protesters']
['Leipzig']
['a', 'record', 'refugee', 'influx']
['they']
['mass', 'sexual', 'violence']
['New', 'Years']
['Eve', 'events']
['Cologne']
['other', 'German', 'cities']
73


At least 10 people are killed and 15 injured

['At', 'least', '10', 'people']
['and', '15']
74


Boko Haram militants shoot and kill seven people and burn down 10 houses in Madagali

['Boko', 'Haram', 'militants']
['seven', 'people']
['10', 'houses']
['Madagali']
75


A Bronze Age village is discovered in Cambridgeshire

['A', 'Bronze', 'Age', 'village']
['Cambridgeshire']
76


Junior doctors in United Kingdom go on strike over a proposed new contract

['Junior', 'doctors']
['United', 'Kingdom']
['strike']
['a', 'proposed', 'new', 'contract']
77


Hurricane Pali becomes earliest hurricane on record in central Pacific Ocean. It is currently no threat to land

['Hurricane', 'Pali']
['earliest', 'hurricane']
['record']
['central', 'Pacific', 'Ocean']
['It']
['no', 'threat']
['land']
78


Five

In [159]:
Args_df=Args_df.replace({'argtext': {'': np.nan}}).dropna(subset=['argtext'])

In [160]:
Args_df=Args_df.reset_index()

In [161]:
Args_df.loc[:,'Arg_ID'] = np.arange(len(Args_df))

In [162]:
Args_df=Args_df[['Arg_ID','event_id','argtext']]

In [163]:
Args_df

Arg_ID event_id                 argtext
0    0       0        A shooting            
1    1       0        place                 
2    2       0        a pub                 
3    3       0        Tel Aviv              
4    4       1        one thousand houses   
..  ..      ..                        ...   
492  492     98       88th Academy Awards   
493  493     98       Samuel Goldwyn Theater
494  494     98       Hollywood             
495  495     99       Actor Alan Rickman    
496  496     99       cancer                

[497 rows x 3 columns]

### 6. Creating Event annotation dataframe 

In [164]:
anno_df=pd.DataFrame()

In [165]:
anno_df['Anno_ID']="NA"
anno_df['Arg_ID']="NA"
anno_df['argtext']="NA"
anno_df['Text']="NA"
anno_df['Important']="NA"
# anno_df['Relation Phrase']="NA"

In [166]:
for i in range(0,497):
    anno_df.loc[i,'Arg_ID']=Args_df.loc[i,'Arg_ID']
    anno_df.loc[i,'argtext']=Args_df.loc[i,'argtext']
    
    

In [167]:
anno_df.loc[:,'Anno_ID'] = np.arange(len(anno_df))

In [168]:
anno_df

Anno_ID Arg_ID                 argtext Text Important
0    0        0      A shooting              NaN  NaN     
1    1        1      place                   NaN  NaN     
2    2        2      a pub                   NaN  NaN     
3    3        3      Tel Aviv                NaN  NaN     
4    4        4      one thousand houses     NaN  NaN     
..  ..       ..                      ...     ...  ...     
492  492      492    88th Academy Awards     NaN  NaN     
493  493      493    Samuel Goldwyn Theater  NaN  NaN     
494  494      494    Hollywood               NaN  NaN     
495  495      495    Actor Alan Rickman      NaN  NaN     
496  496      496    cancer                  NaN  NaN     

[497 rows x 5 columns]

### 7. Need to compare nounphrases and with event summary and replace them with Span of phrase.

In [169]:
colors=['#C0C0C0','#EAB9B9','#FFB19D','#DBD0CC','#FFDAB9','#fabebe','#FFCC99','#A5C1E5','#A0CAFF','#ADADEB','#9999FF','#F1BBFF','#DAC9DA','#FF99FF','#E698CC','#FF96C9','#FFC4D8','#C0C0C0','#EAB9B9','#FFB19D','#DBD0CC','#FFDAB9','#fabebe','#FFCC99','#A5C1E5','#A0CAFF','#ADADEB','#9999FF','#F1BBFF','#C0C0C0','#EAB9B9','#FFB19D','#DBD0CC','#FFDAB9','#fabebe','#FFCC99','#A5C1E5','#A0CAFF','#ADADEB','#9999FF','#F1BBFF','#C0C0C0','#EAB9B9','#FFB19D','#DBD0CC','#FFDAB9','#fabebe','#FFCC99','#A5C1E5','#A0CAFF','#ADADEB','#9999FF','#F1BBFF','#C0C0C0','#EAB9B9','#FFB19D','#DBD0CC','#FFDAB9','#fabebe','#FFCC99','#A5C1E5','#A0CAFF','#ADADEB','#9999FF','#F1BBFF','#C0C0C0','#EAB9B9','#FFB19D','#DBD0CC','#FFDAB9','#fabebe','#FFCC99','#A5C1E5','#A0CAFF','#ADADEB','#9999FF','#F1BBFF','#C0C0C0','#EAB9B9','#FFB19D','#DBD0CC','#FFDAB9','#fabebe','#FFCC99','#A5C1E5','#A0CAFF','#ADADEB','#9999FF','#F1BBFF','#C0C0C0','#EAB9B9','#FFB19D','#DBD0CC','#FFDAB9','#fabebe','#FFCC99','#A5C1E5','#A0CAFF','#ADADEB','#9999FF','#F1BBFF']

In [170]:
m=0
pp=0
for i in range(0,100):
    if pp==100:
        pp=0
    string=event_df.loc[i,'event_summary']
    iid=event_df.loc[i,'event_id']
#     print(string)
#     print("ID: "+str(iid))
    k=0
    for j in range (0,497):
        if Args_df.loc[j,'event_id']==event_df.loc[i,'event_id']:
#             print(Args_df.loc[j,'event_id'])
#             print(Args_df.loc[j,'argtext'])
#             print(event_df.loc[i,'event_id'])
#             print(Args_df.loc[j,'event_summary'])
            k=k+1
#     print("................................")
#     print(k) 
#     print("................................")

        
#     print(k)  
#     print(string)
    n=m+k
#     print(m)
#     print(n)
#     if Args_df.loc[j,'event_id']==event_df.loc[i,'event_id']:
    for x in range(m,n):
        
        
        if Args_df.loc[x,'argtext'] in string:
            if pp==100:
                pp=0
            pos = string.find( Args_df.loc[x,'argtext'] )
            epos = pos +len(Args_df.loc[x,'argtext'])
            string=string[:pos]+" <span class=span1 id="+str(Args_df.loc[x,'Arg_ID'])+" style='background-color:"+colors[pp]+";'> "+Args_df.loc[x,'argtext']+" </span>"+string[epos:]

#             string=string.replace(Args_df.loc[x,'argtext'],"<span id="+str(Args_df.loc[x,'Arg_ID'])+" style='background-color:"+colors[pp]+"; display:inline-block; overflow: hidden;text-overflow:ellipsis;width:auto;padding:2px 5px; margin: 0 5px; border-radius: 10px' >"+Args_df.loc[x,'argtext']+"</span>")
            pp=pp+1
        else:
            print("hi")
            print(Args_df.loc[x,'Arg_ID'])
            print(Args_df.loc[x,'argtext'])
            print(event_df.loc[i,'event_id'])
#     print(string+"\n")
    event_df.loc[i,'eventsummary']=string+" "
   
    m=x+1
#     print("hey i am here"+str(m))
#            
            
#             k=k+1
#         elif Args_df.loc[j,'event_id']!=event_df.loc[i,'event_id']:
                

In [171]:
event_df.loc[1346,'eventsummary']=" <span class=span1 id=2007 style='background-color:#A5C1E5;'> Former Governor </span> of  <span class=span1 id=2008 style='background-color:#A0CAFF;'> Texas </span> and  <span class=span1 id=2009 style='background-color:#ADADEB;'> Republican  <span class=span1 id=2011 style='background-color:#F1BBFF;'> presidential </span> candidate Rick Perry </span> endorses  <span class=span1 id=2010 style='background-color:#9999FF;'> Donald Trump </span> for president and says  <span class=span1 id=2012 style='background-color:#DAC9DA;'> he </span> is open to being  <span class=span1 id=2013 style='background-color:#FF99FF;'> Trumps </span>  <span class=span1 id=2014 style='background-color:#E698CC;'> vicepresidential running mate </span> "

In [172]:
event_df.loc[4692,'eventsummary']=" <span class=span1 id=876 style='background-color:#F1BBFF;'> The Supreme Court </span> of  <span class=span1 id=877 style='background-color:#C0C0C0;'> the United States </span> partially reinstates  <span class=span1 id=878 style='background-color:#EAB9B9;'> President Donald Trumps </span> travel  <span class=span1 id=879 style='background-color:#FFB19D;'> ban </span> and invalidates  <span class=span1 id=880 style='background-color:#DBD0CC;'> certain injunctions </span> that were put on  <span class=span1 id=881 style='background-color:#FFDAB9;'> the order </span> by  <span class=span1 id=882 style='background-color:#fabebe;'> two federal appeals </span>  <span class=span1 id=883 style='background-color:#FFCC99;'> courts </span> earlier .  <span class=span1 id=884 style='background-color:#A5C1E5;'> Final oral hearings </span> concerning  <span class=span1 id=885 style='background-color:#A0CAFF;'> the legality </span> of  <span class=span1 id=886 style='background-color:#ADADEB;'> the Executive Order 13780 </span> will be held in  <span class=span1 id=887 style='background-color:#9999FF;'> October 2017 </span> at  <span class=span1 id=888 style='background-color:#F1BBFF;'> the Supreme Court </span> "

In [173]:
event_df.loc[4744,'eventsummary']=" <span class=span1 id=1143 style='background-color:#FFB19D;'> Floods </span> in  <span class=span1 id=1144 style='background-color:#DBD0CC;'> South China </span> kill  <span class=span1 id=1145 style='background-color:#FFDAB9;'> at least 15 people </span> over  <span class=span1 id=1146 style='background-color:#fabebe;'> the last few days </span> with  <span class=span1 id=1147 style='background-color:#FFCC99;'> tens of thousands </span> more being relocated . More  <span class=span1 id=1148 style='background-color:#A5C1E5;'> rain </span> is forecast in  <span class=span1 id=1149 style='background-color:#A0CAFF;'> future days </span> "

In [174]:
event_df.loc[4817,'eventsummary']=" <span class=span1 id=1516 style='background-color:#FFC4D8;'> Scientists </span> at  <span class=span1 id=1517 style='background-color:#C0C0C0;'> the Chinese Academy </span> of  <span class=span1 id=1518 style='background-color:#EAB9B9;'> Sciences </span> successfully teleport  <span class=span1 id=1519 style='background-color:#FFB19D;'> a photon </span> from  <span class=span1 id=1520 style='background-color:#DBD0CC;'> a ground station </span> in  <span class=span1 id=1521 style='background-color:#FFDAB9;'> Tibet </span> to  <span class=span1 id=1522 style='background-color:#fabebe;'> a satellite </span> orbiting  <span class=span1 id=1523 style='background-color:#FFCC99;'> Earth </span> at  <span class=span1 id=1524 style='background-color:#A5C1E5;'> distance </span> of  <span class=span1 id=1525 style='background-color:#A0CAFF;'> 500 km </span> away .  <span class=span1 id=1526 style='background-color:#ADADEB;'> It </span> is  <span class=span1 id=1527 style='background-color:#9999FF;'> the first time </span>  <span class=span1 id=1528 style='background-color:#F1BBFF;'> an object </span> has been teleported from  <span class=span1 id=1529 style='background-color:#C0C0C0;'> the planet </span> into  <span class=span1 id=1530 style='background-color:#EAB9B9;'> space </span> "

In [175]:
# event_df.loc[4819,'eventsummary']=" <span class=span1 id=1535 style='background-color:#FFCC99;'> Donald Trump Jr </span> discloses  <span class=span1 id=1536 style='background-color:#A5C1E5;'> emails </span> in which  <span class=span1 id=1537 style='background-color:#A0CAFF;'> he </span> and  <span class=span1 id=1538 style='background-color:#ADADEB;'> Rob Goldstone </span> discuss gathering  <span class=span1 id=1539 style='background-color:#9999FF;'> opposition research </span> against  <span class=span1 id=1540 style='background-color:#F1BBFF;'> Hillary Clinton </span> through  <span class=span1 id=1541 style='background-color:#C0C0C0;'> a June 2016 meeting </span> with  <span class=span1 id=1542 style='background-color:#EAB9B9;'> Russian lawyer Natalia Veselnitskaya </span> "

In [176]:
event_df.loc[4820,'eventsummary']=" <span class=span1 id=1543 style='background-color:#FFB19D;'> Scientists </span> at  <span class=span1 id=1544 style='background-color:#DBD0CC;'> the Chinese Academy </span> of  <span class=span1 id=1545 style='background-color:#FFDAB9;'> Sciences </span> successfully teleport  <span class=span1 id=1546 style='background-color:#fabebe;'> a photon </span> from  <span class=span1 id=1547 style='background-color:#FFCC99;'> a ground station </span> in  <span class=span1 id=1548 style='background-color:#A5C1E5;'> Tibet </span> to  <span class=span1 id=1549 style='background-color:#A0CAFF;'> a satellite </span> orbiting  <span class=span1 id=1550 style='background-color:#ADADEB;'> Earth </span> at  <span class=span1 id=1551 style='background-color:#9999FF;'> distance </span> of  <span class=span1 id=1552 style='background-color:#F1BBFF;'> 500 km </span> away .  <span class=span1 id=1553 style='background-color:#C0C0C0;'> It </span> is  <span class=span1 id=1554 style='background-color:#EAB9B9;'> the first time </span>  <span class=span1 id=1555 style='background-color:#FFB19D;'> an object </span> has been teleported from  <span class=span1 id=1556 style='background-color:#DBD0CC;'> the planet </span> into  <span class=span1 id=1557 style='background-color:#FFDAB9;'> space </span> "

In [177]:
event_df.loc[4842,'eventsummary']=" <span class=span1 id=1658 style='background-color:#fabebe;'> An attack </span> by  <span class=span1 id=1659 style='background-color:#FFCC99;'> a man </span> armed with  <span class=span1 id=1660 style='background-color:#A5C1E5;'> a knife </span> in  <span class=span1 id=1661 style='background-color:#A0CAFF;'> Tehran Metros ShahreRey Station </span> leaves  <span class=span1 id=1662 style='background-color:#ADADEB;'> two </span> injured .  <span class=span1 id=1663 style='background-color:#9999FF;'> The attacker </span> is shot dead by  <span class=span1 id=1664 style='background-color:#F1BBFF;'> the police </span> "

In [178]:
event_df.loc[1892,'event_summary']='Turkish Foreign Minister Mevlut Cavusoglu says Turkeys cooperation with Russia in combating Islamic State in Syria does not include Russias use of its Incirlik Air Base'

In [179]:
event_df.loc[332,'event_summary']='Turkish President Recep Tayyip Erdogan blasts United States over its support for Syrian Kurdish groups which Turkey considers to be terrorists'

In [181]:
import re
for i in range(0,100):
    out=event_df.loc[i,'eventsummary']
#     my_string=event_df.loc[i,"event_summary"]
#     splitdata=data.split()

    word ='.'
    if word in out:
        print(i)
#         mystring=my_string.str.replace('n.','n')
        out=out.replace('a.','a .')
        out=out.replace('b.','b .')
        out=out.replace('c.','c .')
        out=out.replace('d.','d .')
        out=out.replace('e.','e .')
        out=out.replace('f.','f .')
        out=out.replace('g.','g .')
        out=out.replace('h.','h .')
        out=out.replace('i.','i .')
        out=out.replace('j.','j .')
        out=out.replace('k.','k .')
        out=out.replace('l.','l .')
        out=out.replace('m.','m .')
        out=out.replace('n.','n .')
        out=out.replace('o.','o .')
        out=out.replace('p.','p .')
        out=out.replace('q.','q .')
        out=out.replace('r.','r .')
        out=out.replace('s.','s .')
        out=out.replace('t.','t .')
        out=out.replace('u.','u .')
        out=out.replace('v.','v .')
        out=out.replace('w.','w .')
        out=out.replace('x.','x .')
        out=out.replace('y.','y .')
        out=out.replace('z.','z .')
        event_df.loc[i,'eventsummary']=out
        print(out)



       

    
# (re_word, my_string)

6
 <span class=span1 id=28 style='background-color:#F1BBFF;'> The United Kingdom </span> designates  <span class=span1 id=29 style='background-color:#C0C0C0;'> Ascension Island </span> and  <span class=span1 id=30 style='background-color:#EAB9B9;'> its surrounding waters </span> in  <span class=span1 id=31 style='background-color:#FFB19D;'> Atlantic Ocean </span> as  <span class=span1 id=32 style='background-color:#DBD0CC;'> a Marine </span> protected  <span class=span1 id=33 style='background-color:#FFDAB9;'> area </span>.  <span class=span1 id=34 style='background-color:#fabebe;'> The reserve </span> will be almost as big as  <span class=span1 id=35 style='background-color:#FFCC99;'> UK </span> with just over  <span class=span1 id=36 style='background-color:#A5C1E5;'> half </span> of  <span class=span1 id=37 style='background-color:#A0CAFF;'> protected area </span> completely closed to  <span class=span1 id=38 style='background-color:#ADADEB;'> fishing </span> 
11
 <span class=span1 

### 8. Converting each word to button

In [182]:
pd.options.display.float_format = '{:,.0f}'.format

In [183]:
df_button=pd.DataFrame()

In [184]:
j=0
for i in range(0,100):
    text=event_df.loc[i,'event_summary']
    print(i)
    words = text.split()
    for word in words:
        df_button.loc[j,'event_id']=event_df.loc[i,'event_id']
        df_button.loc[j,'id']=j
        df_button.loc[j,'Button']=word
        df_button.loc[j,'pos'] = text.find(df_button.loc[j,'Button'])
        
        j=j+1
#         print(word)

        # print the word
        

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99


In [185]:
df_button

event_id    id    Button  pos
0    0         0      A        0   
1    0         1      shooting 2   
2    0         2      takes    11  
3    0         3      place    17  
4    0         4      at       23  
...  ..        ..     ..       ..  
1716 99        1,716  Alan     6   
1717 99        1,717  Rickman  11  
1718 99        1,718  dies     19  
1719 99        1,719  from     24  
1720 99        1,720  cancer   29  

[1721 rows x 4 columns]

In [186]:
import re
for i in range(0,1721):
    out=df_button.loc[i,'Button']
#     my_string=event_df.loc[i,"event_summary"]
#     splitdata=data.split()

    word ='.'
    if word in out:
        print(i)
#         mystring=my_string.str.replace('n.','n')
        out=out.replace('a.','a')
        out=out.replace('b.','b')
        out=out.replace('c.','c')
        out=out.replace('d.','d')
        out=out.replace('e.','e')
        out=out.replace('f.','f')
        out=out.replace('g.','g')
        out=out.replace('h.','h')
        out=out.replace('i.','i')
        out=out.replace('j.','j')
        out=out.replace('k.','k')
        out=out.replace('l.','l')
        out=out.replace('m.','m')
        out=out.replace('n.','n')
        out=out.replace('o.','o')
        out=out.replace('p.','p')
        out=out.replace('q.','q')
        out=out.replace('r.','r')
        out=out.replace('s.','s')
        out=out.replace('t.','t')
        out=out.replace('u.','u')
        out=out.replace('v.','v')
        out=out.replace('w.','w')
        out=out.replace('x.','x')
        out=out.replace('y.','y')
        out=out.replace('z.','z')
        df_button.loc[i,'Button']=out
        print(out)



       

    
# (re_word, my_string)

103
area
222
Kingdom
286
6.85
289
8.1
303
6.7
435
W.
660
5.1
1146
Sgt
1334
Ocean
1431
St
1488
Zone
1586
Alps
1677
Jakarta


In [187]:
df_button

event_id    id    Button  pos
0    0         0      A        0   
1    0         1      shooting 2   
2    0         2      takes    11  
3    0         3      place    17  
4    0         4      at       23  
...  ..        ..     ..       ..  
1716 99        1,716  Alan     6   
1717 99        1,717  Rickman  11  
1718 99        1,718  dies     19  
1719 99        1,719  from     24  
1720 99        1,720  cancer   29  

[1721 rows x 4 columns]

In [188]:
# pd.options.display.float_format = '{:,.0f}'.format
m=0
pp=0
abc=[]
span=[]
import re
for i in range(0,100):
    string=event_df.loc[i,'eventsummary']
    iid=event_df.loc[i,'event_id']
#     print(df.loc[i,"event_summary"])
#     print(string)
#     print("ID"+str(iid))
    k=0
    for j in range (0,1721):
        if df_button.loc[j,'event_id']==event_df.loc[i,'event_id']:
#             print(Args_df.loc[j,'event_id'])
#             print(Args_df.loc[j,'argtext'])
#             print(event_df.loc[i,'event_id'])
#             print(Args_df.loc[j,'event_summary'])
            k=k+1
#     print("................................")
#     print(k) 
#     print("................................")

        
#     print(k)  
#     print(string)
    n=m+k
#     print(m)
#     print(n)
#     if Args_df.loc[j,'event_id']==event_df.loc[i,'event_id']:
    for x in range(m,n):
        
        
        if df_button.loc[x,'Button'] in string :
            search_str=df_button.loc[x,'Button']
#             print(search_str)
#             regex=re.compile('[(a-zA-Z)|^span]')
#             span1=re.search(r"[^(span|back|layout|display|margin|border-radius|:au|#|DAB)]("+df_button.loc[x,'Button']+")[^span]", string)
#             if re.match(r"^([a-z])([0-9]+)([A-Z])", search_str):
            list1=["About","In","Protest","Based","FBI","Jailed","US","Head","Fracking","Justify","Outside","Using","Kenyan","Iowa","TMobile","Updated","Ambassador","Failed","More","For","North","Farright","Without","Presenting","Previously","Reacting","JaisheMohammed","Retired","Refuse","Among","Coinciding","earlier","Italian","Both","abdicate","Rightwing","dead","Chinese","Government","Shortly","With","Campaigning","Because","Marking","Government","Germany","When","An","Citing","Shelling","Armed","ProBeijing","Amidst","Recounts","Despite","Will","As","Fires","Houthi","Before","Illegally","British","From","On","Suspect","Per","Over","Record","Imprisoned","Three","According","Amid","German","Around","While","Atleast","At","The","During","Search","Following","Counting","Syrian","After","Argentinas","Saudiled","A","Iraqi","Defending","Due","Hedge","Former","Under"]
            if search_str in list1:
                span1=re.search(r"("+df_button.loc[x,'Button']+")[^a-zA-Za.-z.A.-Z.]", string)
                span=span1.span()
                pos=span[0]
                epos=span[1]
#             elif re.match(r"\s(\w+)$", search_str):  
#                 span1=re.search(r"\s(\w+)$"+(df_button.loc[x,'Button'])+"[^a-zA-Z]", string)

            else:
#                 myex = re.compile(r"(@|span)")
                span1=re.search(r"[^(?<=a-zA-Z|span|EAB|#A5|input|type|style='|1|<span)]"+(df_button.loc[x,'Button'])+"[^a-zA-Za.-z.A.-Z.]", string)
            
            
                span=span1.span()
#             print(span)
                pos=span[0]
                epos=span[1]
                pos=pos+1
                epos=epos-1
#             print(span1)
#             print(type(df_button.loc[x,'id']))
            string=string[:pos]+"<input class=mydiv id="+str(int(df_button.loc[x,'pos']))+" type='button' value="+df_button.loc[x,'Button']+">"+string[epos:]
        else:
            print("hi")
            print(df_button.loc[x,'Button'])
            print(event_df.loc[i,'event_id'])
#     print(string+"\n")
    event_df.loc[i,'eventsummary2']=string
#     print(event_df.loc[i,'eventsummary2'])
   
    m=x+1


In [189]:
event_df

event_id        date                     category  \
0     0         2016-01-01  Armed conflicts and attacks   
1     1         2016-01-01  Disasters and Incidents       
2     2         2016-01-01  International Relations       
3     3         2016-01-01  Crime and Law                 
4     4         2016-01-03  Armed conflicts and attacks   
...  ..                ...                          ...   
9840  9840      2019-04-29  Disasters and Incidents       
9841  9841      2019-04-29  Politics and Elections        
9842  9842      2019-04-29  Politics and Elections        
9843  9843      2019-04-30  Arts and culture              
9844  9844      2019-04-30  Business and Economy          

                            event_title  \
0     IsraeliE28093Palestinian conflict   
1     FALSE                               
2     FALSE                               
3     FALSE                               
4     Iraqi Civil War 2014E280932017      
...                              ...      
9840  FALSE                               
9841  FALSE                               
9842  FALSE                               
9843  2019 Japanese imperial transition   
9844  FALSE                               

                                                                                                                                                                                                            event_summary  \
0     A shooting takes place at a pub in Tel Aviv                                                                                                                                                                           
1     About one thousand houses in Manilas Tondo district in Philippines are set ablaze following New Years Eve firecracker festivities that left two dead and 380 others injured                                           
2     The EUUkraine Free Trade deal officially comes into force                                                                                                                                                             
3     The twochild policy takes effect in China                                                                                                                                                                             
4     The Islamic State of Iraq and Levant claims responsibility for a suicide bomb attack on a Iraqi Army base Camp Speicher                                                                                               
...                                                                                                                       ...                                                                                               
9840  A minibus carrying Turkish Süper Lig Alanyaspor football players crashes near Alanya                                                                                                                                  
9841  Indonesian President Joko Widodo has decided to relocate the nations capital from Jakarta                                                                                                                             
9842  U.S. Deputy Attorney General Rod Rosenstein announces he will resign                                                                                                                                                  
9843  Emperor Akihito abdicates the Chrysanthemum Throne in favor of his elder son                                                                                                                                          
9844  U.S. Attorney General William Barr has decided to recuse himself from deliberations about whether the Antitrust Division of the U.S. Justice Department ought to challenge the planned merger of TMobile and Sprint   

                                                                                                                               

In [190]:
edf=event_df

In [191]:
edf=edf[:100]
edf=edf[['event_id','eventsummary2']]

In [192]:
event_df

event_id        date                     category  \
0     0         2016-01-01  Armed conflicts and attacks   
1     1         2016-01-01  Disasters and Incidents       
2     2         2016-01-01  International Relations       
3     3         2016-01-01  Crime and Law                 
4     4         2016-01-03  Armed conflicts and attacks   
...  ..                ...                          ...   
9840  9840      2019-04-29  Disasters and Incidents       
9841  9841      2019-04-29  Politics and Elections        
9842  9842      2019-04-29  Politics and Elections        
9843  9843      2019-04-30  Arts and culture              
9844  9844      2019-04-30  Business and Economy          

                            event_title  \
0     IsraeliE28093Palestinian conflict   
1     FALSE                               
2     FALSE                               
3     FALSE                               
4     Iraqi Civil War 2014E280932017      
...                              ...      
9840  FALSE                               
9841  FALSE                               
9842  FALSE                               
9843  2019 Japanese imperial transition   
9844  FALSE                               

                                                                                                                                                                                                            event_summary  \
0     A shooting takes place at a pub in Tel Aviv                                                                                                                                                                           
1     About one thousand houses in Manilas Tondo district in Philippines are set ablaze following New Years Eve firecracker festivities that left two dead and 380 others injured                                           
2     The EUUkraine Free Trade deal officially comes into force                                                                                                                                                             
3     The twochild policy takes effect in China                                                                                                                                                                             
4     The Islamic State of Iraq and Levant claims responsibility for a suicide bomb attack on a Iraqi Army base Camp Speicher                                                                                               
...                                                                                                                       ...                                                                                               
9840  A minibus carrying Turkish Süper Lig Alanyaspor football players crashes near Alanya                                                                                                                                  
9841  Indonesian President Joko Widodo has decided to relocate the nations capital from Jakarta                                                                                                                             
9842  U.S. Deputy Attorney General Rod Rosenstein announces he will resign                                                                                                                                                  
9843  Emperor Akihito abdicates the Chrysanthemum Throne in favor of his elder son                                                                                                                                          
9844  U.S. Attorney General William Barr has decided to recuse himself from deliberations about whether the Antitrust Division of the U.S. Justice Department ought to challenge the planned merger of TMobile and Sprint   

                                                                                                                               

### 9. Convert all df into csv so we could import them in mysql

In [193]:
edf.to_csv(r'C:\Users\gulja\Python 3.7.3\Scripts\thesis\Event Extraction CSV files\events.csv', index=False, header=False,sep=',',encoding='utf-8') 
Args_df.to_csv(r'C:\Users\gulja\Python 3.7.3\Scripts\thesis\Event Extraction CSV files\events_args.csv', index=False,  header=False,encoding='utf-8') 
anno_df.to_csv(r'C:\Users\gulja\Python 3.7.3\Scripts\thesis\Event Extraction CSV files\events_annotation.csv', index=False, header=False,encoding='utf-8')
# Relationphrase_df.to_csv(r'C:\Users\gulja\Python 3.7.3\Scripts\thesis\Event Extraction CSV files\events_annotation.csv', index=False, header=False,encoding='utf-8')

In [1144]:
edf.loc[9469,'eventsummary2']=" <span class=span1 id=48276 style='background-color:#F1BBFF;'> <input class=mydiv id=0 type='button' value=Japanese> <input class=mydiv id=9 type='button' value=Prime> <input class=mydiv id=15 type='button' value=Minister> <input class=mydiv id=24 type='button' value=Shinzo> <input class=mydiv id=31 type='button' value=Abe> </span> <input class=mydiv id=35 type='button' value=says> <span class=span1 id=48277 style='background-color:#C0C0C0;'> <input class=mydiv id=40 type='button' value=relocation> </span> <input class=mydiv id=51 type='button' value=of> <span class=span1 id=48278 style='background-color:#EAB9B9;'> <input class=mydiv id=54 type='button' value=Marine> <input class=mydiv id=61 type='button' value=Corps> <input class=mydiv id=67 type='button' value=Air> <input class=mydiv id=71 type='button' value=Station> <input class=mydiv id=79 type='button' value=Futenma> </span> "

In [ ]:
event_df.loc[2905,'event_summary']='A fire at a karaoke bar in Hanois Cau Giay district kills 13 people'
event_df.loc[3269,'event_summary']='The death toll from bombings in Besiktas'
event_df.loc[3451,'event_summary']='A shootout in Izmir kills two gunmen while anor one escapes'
event_df.loc[3954,'event_summary']='Dutch authorities withdrew landing permission for a plane carrying Turkish Foreign Minister Mevlut Cavusoglu'
event_df.loc[4495,'event_summary']='North Korea launches a ShortRange Ballistic missile near Wonsan towards Sea of Japan'
event_df.loc[5507,'event_summary']='The UluruKata Tjuta National Parks board votes unanimously to ban climbing on Uluru'
event_df.loc[5712,'event_summary']='Peoples Democratic Partys cochair Selahattin Demirtas remains behind bars until next hearing'
event_df.loc[5933,'event_summary']='German foreign minister Sigmar Gabriel and his Turkish colleague Mevlut Cavusoglu agree to improve relations between ir countries'
event_df.loc[6015,'event_summary']='Malaysia upholds death sentences for nine Filipino Tausugs over 2013 incursion in Sabah by a faction of claimant to Sultanate of Sulu throne'
event_df.loc[6051,'event_summary']='A bus crash in Turkeys northwestern Eskisehir Province kills at least 11 people and injures 46 ors'
event_df.loc[6058,'event_summary']='Turkish President Erdogan announces that Turkish Army ground troops have entered district of Afrin in Syria . Turkish Prime Minister Binali Yildirim says goal is to establish a 30 km safe zone'
event_df.loc[6128,'event_summary']='Swiss tennis player Roger Federer successfully defends his title in fivesets mens singles final against Marin Cilic'
event_df.loc[6224,'event_summary']='An overnight fire destroys parts of Haitis historic Marche en Fer Iron Market in Port Prince. It is unclear what started fire'
event_df.loc[6274,'event_summary']='Latvia will ask European Central Bank not to renew mandate of ECB Governing Council member Ilmoars Rimsevics'
event_df.loc[6629,'event_summary']='Polish environment minister Henryk Kowalczyk says Poland alone should decide fate of protected Bialowieza Forest'
event_df.loc[6775,'event_summary']='The parents of Ayse Deniz Karacagil who died in Iraq Raqqa after joining the outlawed Kurdistan Workers Party'
event_df.loc[6876,'event_summary']='A double decker tourist bus collides with lowlying tree branches in Zurrieq'
event_df.loc[7046,'event_summary']='The European Commission rules Polands logging operations in Bialowieza Forest'
event_df.loc[7071,'event_summary']='The US Geological Surveys Hawaiian Volcano Observatory states that Kilauea is showing unusually high activity and that a new vent could form'
event_df.loc[7343,'event_summary']='Hawaiian volcano Kilauea begins erupting at Leilani Estates subdivision'
event_df.loc[7353,'event_summary']='An earthquake strikes a coal mine near JastrzebieZdroj'
event_df.loc[7375,'event_summary']='About 35 structures in Leilani Estates are destroyed during Kilauea eruption in Hawaii'
event_df.loc[7465,'event_summary']='The summit at Kilauea erupts and sends a plume of ash and smoke 30'
event_df.loc[7521,'event_summary']='A magnitude 4.4 earthquake occurs at Kilauea'
event_df.loc[7529,'event_summary']='Several more properties are destroyed as Kilauea continues to erupt'
event_df.loc[7663,'event_summary']='Hawaiian Airlines warns that eruption of Kilauea may hurt bookings and trim revenues'
event_df.loc[7924,'event_summary']='23 passengers on a tour boat in Hawaii are injured after a lava bomb from Kilauea volcano punctures roof of vessel'
event_df.loc[8200,'event_summary']='Footage from US Geological Survey shows lava activity at Kilauea slowing down'
event_df.loc[8449,'event_summary']='Vietnamese President Tran Dai Quang dies at age of 61 following an extended illness. Vice President Dang Thi Ngoc Thinh succeeds as acting President'
event_df.loc[8457,'event_summary']='Hawai Volcanoes National Park reopens after 134 days of closure due to volcanic activity at Kilauea that damaged park infrastructure'
event_df.loc[8471,'event_summary']='Dunkin Donuts announces it will drop Donuts part of its name and be simply known as dunkin beginning in January 2019'
event_df.loc[8710,'event_summary']='The Turkish chief Istanbul prosecutor Irfan Fidans office states that Jamal Khashoggi was'
event_df.loc[8993,'event_summary']='A highspeed train crashes at Marsandiz railway station in Ankara'
event_df.loc[9469,'event_summary']='Japanese Prime Minister Shinzo Abe says relocation of Marine Corps Air Station Futenma'


